# Define Library

In [1]:
# %% [markdown]
# # Jupyter Notebook Loading Header
#
# This is a custom loading header for Jupyter Notebooks in Visual Studio Code.
# It includes common imports and settings to get you started quickly.
# %% [markdown]
## Import Libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from google.cloud import bigquery
from google.cloud import storage
import os
import tempfile
import time
from datetime import datetime
import uuid
import joblib
import uuid
from sklearn.metrics import roc_auc_score
from datetime import datetime, timedelta
import gcsfs
import duckdb as dd
import pickle
import joblib
from typing import Union
import io
path = r'C:\Users\Dwaipayan\AppData\Roaming\gcloud\legacy_credentials\dchakroborti@tonikbank.com\adc.json'
os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = path
client = bigquery.Client(project='prj-prod-dataplatform')
os.environ["GOOGLE_CLOUD_PROJECT"] = "prj-prod-dataplatform"

# %% [markdown]
## Configure Settings
# Set options or configurations as needed
pd.set_option('display.max_columns', None)
pd.set_option("Display.max_rows", 100)

# Function

## calculate_gini

In [2]:
def calculate_gini(pd_scores, bad_indicators):
    """
    Calculate Gini coefficient from scores and binary indicators
    
    Parameters:
    pd_scores: array-like of scores/probabilities
    bad_indicators: array-like of binary outcomes (0/1)
    
    Returns:
    float: Gini coefficient
    """
    # Convert inputs to numpy arrays and ensure they're numeric
    pd_scores = np.array(pd_scores, dtype=float)
    bad_indicators = np.array(bad_indicators, dtype=int)
    
    # Check for valid input data
    if len(pd_scores) == 0 or len(bad_indicators) == 0:
        return np.nan
    
    # Check if we have both good and bad cases (needed for ROC AUC)
    if len(np.unique(bad_indicators)) < 2:
        return np.nan
    
    # Calculate AUC using sklearn
    try:
        auc = roc_auc_score(bad_indicators, pd_scores)
        # Calculate Gini from AUC
        gini = 2 * auc - 1
        return gini
    except ValueError:
        return np.nan

## calculate_periodic_gini_prod_ver_trench

In [3]:
def calculate_periodic_gini_prod_ver_trench(df, score_column, label_column, namecolumn, 
                                        model_version_column=None, trench_column=None, 
                                        loan_type_column=None, loan_product_type_column=None):
    """
    Calculate periodic Gini coefficients at multiple levels:
    - Overall
    - By model version
    - By all combinations of model version, trench category, loan type, and loan product type
    
    Parameters:
    df: DataFrame with disbursement dates and score/label columns
    score_column: name of the score column
    label_column: name of the label column
    namecolumn: name for the bad rate label
    model_version_column: (optional) name of column for model version (e.g., 'modelVersionId')
    trench_column: (optional) name of column for trench category (e.g., 'trenchCategory')
    loan_type_column: (optional) name of loan type column (e.g., 'loan_type')
    loan_product_type_column: (optional) name of loan product type column (e.g., 'loan_product_type')
    """
    # Input validation
    required_columns = ['disbursementdate', score_column, label_column]
    if not all(col in df.columns for col in required_columns):
        raise ValueError(f"Missing required columns. Need: {required_columns}")
    
    optional_columns = {
        'model_version': model_version_column,
        'trench': trench_column,
        'loan_type': loan_type_column,
        'loan_product_type': loan_product_type_column
    }
    
    for col_name, col in optional_columns.items():
        if col and col not in df.columns:
            raise ValueError(f"{col_name.replace('_', ' ').title()} column '{col}' not found in dataframe")
    
    # Create a copy to avoid modifying original dataframe
    df = df.copy()
    
    # Ensure date is datetime type
    df['disbursementdate'] = pd.to_datetime(df['disbursementdate'])
    
    # Ensure score and label columns are numeric
    df[score_column] = pd.to_numeric(df[score_column], errors='coerce')
    df[label_column] = pd.to_numeric(df[label_column], errors='coerce')
    
    # Drop rows with invalid values
    df = df.dropna(subset=[score_column, label_column])
    
    # Define list of datasets to process
    datasets_to_process = [('Overall', df, {})]
    
    # Add model version level segmentation
    if model_version_column:
        for model_version in sorted(df[model_version_column].dropna().unique()):
            model_df = df[df[model_version_column] == model_version]
            metadata = {model_version_column: model_version}
            datasets_to_process.append((f'ModelVersion_{model_version}', model_df, metadata))
    
    # Add all combinations of model_version, trench, loan_type, loan_product_type
    segment_columns = []
    if model_version_column:
        segment_columns.append(('ModelVersion', model_version_column))
    if trench_column:
        segment_columns.append(('Trench', trench_column))
    if loan_type_column:
        segment_columns.append(('LoanType', loan_type_column))
    if loan_product_type_column:
        segment_columns.append(('ProductType', loan_product_type_column))
    
    # Generate all combinations (only if we have multiple segment columns)
    if len(segment_columns) > 1:
        # Create combinations by iterating through all segment dimensions
        def generate_combinations(df, segment_columns, index=0, current_filter=None, current_name=''):
            if current_filter is None:
                current_filter = {}
            
            if index >= len(segment_columns):
                # Apply all filters and create segment
                filtered_df = df
                for col, val in current_filter.items():
                    filtered_df = filtered_df[filtered_df[col] == val]
                
                if len(filtered_df) > 0:
                    yield (current_name.strip('_'), filtered_df, current_filter.copy())
                return
            
            seg_name, seg_col = segment_columns[index]
            for seg_value in sorted(df[seg_col].dropna().unique()):
                new_filter = current_filter.copy()
                new_filter[seg_col] = seg_value
                new_name = current_name + f'{seg_name}_{seg_value}_'
                
                yield from generate_combinations(df, segment_columns, index + 1, new_filter, new_name)
        
        for combo_name, combo_df, combo_metadata in generate_combinations(df, segment_columns):
            datasets_to_process.append((combo_name, combo_df, combo_metadata))
    
    all_results = []
    
    # Process each dataset
    for dataset_name, dataset_df, metadata in datasets_to_process:
        # Calculate weekly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['week'] = dataset_df_copy['disbursementdate'].dt.to_period('W')
        weekly_gini = dataset_df_copy.groupby('week').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 10 else np.nan
        ).reset_index(name='gini')
        weekly_gini['period'] = 'Week'
        weekly_gini['start_date'] = weekly_gini['week'].apply(lambda x: x.to_timestamp())
        weekly_gini['end_date'] = weekly_gini['start_date'] + timedelta(days=6)
        weekly_gini = weekly_gini[['start_date', 'end_date', 'gini', 'period']]
        
        # Calculate monthly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['month'] = dataset_df_copy['disbursementdate'].dt.to_period('M')
        monthly_gini = dataset_df_copy.groupby('month').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 20 else np.nan
        ).reset_index(name='gini')
        monthly_gini['period'] = 'Month'
        monthly_gini['start_date'] = monthly_gini['month'].apply(lambda x: x.to_timestamp())
        monthly_gini['end_date'] = monthly_gini['start_date'] + pd.DateOffset(months=1) - pd.Timedelta(days=1)
        monthly_gini = monthly_gini[['start_date', 'end_date', 'gini', 'period']]
        
        # Combine results for this dataset
        gini_results = pd.concat([weekly_gini, monthly_gini], ignore_index=True)
        gini_results = gini_results.sort_values(by='start_date').reset_index(drop=True)
        
        # Add metadata columns
        gini_results['Model_Name'] = score_column
        gini_results['bad_rate'] = namecolumn
        gini_results['segment_type'] = dataset_name
        
        # Add individual segment components
        if model_version_column and model_version_column in metadata:
            gini_results['model_version'] = metadata[model_version_column]
        else:
            gini_results['model_version'] = None
        
        if trench_column and trench_column in metadata:
            gini_results['trench_category'] = metadata[trench_column]
        else:
            gini_results['trench_category'] = None
        
        if loan_type_column and loan_type_column in metadata:
            gini_results['loan_type'] = metadata[loan_type_column]
        else:
            gini_results['loan_type'] = None
        
        if loan_product_type_column and loan_product_type_column in metadata:
            gini_results['loan_product_type'] = metadata[loan_product_type_column]
        else:
            gini_results['loan_product_type'] = None
        
        gini_results.rename(columns={'gini': f'{score_column}_{namecolumn}_gini'}, inplace=True)
        
        all_results.append(gini_results)
    
    # Combine all results
    final_results = pd.concat(all_results, ignore_index=True)
    
    return final_results


# Usage:
# gini_results = calculate_periodic_gini_prod_ver_trench(
#     df_concat, 
#     'Alpha_cic_sil_score', 
#     'deffpd0', 
#     'FPD0',
#     model_version_column='modelVersionId',
#     trench_column='trenchCategory',
#     loan_type_column='loan_type',
#     loan_product_type_column='loan_product_type'
# )

In [4]:
# def calculate_periodic_gini_prod_ver_trench_md(df, score_column, label_column, namecolumn, 
#                                         model_version_column=None, trench_column=None, 
#                                         loan_type_column=None, loan_product_type_column=None,
#                                         account_id_column=None):
#     """
#     Calculate periodic Gini coefficients at multiple levels:
#     - Overall
#     - By model version
#     - By all combinations of model version, trench category, loan type, and loan product type
    
#     Parameters:
#     df: DataFrame with disbursement dates and score/label columns
#     score_column: name of the score column
#     label_column: name of the label column
#     namecolumn: name for the bad rate label
#     model_version_column: (optional) name of column for model version (e.g., 'modelVersionId')
#     trench_column: (optional) name of column for trench category (e.g., 'trenchCategory')
#     loan_type_column: (optional) name of loan type column (e.g., 'loan_type')
#     loan_product_type_column: (optional) name of loan product type column (e.g., 'loan_product_type')
#     account_id_column: (optional) name of column for distinct account IDs (e.g., 'digitalLoanAccountId')
#     """
#     # Input validation
#     required_columns = ['disbursementdate', score_column, label_column]
#     if not all(col in df.columns for col in required_columns):
#         raise ValueError(f"Missing required columns. Need: {required_columns}")
    
#     optional_columns = {
#         'model_version': model_version_column,
#         'trench': trench_column,
#         'loan_type': loan_type_column,
#         'loan_product_type': loan_product_type_column,
#         'account_id': account_id_column
#     }
    
#     for col_name, col in optional_columns.items():
#         if col and col not in df.columns:
#             raise ValueError(f"{col_name.replace('_', ' ').title()} column '{col}' not found in dataframe")
    
#     # Create a copy to avoid modifying original dataframe
#     df = df.copy()
    
#     # Ensure date is datetime type
#     df['disbursementdate'] = pd.to_datetime(df['disbursementdate'])
    
#     # Ensure score and label columns are numeric
#     df[score_column] = pd.to_numeric(df[score_column], errors='coerce')
#     df[label_column] = pd.to_numeric(df[label_column], errors='coerce')
    
#     # Drop rows with invalid values
#     df = df.dropna(subset=[score_column, label_column])
    
#     # Define list of datasets to process
#     datasets_to_process = [('Overall', df, {})]
    
#     # Add model version level segmentation
#     if model_version_column:
#         for model_version in sorted(df[model_version_column].dropna().unique()):
#             model_df = df[df[model_version_column] == model_version]
#             metadata = {model_version_column: model_version}
#             datasets_to_process.append((f'ModelVersion_{model_version}', model_df, metadata))
    
#     # Add all combinations of model_version, trench, loan_type, loan_product_type
#     segment_columns = []
#     if model_version_column:
#         segment_columns.append(('ModelVersion', model_version_column))
#     if trench_column:
#         segment_columns.append(('Trench', trench_column))
#     if loan_type_column:
#         segment_columns.append(('LoanType', loan_type_column))
#     if loan_product_type_column:
#         segment_columns.append(('ProductType', loan_product_type_column))
    
#     # Generate all combinations (only if we have multiple segment columns)
#     if len(segment_columns) > 1:
#         # Create combinations by iterating through all segment dimensions
#         def generate_combinations(df, segment_columns, index=0, current_filter=None, current_name=''):
#             if current_filter is None:
#                 current_filter = {}
            
#             if index >= len(segment_columns):
#                 # Apply all filters and create segment
#                 filtered_df = df
#                 for col, val in current_filter.items():
#                     filtered_df = filtered_df[filtered_df[col] == val]
                
#                 if len(filtered_df) > 0:
#                     yield (current_name.strip('_'), filtered_df, current_filter.copy())
#                 return
            
#             seg_name, seg_col = segment_columns[index]
#             for seg_value in sorted(df[seg_col].dropna().unique()):
#                 new_filter = current_filter.copy()
#                 new_filter[seg_col] = seg_value
#                 new_name = current_name + f'{seg_name}_{seg_value}_'
                
#                 yield from generate_combinations(df, segment_columns, index + 1, new_filter, new_name)
        
#         for combo_name, combo_df, combo_metadata in generate_combinations(df, segment_columns):
#             datasets_to_process.append((combo_name, combo_df, combo_metadata))
    
#     all_results = []
    
#     # Process each dataset
#     for dataset_name, dataset_df, metadata in datasets_to_process:
#         # Calculate weekly Gini
#         dataset_df_copy = dataset_df.copy()
#         dataset_df_copy['week'] = dataset_df_copy['disbursementdate'].dt.to_period('W')
#         weekly_gini = dataset_df_copy.groupby('week').apply(
#             lambda x: calculate_gini(x[score_column], x[label_column])
#             if len(x) >= 10 else np.nan
#         ).reset_index(name='gini')
#         weekly_gini['period'] = 'Week'
#         weekly_gini['start_date'] = weekly_gini['week'].apply(lambda x: x.to_timestamp())
#         weekly_gini['end_date'] = weekly_gini['start_date'] + timedelta(days=6)
        
#         # Add distinct account count for weekly
#         if account_id_column:
#             weekly_gini['distinct_accounts'] = dataset_df_copy.groupby('week')[account_id_column].nunique().values
        
#         weekly_gini = weekly_gini[['start_date', 'end_date', 'gini', 'period']]
        
#         # Calculate monthly Gini
#         dataset_df_copy = dataset_df.copy()
#         dataset_df_copy['month'] = dataset_df_copy['disbursementdate'].dt.to_period('M')
#         monthly_gini = dataset_df_copy.groupby('month').apply(
#             lambda x: calculate_gini(x[score_column], x[label_column])
#             if len(x) >= 20 else np.nan
#         ).reset_index(name='gini')
#         monthly_gini['period'] = 'Month'
#         monthly_gini['start_date'] = monthly_gini['month'].apply(lambda x: x.to_timestamp())
#         monthly_gini['end_date'] = monthly_gini['start_date'] + pd.DateOffset(months=1) - pd.Timedelta(days=1)
        
#         # Add distinct account count for monthly
#         if account_id_column:
#             monthly_gini['distinct_accounts'] = dataset_df_copy.groupby('month')[account_id_column].nunique().values
        
#         monthly_gini = monthly_gini[['start_date', 'end_date', 'gini', 'period']]
        
#         # Combine results for this dataset
#         gini_results = pd.concat([weekly_gini, monthly_gini], ignore_index=True)
#         gini_results = gini_results.sort_values(by='start_date').reset_index(drop=True)
        
#         # Add metadata columns
#         gini_results['Model_Name'] = score_column
#         gini_results['bad_rate'] = namecolumn
#         gini_results['segment_type'] = dataset_name
        
#         # Add individual segment components
#         if model_version_column and model_version_column in metadata:
#             gini_results['model_version'] = metadata[model_version_column]
#         else:
#             gini_results['model_version'] = None
        
#         if trench_column and trench_column in metadata:
#             gini_results['trench_category'] = metadata[trench_column]
#         else:
#             gini_results['trench_category'] = None
        
#         if loan_type_column and loan_type_column in metadata:
#             gini_results['loan_type'] = metadata[loan_type_column]
#         else:
#             gini_results['loan_type'] = None
        
#         if loan_product_type_column and loan_product_type_column in metadata:
#             gini_results['loan_product_type'] = metadata[loan_product_type_column]
#         else:
#             gini_results['loan_product_type'] = None
        
#         gini_results.rename(columns={'gini': f'{score_column}_{namecolumn}_gini'}, inplace=True)
        
#         all_results.append(gini_results)
    
#     # Combine all results
#     final_results = pd.concat(all_results, ignore_index=True)
    
#     return final_results


# # Usage:
# # gini_results = calculate_periodic_gini_prod_ver_trench(
# #     df_concat, 
# #     'Alpha_cic_sil_score', 
# #     'deffpd0', 
# #     'FPD0',
# #     model_version_column='modelVersionId',
# #     trench_column='trenchCategory',
# #     loan_type_column='loan_type',
# #     loan_product_type_column='loan_product_type',
# #     account_id_column='digitalLoanAccountId'
# # )

In [5]:
import pandas as pd
import numpy as np
from datetime import timedelta
from itertools import combinations

def calculate_gini(scores, labels):
    """Calculate Gini coefficient"""
    n = len(scores)
    if n < 2:
        return np.nan
    
    sorted_indices = np.argsort(scores)
    sorted_labels = labels.iloc[sorted_indices].values
    cumsum_labels = np.cumsum(sorted_labels)
    
    gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
    return gini


def calculate_periodic_gini_prod_ver_trench_md(df, score_column, label_column, namecolumn, 
                                        model_version_column=None, trench_column=None, 
                                        loan_type_column=None, loan_product_type_column=None,
                                        account_id_column=None):
    """
    Calculate periodic Gini coefficients at multiple levels:
    - Overall (entire dataset)
    - By each individual segment (model version, trench, loan type, loan product type)
    - By all possible combinations of segments
    
    Parameters:
    df: DataFrame with disbursement dates and score/label columns
    score_column: name of the score column
    label_column: name of the label column
    namecolumn: name for the bad rate label
    model_version_column: (optional) name of column for model version
    trench_column: (optional) name of column for trench category
    loan_type_column: (optional) name of loan type column
    loan_product_type_column: (optional) name of loan product type column
    account_id_column: (optional) name of column for distinct account IDs
    """
    # Input validation
    required_columns = ['disbursementdate', score_column, label_column]
    if not all(col in df.columns for col in required_columns):
        raise ValueError(f"Missing required columns. Need: {required_columns}")
    
    optional_columns = {
        'model_version': model_version_column,
        'trench': trench_column,
        'loan_type': loan_type_column,
        'loan_product_type': loan_product_type_column,
        'account_id': account_id_column
    }
    
    for col_name, col in optional_columns.items():
        if col and col not in df.columns:
            raise ValueError(f"{col_name.replace('_', ' ').title()} column '{col}' not found in dataframe")
    
    # Create a copy to avoid modifying original dataframe
    df = df.copy()
    
    # Ensure date is datetime type
    df['disbursementdate'] = pd.to_datetime(df['disbursementdate'])
    
    # Ensure score and label columns are numeric
    df[score_column] = pd.to_numeric(df[score_column], errors='coerce')
    df[label_column] = pd.to_numeric(df[label_column], errors='coerce')
    
    # Drop rows with invalid values
    df = df.dropna(subset=[score_column, label_column])
    
    # Define list of datasets to process
    datasets_to_process = [('Overall', df, {})]
    
    # Create list of available segment columns
    segment_columns = []
    if model_version_column:
        segment_columns.append(('ModelVersion', model_version_column))
    if trench_column:
        segment_columns.append(('Trench', trench_column))
    if loan_type_column:
        segment_columns.append(('LoanType', loan_type_column))
    if loan_product_type_column:
        segment_columns.append(('ProductType', loan_product_type_column))
    
    # Generate all possible combinations of segment columns (from single to all)
    for r in range(1, len(segment_columns) + 1):
        for combo in combinations(segment_columns, r):
            # Create combinations by iterating through all segment dimensions
            def generate_combinations(df, segment_columns, index=0, current_filter=None, current_name=''):
                if current_filter is None:
                    current_filter = {}
                
                if index >= len(segment_columns):
                    # Apply all filters and create segment
                    filtered_df = df
                    for col, val in current_filter.items():
                        filtered_df = filtered_df[filtered_df[col] == val]
                    
                    if len(filtered_df) > 0:
                        yield (current_name.strip('_'), filtered_df, current_filter.copy())
                    return
                
                seg_name, seg_col = segment_columns[index]
                for seg_value in sorted(df[seg_col].dropna().unique()):
                    new_filter = current_filter.copy()
                    new_filter[seg_col] = seg_value
                    new_name = current_name + f'{seg_name}_{seg_value}_'
                    
                    yield from generate_combinations(df, segment_columns, index + 1, new_filter, new_name)
            
            for combo_name, combo_df, combo_metadata in generate_combinations(df, list(combo)):
                datasets_to_process.append((combo_name, combo_df, combo_metadata))
    
    all_results = []
    
    # Process each dataset
    for dataset_name, dataset_df, metadata in datasets_to_process:
        # Calculate weekly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['week'] = dataset_df_copy['disbursementdate'].dt.to_period('W')
        weekly_gini = dataset_df_copy.groupby('week').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 10 else np.nan
        ).reset_index(name='gini')
        weekly_gini['period'] = 'Week'
        weekly_gini['start_date'] = weekly_gini['week'].apply(lambda x: x.to_timestamp())
        weekly_gini['end_date'] = weekly_gini['start_date'] + timedelta(days=6)
        
        # Add distinct account count for weekly
        if account_id_column:
            weekly_account_counts = dataset_df_copy.groupby('week')[account_id_column].nunique().reset_index()
            weekly_account_counts.columns = ['week', 'distinct_accounts']
            weekly_gini = weekly_gini.merge(weekly_account_counts, on='week', how='left')
        
        weekly_gini = weekly_gini[['start_date', 'end_date', 'gini', 'period'] + (['distinct_accounts'] if account_id_column else [])]
        
        # Calculate monthly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['month'] = dataset_df_copy['disbursementdate'].dt.to_period('M')
        monthly_gini = dataset_df_copy.groupby('month').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 20 else np.nan
        ).reset_index(name='gini')
        monthly_gini['period'] = 'Month'
        monthly_gini['start_date'] = monthly_gini['month'].apply(lambda x: x.to_timestamp())
        monthly_gini['end_date'] = monthly_gini['start_date'] + pd.DateOffset(months=1) - pd.Timedelta(days=1)
        
        # Add distinct account count for monthly
        if account_id_column:
            monthly_account_counts = dataset_df_copy.groupby('month')[account_id_column].nunique().reset_index()
            monthly_account_counts.columns = ['month', 'distinct_accounts']
            monthly_gini = monthly_gini.merge(monthly_account_counts, on='month', how='left')
        
        monthly_gini = monthly_gini[['start_date', 'end_date', 'gini', 'period'] + (['distinct_accounts'] if account_id_column else [])]
        
        # Combine results for this dataset
        gini_results = pd.concat([weekly_gini, monthly_gini], ignore_index=True)
        gini_results = gini_results.sort_values(by='start_date').reset_index(drop=True)
        
        # Add metadata columns
        gini_results['Model_Name'] = score_column
        gini_results['bad_rate'] = namecolumn
        gini_results['segment_type'] = dataset_name
        
        # Add individual segment components
        if model_version_column and model_version_column in metadata:
            gini_results['model_version'] = metadata[model_version_column]
        else:
            gini_results['model_version'] = None
        
        if trench_column and trench_column in metadata:
            gini_results['trench_category'] = metadata[trench_column]
        else:
            gini_results['trench_category'] = None
        
        if loan_type_column and loan_type_column in metadata:
            gini_results['loan_type'] = metadata[loan_type_column]
        else:
            gini_results['loan_type'] = None
        
        if loan_product_type_column and loan_product_type_column in metadata:
            gini_results['loan_product_type'] = metadata[loan_product_type_column]
        else:
            gini_results['loan_product_type'] = None
        
        gini_results.rename(columns={'gini': f'{score_column}_{namecolumn}_gini'}, inplace=True)
        
        all_results.append(gini_results)
    
    # Combine all results
    final_results = pd.concat(all_results, ignore_index=True)
    
    return final_results


# Usage:
# gini_results = calculate_periodic_gini_prod_ver_trench_md(
#     df_concat, 
#     'Alpha_cic_sil_score', 
#     'deffpd0', 
#     'FPD0',
#     model_version_column='modelVersionId',
#     trench_column='trenchCategory',
#     loan_type_column='loan_type',
#     loan_product_type_column='loan_product_type',
#     account_id_column='digitalLoanAccountId'
# )

In [6]:
import pandas as pd
import numpy as np
from datetime import timedelta
from itertools import combinations

def calculate_gini(scores, labels):
    """Calculate Gini coefficient"""
    n = len(scores)
    if n < 2:
        return np.nan
    
    sorted_indices = np.argsort(scores)
    sorted_labels = labels.iloc[sorted_indices].values
    cumsum_labels = np.cumsum(sorted_labels)
    
    gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
    return gini


def calculate_periodic_gini_prod_ver_trench_md_col(df, score_column, label_column, namecolumn, 
                                        model_version_column=None, trench_column=None, 
                                        loan_type_column=None, loan_product_type_column=None,
                                        account_id_column=None):
    """
    Calculate periodic Gini coefficients at multiple levels (wide format):
    - Overall (entire dataset)
    - By each individual segment (model version, trench, loan type, loan product type)
    - By all possible combinations of segments
    
    Returns wide format with one row per period and separate columns for each segment_type's Gini.
    
    Parameters:
    df: DataFrame with disbursement dates and score/label columns
    score_column: name of the score column
    label_column: name of the label column
    namecolumn: name for the bad rate label
    model_version_column: (optional) name of column for model version
    trench_column: (optional) name of column for trench category
    loan_type_column: (optional) name of loan type column
    loan_product_type_column: (optional) name of loan product type column
    account_id_column: (optional) name of column for distinct account IDs
    """
    # Input validation
    required_columns = ['disbursementdate', score_column, label_column]
    if not all(col in df.columns for col in required_columns):
        raise ValueError(f"Missing required columns. Need: {required_columns}")
    
    optional_columns = {
        'model_version': model_version_column,
        'trench': trench_column,
        'loan_type': loan_type_column,
        'loan_product_type': loan_product_type_column,
        'account_id': account_id_column
    }
    
    for col_name, col in optional_columns.items():
        if col and col not in df.columns:
            raise ValueError(f"{col_name.replace('_', ' ').title()} column '{col}' not found in dataframe")
    
    # Create a copy to avoid modifying original dataframe
    df = df.copy()
    
    # Ensure date is datetime type
    df['disbursementdate'] = pd.to_datetime(df['disbursementdate'])
    
    # Ensure score and label columns are numeric
    df[score_column] = pd.to_numeric(df[score_column], errors='coerce')
    df[label_column] = pd.to_numeric(df[label_column], errors='coerce')
    
    # Drop rows with invalid values
    df = df.dropna(subset=[score_column, label_column])
    
    # Define list of datasets to process
    datasets_to_process = [('Overall', df, {})]
    
    # Create list of available segment columns
    segment_columns = []
    if model_version_column:
        segment_columns.append(('ModelVersion', model_version_column))
    if trench_column:
        segment_columns.append(('Trench', trench_column))
    if loan_type_column:
        segment_columns.append(('LoanType', loan_type_column))
    if loan_product_type_column:
        segment_columns.append(('ProductType', loan_product_type_column))
    
    # Generate all possible combinations of segment columns (from single to all)
    for r in range(1, len(segment_columns) + 1):
        for combo in combinations(segment_columns, r):
            # Create combinations by iterating through all segment dimensions
            def generate_combinations(df, segment_columns, index=0, current_filter=None, current_name=''):
                if current_filter is None:
                    current_filter = {}
                
                if index >= len(segment_columns):
                    # Apply all filters and create segment
                    filtered_df = df
                    for col, val in current_filter.items():
                        filtered_df = filtered_df[filtered_df[col] == val]
                    
                    if len(filtered_df) > 0:
                        yield (current_name.strip('_'), filtered_df, current_filter.copy())
                    return
                
                seg_name, seg_col = segment_columns[index]
                for seg_value in sorted(df[seg_col].dropna().unique()):
                    new_filter = current_filter.copy()
                    new_filter[seg_col] = seg_value
                    new_name = current_name + f'{seg_name}_{seg_value}_'
                    
                    yield from generate_combinations(df, segment_columns, index + 1, new_filter, new_name)
            
            for combo_name, combo_df, combo_metadata in generate_combinations(df, list(combo)):
                datasets_to_process.append((combo_name, combo_df, combo_metadata))
    
    all_results = []
    
    # Process each dataset
    for dataset_name, dataset_df, metadata in datasets_to_process:
        # Calculate weekly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['week'] = dataset_df_copy['disbursementdate'].dt.to_period('W')
        weekly_gini = dataset_df_copy.groupby('week').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 10 else np.nan
        ).reset_index(name='gini')
        weekly_gini['period'] = 'Week'
        weekly_gini['start_date'] = weekly_gini['week'].apply(lambda x: x.to_timestamp())
        weekly_gini['end_date'] = weekly_gini['start_date'] + timedelta(days=6)
        weekly_gini = weekly_gini[['start_date', 'end_date', 'gini', 'period']]
        
        # Calculate monthly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['month'] = dataset_df_copy['disbursementdate'].dt.to_period('M')
        monthly_gini = dataset_df_copy.groupby('month').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 20 else np.nan
        ).reset_index(name='gini')
        monthly_gini['period'] = 'Month'
        monthly_gini['start_date'] = monthly_gini['month'].apply(lambda x: x.to_timestamp())
        monthly_gini['end_date'] = monthly_gini['start_date'] + pd.DateOffset(months=1) - pd.Timedelta(days=1)
        monthly_gini = monthly_gini[['start_date', 'end_date', 'gini', 'period']]
        
        # Combine results for this dataset
        gini_results = pd.concat([weekly_gini, monthly_gini], ignore_index=True)
        gini_results = gini_results.sort_values(by='start_date').reset_index(drop=True)
        
        # Create column name for this segment's Gini
        gini_column_name = f'{score_column}_{namecolumn}_gini_{dataset_name}'
        gini_results[gini_column_name] = gini_results['gini']
        gini_results = gini_results.drop('gini', axis=1)
        
        all_results.append(gini_results)
    
    # Merge all results on start_date, end_date, and period
    final_results = all_results[0]
    for result_df in all_results[1:]:
        final_results = final_results.merge(
            result_df,
            on=['start_date', 'end_date', 'period'],
            how='outer'
        )
    
    # Add metadata columns (these will be the same for each row)
    final_results['Model_Name'] = score_column
    final_results['bad_rate'] = namecolumn
    
    if model_version_column:
        final_results['model_version'] = None
    else:
        final_results['model_version'] = None
    
    if trench_column:
        final_results['trench_category'] = None
    else:
        final_results['trench_category'] = None
    
    if loan_type_column:
        final_results['loan_type'] = None
    else:
        final_results['loan_type'] = None
    
    if loan_product_type_column:
        final_results['loan_product_type'] = None
    else:
        final_results['loan_product_type'] = None
    
    # Reorder columns: metadata first, then all Gini columns
    metadata_cols = ['start_date', 'end_date', 'period', 'Model_Name', 'bad_rate', 
                     'model_version', 'trench_category', 'loan_type', 'loan_product_type']
    gini_cols = [col for col in final_results.columns if col.startswith(f'{score_column}_{namecolumn}_gini_')]
    
    final_results = final_results[metadata_cols + gini_cols]
    
    return final_results


# Usage:
# gini_results = calculate_periodic_gini_prod_ver_trench_md(
#     df_concat, 
#     'Alpha_cic_sil_score', 
#     'deffpd0', 
#     'FPD0',
#     model_version_column='modelVersionId',
#     trench_column='trenchCategory',
#     loan_type_column='loan_type',
#     loan_product_type_column='loan_product_type',
#     account_id_column='digitalLoanAccountId'
# )

In [7]:
import pandas as pd
import numpy as np
from datetime import timedelta
from itertools import combinations

def calculate_gini(scores, labels):
    """Calculate Gini coefficient"""
    n = len(scores)
    if n < 2:
        return np.nan
    
    sorted_indices = np.argsort(scores)
    sorted_labels = labels.iloc[sorted_indices].values
    cumsum_labels = np.cumsum(sorted_labels)
    
    gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
    return gini


def calculate_periodic_gini_prod_ver_trench_dimfact(df, score_column, label_column, namecolumn, 
                                        model_version_column=None, trench_column=None, 
                                        loan_type_column=None, loan_product_type_column=None,
                                        account_id_column=None):
    """
    Calculate periodic Gini coefficients and return Power BI-friendly long format
    with fact and dimension tables.
    
    Returns:
    - fact_table: Long format with one row per segment per period
    - dimension_table: Unique segment combinations for filtering
    
    Parameters:
    df: DataFrame with disbursement dates and score/label columns
    score_column: name of the score column
    label_column: name of the label column
    namecolumn: name for the bad rate label
    model_version_column: (optional) name of column for model version
    trench_column: (optional) name of column for trench category
    loan_type_column: (optional) name of loan type column
    loan_product_type_column: (optional) name of loan product type column
    account_id_column: (optional) name of column for distinct account IDs
    """
    # Input validation
    required_columns = ['disbursementdate', score_column, label_column]
    if not all(col in df.columns for col in required_columns):
        raise ValueError(f"Missing required columns. Need: {required_columns}")
    
    optional_columns = {
        'model_version': model_version_column,
        'trench': trench_column,
        'loan_type': loan_type_column,
        'loan_product_type': loan_product_type_column,
        'account_id': account_id_column
    }
    
    for col_name, col in optional_columns.items():
        if col and col not in df.columns:
            raise ValueError(f"{col_name.replace('_', ' ').title()} column '{col}' not found in dataframe")
    
    # Create a copy to avoid modifying original dataframe
    df = df.copy()
    
    # Ensure date is datetime type
    df['disbursementdate'] = pd.to_datetime(df['disbursementdate'])
    
    # Ensure score and label columns are numeric
    df[score_column] = pd.to_numeric(df[score_column], errors='coerce')
    df[label_column] = pd.to_numeric(df[label_column], errors='coerce')
    
    # Drop rows with invalid values
    df = df.dropna(subset=[score_column, label_column])
    
    # Define list of datasets to process
    datasets_to_process = [('Overall', df, {})]
    
    # Create list of available segment columns
    segment_columns = []
    if model_version_column:
        segment_columns.append(('ModelVersion', model_version_column))
    if trench_column:
        segment_columns.append(('Trench', trench_column))
    if loan_type_column:
        segment_columns.append(('LoanType', loan_type_column))
    if loan_product_type_column:
        segment_columns.append(('ProductType', loan_product_type_column))
    
    # Generate all possible combinations of segment columns
    for r in range(1, len(segment_columns) + 1):
        for combo in combinations(segment_columns, r):
            def generate_combinations(df, segment_columns, index=0, current_filter=None, current_name=''):
                if current_filter is None:
                    current_filter = {}
                
                if index >= len(segment_columns):
                    filtered_df = df
                    for col, val in current_filter.items():
                        filtered_df = filtered_df[filtered_df[col] == val]
                    
                    if len(filtered_df) > 0:
                        yield (current_name.strip('_'), filtered_df, current_filter.copy())
                    return
                
                seg_name, seg_col = segment_columns[index]
                for seg_value in sorted(df[seg_col].dropna().unique()):
                    new_filter = current_filter.copy()
                    new_filter[seg_col] = seg_value
                    new_name = current_name + f'{seg_name}_{seg_value}_'
                    
                    yield from generate_combinations(df, segment_columns, index + 1, new_filter, new_name)
            
            for combo_name, combo_df, combo_metadata in generate_combinations(df, list(combo)):
                datasets_to_process.append((combo_name, combo_df, combo_metadata))
    
    all_results = []
    
    # Process each dataset
    for dataset_name, dataset_df, metadata in datasets_to_process:
        # Calculate weekly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['week'] = dataset_df_copy['disbursementdate'].dt.to_period('W')
        weekly_gini = dataset_df_copy.groupby('week').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 10 else np.nan
        ).reset_index(name='gini_value')
        weekly_gini['period'] = 'Week'
        weekly_gini['start_date'] = weekly_gini['week'].apply(lambda x: x.to_timestamp())
        weekly_gini['end_date'] = weekly_gini['start_date'] + timedelta(days=6)
        
        # Add distinct account count for weekly
        if account_id_column:
            weekly_account_counts = dataset_df_copy.groupby('week')[account_id_column].nunique().reset_index()
            weekly_account_counts.columns = ['week', 'distinct_accounts']
            weekly_gini = weekly_gini.merge(weekly_account_counts, on='week', how='left')
        else:
            weekly_gini['distinct_accounts'] = None
        
        weekly_gini = weekly_gini[['start_date', 'end_date', 'gini_value', 'period', 'distinct_accounts']]
        
        # Calculate monthly Gini
        dataset_df_copy = dataset_df.copy()
        dataset_df_copy['month'] = dataset_df_copy['disbursementdate'].dt.to_period('M')
        monthly_gini = dataset_df_copy.groupby('month').apply(
            lambda x: calculate_gini(x[score_column], x[label_column])
            if len(x) >= 20 else np.nan
        ).reset_index(name='gini_value')
        monthly_gini['period'] = 'Month'
        monthly_gini['start_date'] = monthly_gini['month'].apply(lambda x: x.to_timestamp())
        monthly_gini['end_date'] = monthly_gini['start_date'] + pd.DateOffset(months=1) - pd.Timedelta(days=1)
        
        # Add distinct account count for monthly
        if account_id_column:
            monthly_account_counts = dataset_df_copy.groupby('month')[account_id_column].nunique().reset_index()
            monthly_account_counts.columns = ['month', 'distinct_accounts']
            monthly_gini = monthly_gini.merge(monthly_account_counts, on='month', how='left')
        else:
            monthly_gini['distinct_accounts'] = None
        
        monthly_gini = monthly_gini[['start_date', 'end_date', 'gini_value', 'period', 'distinct_accounts']]
        
        # Combine results for this dataset
        gini_results = pd.concat([weekly_gini, monthly_gini], ignore_index=True)
        gini_results = gini_results.sort_values(by='start_date').reset_index(drop=True)
        
        # Add metadata columns
        gini_results['Model_Name'] = score_column
        gini_results['bad_rate'] = namecolumn
        gini_results['segment_type'] = dataset_name
        
        # Add individual segment components
        gini_results['model_version'] = metadata.get(model_version_column, None) if model_version_column else None
        gini_results['trench_category'] = metadata.get(trench_column, None) if trench_column else None
        gini_results['loan_type'] = metadata.get(loan_type_column, None) if loan_type_column else None
        gini_results['loan_product_type'] = metadata.get(loan_product_type_column, None) if loan_product_type_column else None
        
        all_results.append(gini_results)
    
    # Combine all results
    fact_table = pd.concat(all_results, ignore_index=True)
    
    # Create dimension table (unique segment combinations for filtering)
    dimension_table = fact_table[['Model_Name', 'bad_rate', 'segment_type', 'model_version', 
                                   'trench_category', 'loan_type', 'loan_product_type']].drop_duplicates().reset_index(drop=True)
    dimension_table['segment_id'] = range(len(dimension_table))
    
    # Add segment_id to fact table
    fact_table = fact_table.merge(dimension_table[['segment_id', 'Model_Name', 'bad_rate', 'segment_type', 
                                                     'model_version', 'trench_category', 'loan_type', 'loan_product_type']], 
                                  on=['Model_Name', 'bad_rate', 'segment_type', 'model_version', 
                                      'trench_category', 'loan_type', 'loan_product_type'], 
                                  how='left')
    
    # Reorder columns in fact table
    fact_table = fact_table[['segment_id', 'start_date', 'end_date', 'period', 'gini_value', 'distinct_accounts',
                             'Model_Name', 'bad_rate', 'segment_type', 'model_version', 'trench_category', 
                             'loan_type', 'loan_product_type']]
    
    return fact_table, dimension_table


# Usage:
# fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_md(
#     df_concat, 
#     'Alpha_cic_sil_score', 
#     'deffpd0', 
#     'FPD0',
#     model_version_column='modelVersionId',
#     trench_column='trenchCategory',
#     loan_type_column='loan_type',
#     loan_product_type_column='loan_product_type',
#     account_id_column='digitalLoanAccountId'
# )
# 
# # In Power BI:
# # 1. Import fact_table and dimension_table
# # 2. Create relationship: dimension_table[segment_id] -> fact_table[segment_id]
# # 3. Use dimension table columns as filters
# # 4. Create DAX measures:
# #    - Gini Measure = AVERAGE(fact_table[gini_value])
# #    - Account Count = SUM(fact_table[distinct_accounts])
# # 5. Use start_date, end_date, period for time-based analysis

# update_tables

In [8]:

def update_tables(fact_table: pd.DataFrame, dimension_table: pd.DataFrame, model_name: str, product: str) -> tuple:
    """
    Updates fact_table and dimension_table:
    - Sets 'Model_display_name' to the given model_name
    - Replaces NaN values in specified columns with 'Overall'
    
    Returns:
        Updated fact_table and dimension_table as a tuple
    """
    # Columns where missing values should be replaced
    cols_to_replace = ['model_version', 'trench_category', 'loan_type', 'loan_product_type']
    
    # Update fact_table
    fact_table['Model_display_name'] = model_name
    fact_table['Product_Category'] = product
    fact_table[cols_to_replace] = fact_table[cols_to_replace].fillna('Overall')
    
    # Update dimension_table
    dimension_table['Model_display_name'] = model_name
    dimension_table['Product_Category'] = product
    dimension_table[cols_to_replace] = dimension_table[cols_to_replace].fillna('Overall')
    
    return fact_table, dimension_table


# SIL

## cic_model_sil

### FPD0

### Test

In [9]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (49314, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3341392  32acec8d-2500-4792-85b6-b65fa3de1744    60833413920014   
1    3341022  4a4a7ffa-ff23-43c2-bd1b-7c002af9f3dd    60833410220011   
2    3341053  1d39bf79-2fde-48b4-86e8-80049b658186    60833410530018   
3    3341010  2beb698e-233a-4c3f-a28a-48a9b84515c1    60833410100017   
4    3341090  10180088-469f-44a1-a456-ea553d6bdd89    60833410900013   

  modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil  0.15300666239968524   2025-03-26 12:56:59   
1    cic_model_sil   0.1752134698666708   2025-03-26 09:24:30   
2    cic_model_sil  0.14486139276382995   2025-03-26 09:40:03   
3    cic_model_sil  0.13818363299922884   2025-03-26 09:11:26   
4    cic_model_sil  0.12163557278783477   2025-03-26 10:05:36   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-03-26           2025-03           Test        1                1   
1       2025-03-26           2025-03           Test        0                1   
2       2025-03-26           2025-03           Test        0                1   
3       2025-03-26           2025-03           Test        0                1   
4       2025-03-26           2025-03           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [10]:
df1 = dfd.copy()

### Train

In [11]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (292181, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2265331  824fe15d-1b63-4b3a-b6ee-804730a50840    60822653310014   
1     2253965  71c36928-9f11-4eb8-8d10-c4bd0e5f176d    60822539650019   
2     2174521  a21a5f55-629e-4402-a314-d55f83b1ce6c    60821745210013   
3     2282229  78c60125-6e6c-4cc2-8607-6db18f8e72fb    60822822290015   
4     1906261  aa42d0e6-aca4-4917-a065-8cfdf17ccc0d    60819062610016   

        modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0  Alpha - CIC-SIL-Model             0.164665   2023-10-08 19:09:57   
1  Alpha - CIC-SIL-Model             0.080221   2023-09-30 16:13:31   
2  Alpha - CIC-SIL-Model             0.125999   2023-08-05 18:14:19   
3  Alpha - CIC-SIL-Model             0.055914   2023-10-23 17:23:08   
4  Alpha - CIC-SIL-Model             0.065794   2023-02-18 14:49:12   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2023-10-08           2023-10          Train        0                1   
1       2023-09-30           2023-09          Train        0                1   
2       2023-08-05           2023-08          Train        0                1   
3       2023-10-23           2023-10          Train        0                1   
4       2023-02-18           2023-02          Train        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [12]:
df2 = dfd.copy()

### Concat

In [13]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (341495, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3341392  32acec8d-2500-4792-85b6-b65fa3de1744    60833413920014   
1    3341022  4a4a7ffa-ff23-43c2-bd1b-7c002af9f3dd    60833410220011   
2    3341053  1d39bf79-2fde-48b4-86e8-80049b658186    60833410530018   
3    3341010  2beb698e-233a-4c3f-a28a-48a9b84515c1    60833410100017   
4    3341090  10180088-469f-44a1-a456-ea553d6bdd89    60833410900013   

  modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil  0.15300666239968524   2025-03-26 12:56:59   
1    cic_model_sil   0.1752134698666708   2025-03-26 09:24:30   
2    cic_model_sil  0.14486139276382995   2025-03-26 09:40:03   
3    cic_model_sil  0.13818363299922884   2025-03-26 09:11:26   
4    cic_model_sil  0.12163557278783477   2025-03-26 10:05:36   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-03-26           2025-03           Test        1                1   
1       2025-03-26           2025-03           Test        0                1   
2       2025-03-26           2025-03           Test        0                1   
3       2025-03-26           2025-03           Test        0                1   
4       2025-03-26           2025-03           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [14]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'Alpha_cic_sil_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [15]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance            14398
                                                Mall                  4779
                SIL ZERO        v1              Appliance             2032
                SIL-Instore     v1              Appliance            23181
                                                Mall                  4924
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            27940
                                                Mall                  8153
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [16]:
df_concat['new_loan_type'].unique()

array(['SIL-Instore', 'SIL ZERO', 'SIL Competitor', 'SIL Repeat'],
      dtype=object)

In [17]:
# df_concat.to_csv(r"D:\OneDrive - Tonik Financial Pte Ltd\MyStuff\Data Engineering\Model_Monitoring\Gini Monitoring\New_Gini_Monitoring_2025-11-25\Future\sample.csv", index = False)

In [18]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Alpha_cic_sil_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [19]:
fact_table, dimension_table =update_tables(fact_table, dimension_table, 'cic_model_sil', 'SIL')

In [20]:
# print(fact_table.columns)
# fact_table['segment_type'].value_counts(dropna=False)
# fact_table['Model_display_name'] = 'cic_model_sil'

In [21]:
# # Columns where missing values should be replaced
# cols_to_replace = ['model_version', 'trench_category', 'loan_type', 'loan_product_type']

# # Replace NaN values with 'Overall'
# fact_table[cols_to_replace] = fact_table[cols_to_replace].fillna('Overall')

# fact_table.head()


In [22]:
# dimension_table['Model_display_name'] = 'cic_model_sil'

In [23]:
# # Columns where missing values should be replaced
# cols_to_replace = ['model_version', 'trench_category', 'loan_type', 'loan_product_type']

# # Replace NaN values with 'Overall'
# dimension_table[cols_to_replace] = dimension_table[cols_to_replace].fillna('Overall')

# dimension_table.head()

In [24]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_TRUNCATE",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=d63499a0-9e0f-459f-b068-f00eb81db6b3>

In [25]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_TRUNCATE",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=51d60fc2-ff79-4da3-a7e2-5a4fb422bf9d>

### FPD10

### Test

In [26]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (49314, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3696243  1cf1da6f-3cb7-491e-93e2-496ec70a9011    60836962430015   
1    3696154  2d43cda8-954f-40dc-be03-3a9ce1cb0a88    60836961540015   
2    3696212  3b45454c-e3d8-4072-b146-269a4ed008a4    60836962120018   
3    3696179  57401021-d7ea-40d7-bbfb-ec6f0d68b32e    60836961790014   
4    3696164  59e1de91-d469-42b6-86bf-2375c9675376    60836961640017   

  modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil   0.1884467427914663   2025-09-21 11:39:19   
1    cic_model_sil  0.10276763916461164   2025-09-21 11:19:54   
2    cic_model_sil  0.06109008507583079   2025-09-21 11:31:51   
3    cic_model_sil  0.10216105370739698   2025-09-21 11:29:35   
4    cic_model_sil  0.08119468618993392   2025-09-21 11:21:23   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-09-21           2025-09           Test         0   
1       2025-09-21           2025-09           Test         0   
2       2025-09-21           2025-09           Test         0   
3       2025-09-21           2025-09           Test         0   
4       2025-09-21           2025-09           Test         0   

   flg_mature_fpd0   new_loan_type modelVersionId trenchCategory  \
0                1     SIL-Instore             v1            ALL   
1                1     SIL-Instore             v1            ALL   
2                1  SIL Competitor             v1            ALL   
3                1  SIL Competitor             v1            ALL   
4                1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [27]:
df1 = dfd.copy()

### Train

In [28]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (292181, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2415285  56fa9034-34f4-468d-85c5-0e9629b9bcee    60824152850012   
1     2286035  1b3f72c8-f52e-4d35-865d-533f9eab2d1f    60822860350013   
2     2247676  58944713-7c86-46c5-a497-72cd4e9f42b4    60822476760014   
3     2256527  95036a20-71bf-4cd0-8279-7a61114526a3    60822565270013   
4     2220017  4fa207f3-8cbd-4513-9067-49120443d41b    60822200170017   

        modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0  Alpha - CIC-SIL-Model             0.125471   2024-02-29 19:55:03   
1  Alpha - CIC-SIL-Model             0.157741   2023-10-27 17:45:05   
2  Alpha - CIC-SIL-Model             0.125541   2023-09-25 15:44:49   
3  Alpha - CIC-SIL-Model             0.199273   2023-10-02 13:10:53   
4  Alpha - CIC-SIL-Model             0.101669   2023-09-03 16:40:53   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2024-02-29           2024-02          Train         1   
1       2023-10-27           2023-10          Train         0   
2       2023-09-25           2023-09          Train         0   
3       2023-10-02           2023-10          Train         0   
4       2023-09-03           2023-09          Train         0   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [29]:
df2 = dfd.copy()

### Concat

In [30]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (341495, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3696243  1cf1da6f-3cb7-491e-93e2-496ec70a9011    60836962430015   
1    3696154  2d43cda8-954f-40dc-be03-3a9ce1cb0a88    60836961540015   
2    3696212  3b45454c-e3d8-4072-b146-269a4ed008a4    60836962120018   
3    3696179  57401021-d7ea-40d7-bbfb-ec6f0d68b32e    60836961790014   
4    3696164  59e1de91-d469-42b6-86bf-2375c9675376    60836961640017   

  modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil   0.1884467427914663   2025-09-21 11:39:19   
1    cic_model_sil  0.10276763916461164   2025-09-21 11:19:54   
2    cic_model_sil  0.06109008507583079   2025-09-21 11:31:51   
3    cic_model_sil  0.10216105370739698   2025-09-21 11:29:35   
4    cic_model_sil  0.08119468618993392   2025-09-21 11:21:23   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-09-21           2025-09           Test         0   
1       2025-09-21           2025-09           Test         0   
2       2025-09-21           2025-09           Test         0   
3       2025-09-21           2025-09           Test         0   
4       2025-09-21           2025-09           Test         0   

   flg_mature_fpd0   new_loan_type modelVersionId trenchCategory  \
0                1     SIL-Instore             v1            ALL   
1                1     SIL-Instore             v1            ALL   
2                1  SIL Competitor             v1            ALL   
3                1  SIL Competitor             v1            ALL   
4                1     SIL-Instore             v1            ALL   

  loan_product_type  flg_mature_fpd10  
0         Appliance              <NA>  
1         Appliance              <NA>  
2         Appliance              <NA>  
3         Appliance              <NA>  
4         Appliance              <NA>

In [31]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance            14398
                                                Mall                  4779
                SIL ZERO        v1              Appliance             2032
                SIL-Instore     v1              Appliance            23181
                                                Mall                  4924
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            27940
                                                Mall                  8153
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [32]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Alpha_cic_sil_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [33]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_sil', product='SIL')

In [34]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=0bbc7e71-00e3-4160-841b-3dc444ebf142>

In [35]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=3cd1e34a-5c37-4614-a5a6-0ca443851437>

### FPD30

### Test

In [36]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (38120, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3649348  b9d3cfda-e9ec-457d-acc9-378fc5dbe34a    60836493480011   
1    3649357  005cb5ff-911d-4f65-ba82-7ab53ad36703    60836493570011   
2    3649360  d69adbb2-c6f8-4c4c-823c-3cb326846078    60836493600016   
3    3649366  dcb09537-dcda-434a-af1f-d28133ed1ed9    60836493660012   
4    3649367  7f4b2f91-c197-4a19-99f3-65ed394e7480    60836493670013   

  modelDisplayName   Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil   0.17544426787160503   2025-08-29 11:05:05   
1    cic_model_sil   0.12767864370044307   2025-08-29 11:23:19   
2    cic_model_sil  0.048451027527634465   2025-08-29 11:05:41   
3    cic_model_sil    0.0881313209403649   2025-08-29 11:08:09   
4    cic_model_sil   0.08915525466033108   2025-08-29 11:07:43   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-08-29           2025-08           Test         0   
1       2025-08-29           2025-08           Test         0   
2       2025-08-29           2025-08           Test         0   
3       2025-08-29           2025-08           Test         0   
4       2025-08-29           2025-08           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1  SIL Competitor             v1            ALL   
1                 1  SIL Competitor             v1            ALL   
2                 1  SIL Competitor             v1            ALL   
3                 1        SIL ZERO             v1            ALL   
4                 1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1              Mall  
2         Appliance  
3         Appliance  
4              Mall

In [37]:
df1 = dfd.copy()

### Train

In [38]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (292168, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2223374  a2acf8f0-0d02-4ba7-9e41-e148ca357253    60822233740017   
1     2388939  5d6b748a-b2ff-4fb6-8c9e-07fafd0bf9da    60823889390018   
2     2268557  7c2cce2c-d725-429c-b686-f5def4e38a03    60822685570012   
3     2393893  c4fffb9b-d1c5-4b62-92a3-030d5dc04057    60823938930016   
4     2397963  788e58ec-9753-430d-9a88-d0671394c18f    60823979630019   

        modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0  Alpha - CIC-SIL-Model             0.123149   2023-09-06 15:10:31   
1  Alpha - CIC-SIL-Model             0.132892   2024-02-03 18:55:45   
2  Alpha - CIC-SIL-Model             0.109930   2023-10-12 10:40:26   
3  Alpha - CIC-SIL-Model             0.107587   2024-02-09 10:53:12   
4  Alpha - CIC-SIL-Model             0.123620   2024-02-12 13:39:40   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2023-09-06           2023-09          Train         0   
1       2024-02-03           2024-02          Train         0   
2       2023-10-12           2023-10          Train         0   
3       2024-02-09           2024-02          Train         0   
4       2024-02-15           2024-02          Train         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [39]:
df2 = dfd.copy()

### Concat

In [40]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (330288, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3649348  b9d3cfda-e9ec-457d-acc9-378fc5dbe34a    60836493480011   
1    3649357  005cb5ff-911d-4f65-ba82-7ab53ad36703    60836493570011   
2    3649360  d69adbb2-c6f8-4c4c-823c-3cb326846078    60836493600016   
3    3649366  dcb09537-dcda-434a-af1f-d28133ed1ed9    60836493660012   
4    3649367  7f4b2f91-c197-4a19-99f3-65ed394e7480    60836493670013   

  modelDisplayName   Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil   0.17544426787160503   2025-08-29 11:05:05   
1    cic_model_sil   0.12767864370044307   2025-08-29 11:23:19   
2    cic_model_sil  0.048451027527634465   2025-08-29 11:05:41   
3    cic_model_sil    0.0881313209403649   2025-08-29 11:08:09   
4    cic_model_sil   0.08915525466033108   2025-08-29 11:07:43   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-08-29           2025-08           Test         0   
1       2025-08-29           2025-08           Test         0   
2       2025-08-29           2025-08           Test         0   
3       2025-08-29           2025-08           Test         0   
4       2025-08-29           2025-08           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1  SIL Competitor             v1            ALL   
1                 1  SIL Competitor             v1            ALL   
2                 1  SIL Competitor             v1            ALL   
3                 1        SIL ZERO             v1            ALL   
4                 1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1              Mall  
2         Appliance  
3         Appliance  
4              Mall

In [41]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance            10847
                                                Mall                  3601
                SIL ZERO        v1              Appliance             1683
                SIL-Instore     v1              Appliance            18177
                                                Mall                  3812
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            27935
                                                Mall                  8153
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [42]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Alpha_cic_sil_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [43]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_sil', product='SIL')

In [44]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=11e78444-a3b1-4205-8677-48699f14bb0a>

In [45]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=4535498e-1855-4dff-8eb2-e399d8e4e763>

### FSPD30

### Test

In [46]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (29170, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3664338  a5872ed1-a008-45d6-b6e6-43d70c488255    60836643380018   
1    3667324  be0913e6-ae5c-49f8-86e6-7017cf6cffe2    60836673240014   
2    3667268  a40e54d5-2b2c-4191-a97f-d051504e75d6    60836672680013   
3    3674553  3d7a381e-525f-4e35-b9b5-d4bda1f0ced9    60836745530018   
4    3667051  f87795fd-f6d6-4dae-b637-d2c078d4908f    60836670510018   

  modelDisplayName   Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil    0.1268715555250324   2025-09-04 19:38:34   
1    cic_model_sil  0.042867523942440464   2025-09-06 11:48:09   
2    cic_model_sil   0.07941635712002307   2025-09-06 11:22:34   
3    cic_model_sil   0.05452750510329723   2025-09-09 16:37:50   
4    cic_model_sil   0.12367134360170585   2025-09-06 10:06:22   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-04           2025-09           Test          0   
1       2025-09-06           2025-09           Test          0   
2       2025-09-06           2025-09           Test          0   
3       2025-09-09           2025-09           Test          0   
4       2025-09-06           2025-09           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1        SIL ZERO             v1            ALL   
1                   1  SIL Competitor             v1            ALL   
2                   1     SIL-Instore             v1            ALL   
3                   1  SIL Competitor             v1            ALL   
4                   1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [47]:
df1 = dfd.copy()

### Train

In [48]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (283067, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2265331  824fe15d-1b63-4b3a-b6ee-804730a50840    60822653310014   
1     2253965  71c36928-9f11-4eb8-8d10-c4bd0e5f176d    60822539650019   
2     2174521  a21a5f55-629e-4402-a314-d55f83b1ce6c    60821745210013   
3     2282229  78c60125-6e6c-4cc2-8607-6db18f8e72fb    60822822290015   
4     1906261  aa42d0e6-aca4-4917-a065-8cfdf17ccc0d    60819062610016   

        modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0  Alpha - CIC-SIL-Model             0.164665   2023-10-08 19:09:57   
1  Alpha - CIC-SIL-Model             0.080221   2023-09-30 16:13:31   
2  Alpha - CIC-SIL-Model             0.125999   2023-08-05 18:14:19   
3  Alpha - CIC-SIL-Model             0.055914   2023-10-23 17:23:08   
4  Alpha - CIC-SIL-Model             0.065794   2023-02-18 14:49:12   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2023-10-08           2023-10          Train          0   
1       2023-09-30           2023-09          Train          0   
2       2023-08-05           2023-08          Train          0   
3       2023-10-23           2023-10          Train          0   
4       2023-02-18           2023-02          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1   SIL-Instore             v1            ALL   
1                   1   SIL-Instore             v1            ALL   
2                   1   SIL-Instore             v1            ALL   
3                   1   SIL-Instore             v1            ALL   
4                   1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [49]:
df2 = dfd.copy()

### Concat

In [50]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (312237, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3664338  a5872ed1-a008-45d6-b6e6-43d70c488255    60836643380018   
1    3667324  be0913e6-ae5c-49f8-86e6-7017cf6cffe2    60836673240014   
2    3667268  a40e54d5-2b2c-4191-a97f-d051504e75d6    60836672680013   
3    3674553  3d7a381e-525f-4e35-b9b5-d4bda1f0ced9    60836745530018   
4    3667051  f87795fd-f6d6-4dae-b637-d2c078d4908f    60836670510018   

  modelDisplayName   Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil    0.1268715555250324   2025-09-04 19:38:34   
1    cic_model_sil  0.042867523942440464   2025-09-06 11:48:09   
2    cic_model_sil   0.07941635712002307   2025-09-06 11:22:34   
3    cic_model_sil   0.05452750510329723   2025-09-09 16:37:50   
4    cic_model_sil   0.12367134360170585   2025-09-06 10:06:22   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-04           2025-09           Test          0   
1       2025-09-06           2025-09           Test          0   
2       2025-09-06           2025-09           Test          0   
3       2025-09-09           2025-09           Test          0   
4       2025-09-06           2025-09           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1        SIL ZERO             v1            ALL   
1                   1  SIL Competitor             v1            ALL   
2                   1     SIL-Instore             v1            ALL   
3                   1  SIL Competitor             v1            ALL   
4                   1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [51]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             8012
                                                Mall                  2632
                SIL ZERO        v1              Appliance             1340
                SIL-Instore     v1              Appliance            14265
                                                Mall                  2921
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            25152
                                                Mall                  7238
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [52]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Alpha_cic_sil_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [53]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_sil', product='SIL')

In [54]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=803c6cc9-0e43-466c-bff7-12e6797fe598>

In [55]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=f955095a-3531-42fd-9265-2db888899ea1>

### FSTPD30

### Test

In [56]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (19609, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3603221  67c928fa-e469-4471-b6fa-0ccfc459d6b5    60836032210012   
1    3452144  e5ced157-e148-4f14-8843-9e9a78bd3455    60834521440015   
2    3381741  64dc0d73-2ee4-402f-a011-75b2a711d917    60833817410015   
3    3605049  20dc9554-bb7a-47fe-abbf-a79febabfaf3    60836050490016   
4    3603759  838f536b-7d43-444a-b856-250535d2975f    60836037590011   

  modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil  0.15812960263127632   2025-08-06 15:08:17   
1    cic_model_sil  0.16659797676062135   2025-05-22 19:37:58   
2    cic_model_sil  0.06330238280726355   2025-04-15 18:26:12   
3    cic_model_sil  0.11136085020144332   2025-08-07 13:28:53   
4    cic_model_sil  0.15018469238786453   2025-08-06 17:59:33   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-06           2025-08           Test           0   
1       2025-05-22           2025-05           Test           0   
2       2025-04-15           2025-04           Test           0   
3       2025-08-07           2025-08           Test           0   
4       2025-08-06           2025-08           Test           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1              Mall  
2         Appliance  
3         Appliance  
4         Appliance

In [57]:
df1 = dfd.copy()

### Train

In [58]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Alpha_cic_sil_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Alpha - CIC-SIL-Model', 'cic_model_sil', 'Sil-Alpha-CIC-SIL-Model')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Alpha_cic_sil_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Alpha_cic_sil_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (271522, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2245104  04b0a35b-af72-44a1-ab61-335026c3a0ba    60822451040015   
1     2244374  f3411572-8df3-4a63-b82d-ef960c878bdb    60822443740011   
2     2199287  fdaedd35-c1de-4d37-b9af-59252178fe79    60821992870012   
3     2186912  34894b33-e426-43b0-8b61-02caaffa6557    60821869120017   
4     1941498  9af7e49f-8403-43d8-af12-15c9adec3948    60819414980015   

        modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0  Alpha - CIC-SIL-Model             0.161959   2023-09-23 18:32:39   
1  Alpha - CIC-SIL-Model             0.119192   2023-09-23 13:07:37   
2  Alpha - CIC-SIL-Model             0.164733   2023-08-20 17:02:21   
3  Alpha - CIC-SIL-Model             0.127252   2023-08-13 12:19:18   
4  Alpha - CIC-SIL-Model             0.153677   2023-03-13 16:09:53   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2023-09-23           2023-09          Train           0   
1       2023-09-23           2023-09          Train           0   
2       2023-08-20           2023-08          Train           0   
3       2023-08-13           2023-08          Train           1   
4       2023-03-13           2023-03          Train           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [59]:
df2 = dfd.copy()

### Concat

In [60]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (291131, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3603221  67c928fa-e469-4471-b6fa-0ccfc459d6b5    60836032210012   
1    3452144  e5ced157-e148-4f14-8843-9e9a78bd3455    60834521440015   
2    3381741  64dc0d73-2ee4-402f-a011-75b2a711d917    60833817410015   
3    3605049  20dc9554-bb7a-47fe-abbf-a79febabfaf3    60836050490016   
4    3603759  838f536b-7d43-444a-b856-250535d2975f    60836037590011   

  modelDisplayName  Alpha_cic_sil_score appln_submit_datetime  \
0    cic_model_sil  0.15812960263127632   2025-08-06 15:08:17   
1    cic_model_sil  0.16659797676062135   2025-05-22 19:37:58   
2    cic_model_sil  0.06330238280726355   2025-04-15 18:26:12   
3    cic_model_sil  0.11136085020144332   2025-08-07 13:28:53   
4    cic_model_sil  0.15018469238786453   2025-08-06 17:59:33   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-06           2025-08           Test           0   
1       2025-05-22           2025-05           Test           0   
2       2025-04-15           2025-04           Test           0   
3       2025-08-07           2025-08           Test           0   
4       2025-08-06           2025-08           Test           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1              Mall  
2         Appliance  
3         Appliance  
4         Appliance

In [61]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             4892
                                                Mall                  1606
                SIL ZERO        v1              Appliance              941
                SIL-Instore     v1              Appliance            10166
                                                Mall                  2004
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            21624
                                                Mall                  6102
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [62]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Alpha_cic_sil_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [63]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (9890, 15)
The shape of the dimension table is:	 (175, 10)


In [64]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8cef104d-856a-4c1b-8b09-fbd75df7e4d2>

In [65]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=3aac0503-38de-497a-96be-5e3e6ceef68e>

## alpha_stack_model_sil

### FPD0

### Test

In [66]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (49314, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2814175  0bc78da7-6084-413b-bf16-af4b4d48e41c    60828141750025   
1    3488678  2e2d1f11-1205-48bf-b447-933f48abe0ba    60834886780027   
2    3741166  6d6543fd-984f-4671-a57a-e1f72685ba79    60837411660011   
3    3741211  c6f43789-d266-4ea9-b01a-0f9266be42df    60837412110018   
4    3741216  29fcae1e-e291-4fc1-a949-840b722f99a7    60837412160013   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.03335635042479726   2025-10-13 11:24:02   
1  alpha_stack_model_sil    0.1431711760835379   2025-10-13 10:40:44   
2  alpha_stack_model_sil   0.11076878138747613   2025-10-13 10:19:08   
3  alpha_stack_model_sil   0.04706108343699631   2025-10-13 10:25:17   
4  alpha_stack_model_sil   0.04749411806052213   2025-10-13 10:32:51   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-10-13           2025-10           Test        0                1   
1       2025-10-13           2025-10           Test        0                1   
2       2025-10-13           2025-10           Test        0                1   
3       2025-10-13           2025-10           Test        0                1   
4       2025-10-13           2025-10           Test        0                1   

    new_loan_type modelVersionId trenchCategory loan_product_type  
0     SIL-Instore             v1            ALL         Appliance  
1     SIL-Instore             v1            ALL         Appliance  
2     SIL-Instore             v1            ALL         Appliance  
3  SIL Competitor             v1            ALL         Appliance  
4     SIL-Instore             v1            ALL         Appliance

In [67]:
df1 = dfd.copy()

### Train

In [68]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (297168, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2253633  82ac119a-45b7-4c05-a35c-0a7259d36160    60822536330012   
1     2276509  5ad05d10-97f7-4fc3-8d60-c18add4da273    60822765090011   
2     2408210  54eb187f-b260-44fb-b441-145e42b3040a    60824082100011   
3     2410050  71753995-d309-4448-978c-3f3504abc6c7    60824100500015   
4     2206802  e2db4cc1-eb92-4d04-b8dc-61864e148daa    60822068020018   

        modelDisplayName  Sil_Alpha_Stack_score appln_submit_datetime  \
0  Alpha - StackingModel               0.340642   2024-02-07 18:02:38   
1  Alpha - StackingModel               0.382501   2023-10-18 11:12:21   
2  Alpha - StackingModel               0.110795   2024-02-22 17:46:44   
3  Alpha - StackingModel               0.196353   2024-02-24 16:07:35   
4  Alpha - StackingModel               0.056088   2023-08-25 14:53:07   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2024-02-07           2024-02          Train        1                1   
1       2023-10-18           2023-10          Train        0                1   
2       2024-02-22           2024-02          Train        1                1   
3       2024-02-24           2024-02          Train        0                1   
4       2023-08-25           2023-08          Train        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [69]:
df2 = dfd.copy()

### Concat

In [70]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (346482, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2814175  0bc78da7-6084-413b-bf16-af4b4d48e41c    60828141750025   
1    3488678  2e2d1f11-1205-48bf-b447-933f48abe0ba    60834886780027   
2    3741166  6d6543fd-984f-4671-a57a-e1f72685ba79    60837411660011   
3    3741211  c6f43789-d266-4ea9-b01a-0f9266be42df    60837412110018   
4    3741216  29fcae1e-e291-4fc1-a949-840b722f99a7    60837412160013   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.03335635042479726   2025-10-13 11:24:02   
1  alpha_stack_model_sil    0.1431711760835379   2025-10-13 10:40:44   
2  alpha_stack_model_sil   0.11076878138747613   2025-10-13 10:19:08   
3  alpha_stack_model_sil   0.04706108343699631   2025-10-13 10:25:17   
4  alpha_stack_model_sil   0.04749411806052213   2025-10-13 10:32:51   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-10-13           2025-10           Test        0                1   
1       2025-10-13           2025-10           Test        0                1   
2       2025-10-13           2025-10           Test        0                1   
3       2025-10-13           2025-10           Test        0                1   
4       2025-10-13           2025-10           Test        0                1   

    new_loan_type modelVersionId trenchCategory loan_product_type  
0     SIL-Instore             v1            ALL         Appliance  
1     SIL-Instore             v1            ALL         Appliance  
2     SIL-Instore             v1            ALL         Appliance  
3  SIL Competitor             v1            ALL         Appliance  
4     SIL-Instore             v1            ALL         Appliance

In [71]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'Sil_Alpha_Stack_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [72]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance            14398
                                                Mall                  4779
                SIL ZERO        v1              Appliance             2032
                SIL-Instore     v1              Appliance            23181
                                                Mall                  4924
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            29562
                                                Mall                  8641
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [73]:
df_concat['new_loan_type'].unique()

array(['SIL-Instore', 'SIL Competitor', 'SIL ZERO', 'SIL Repeat'],
      dtype=object)

In [74]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Sil_Alpha_Stack_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [75]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (11524, 15)
The shape of the dimension table is:	 (175, 10)


In [76]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=11f2bff4-b64b-4fef-916e-48af3b61b4c4>

In [77]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=98c4f6c4-6b56-416a-bd69-c7bc30f01ba7>

### FPD10

### Test

In [78]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (49314, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2217104  f79cf4f1-6600-4590-9204-532f6cee93ba    60822171040034   
1    2291594  bf7b6fbb-695c-48ea-a56e-a229edf82e61    60822915940014   
2    3634235  6d640f14-ffd2-43a3-b1e4-62ec3e82b5d9    60836342350017   
3    3644784  9ff96c42-674b-487e-9e4a-cbb16b165045    60836447840016   
4    3644816  2976be11-1111-40ad-9cac-877b2d01abeb    60836448160017   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.12253237264131246   2025-08-26 17:17:58   
1  alpha_stack_model_sil   0.06756078826927069   2025-08-26 16:29:08   
2  alpha_stack_model_sil   0.03224989422262025   2025-08-26 16:43:52   
3  alpha_stack_model_sil    0.0953431772839386   2025-08-26 15:38:32   
4  alpha_stack_model_sil   0.04555704698415861   2025-08-26 15:38:29   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-08-26           2025-08           Test         0   
1       2025-08-26           2025-08           Test         0   
2       2025-08-26           2025-08           Test         1   
3       2025-08-26           2025-08           Test         1   
4       2025-08-26           2025-08           Test         0   

   flg_mature_fpd0   new_loan_type modelVersionId trenchCategory  \
0                1     SIL-Instore             v1            ALL   
1                1     SIL-Instore             v1            ALL   
2                1  SIL Competitor             v1            ALL   
3                1     SIL-Instore             v1            ALL   
4                1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2              Mall  
3         Appliance  
4         Appliance

In [79]:
df1 = dfd.copy()

### Train

In [80]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (297168, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2396664  5f5785aa-cd67-4ff6-9ee3-1274fffec602    60823966640017   
1     2245129  52c5c0e9-ad3a-414e-bf74-dd09302fa7e9    60822451290014   
2     2288079  cb2b2c21-23ca-4e5f-b092-44d5bb813cf3    60822880790013   
3     2413935  168b5ce8-fec9-4347-92c7-d38535175717    60824139350015   
4     2288705  59261373-d2ed-46cc-a668-346d36eb5cd3    60822887050016   

        modelDisplayName  Sil_Alpha_Stack_score appln_submit_datetime  \
0  Alpha - StackingModel               0.038307   2024-02-11 11:07:01   
1  Alpha - StackingModel               0.281433   2023-09-23 18:50:12   
2  Alpha - StackingModel               0.098419   2023-10-29 18:32:46   
3  Alpha - StackingModel               0.209353   2024-02-28 14:13:47   
4  Alpha - StackingModel               0.206326   2023-10-30 14:34:23   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2024-02-11           2024-02          Train         0   
1       2023-09-23           2023-09          Train         1   
2       2023-10-29           2023-10          Train         0   
3       2024-02-28           2024-02          Train         0   
4       2023-10-30           2023-10          Train         0   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [81]:
df2 = dfd.copy()

### Concat

In [82]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (346482, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2217104  f79cf4f1-6600-4590-9204-532f6cee93ba    60822171040034   
1    2291594  bf7b6fbb-695c-48ea-a56e-a229edf82e61    60822915940014   
2    3634235  6d640f14-ffd2-43a3-b1e4-62ec3e82b5d9    60836342350017   
3    3644784  9ff96c42-674b-487e-9e4a-cbb16b165045    60836447840016   
4    3644816  2976be11-1111-40ad-9cac-877b2d01abeb    60836448160017   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.12253237264131246   2025-08-26 17:17:58   
1  alpha_stack_model_sil   0.06756078826927069   2025-08-26 16:29:08   
2  alpha_stack_model_sil   0.03224989422262025   2025-08-26 16:43:52   
3  alpha_stack_model_sil    0.0953431772839386   2025-08-26 15:38:32   
4  alpha_stack_model_sil   0.04555704698415861   2025-08-26 15:38:29   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-08-26           2025-08           Test         0   
1       2025-08-26           2025-08           Test         0   
2       2025-08-26           2025-08           Test         1   
3       2025-08-26           2025-08           Test         1   
4       2025-08-26           2025-08           Test         0   

   flg_mature_fpd0   new_loan_type modelVersionId trenchCategory  \
0                1     SIL-Instore             v1            ALL   
1                1     SIL-Instore             v1            ALL   
2                1  SIL Competitor             v1            ALL   
3                1     SIL-Instore             v1            ALL   
4                1  SIL Competitor             v1            ALL   

  loan_product_type  flg_mature_fpd10  
0         Appliance              <NA>  
1         Appliance              <NA>  
2              Mall              <NA>  
3         Appliance              <NA>  
4         Appliance              <NA>

In [83]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance            14398
                                                Mall                  4779
                SIL ZERO        v1              Appliance             2032
                SIL-Instore     v1              Appliance            23181
                                                Mall                  4924
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            29562
                                                Mall                  8641
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [84]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Sil_Alpha_Stack_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [85]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_sil', product='SIL')

In [86]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=0bcc5206-0242-4064-ae29-58269c778f88>

In [87]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=dd977daa-1d99-48ab-aac3-9810d38a40ab>

### FPD30

### Test

In [88]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (38120, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3529423  739e8a3e-b1a3-41bb-afc9-df386f5b0153    60835294230018   
1    3529497  07c9b0ce-2976-49de-983f-60979714f4f6    60835294970016   
2    3529490  0bed6ad2-127e-4962-9217-3c4790ef3b6e    60835294900019   
3    3529456  18f3ca19-648c-4a92-9c2b-355aa264774d    60835294560017   
4    3529582  1b02039a-3c20-411e-94dd-78e33d7a836d    60835295820012   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil    0.1373602988355313   2025-06-30 13:05:50   
1  alpha_stack_model_sil   0.04200041578261979   2025-06-30 13:24:36   
2  alpha_stack_model_sil   0.06292534789462584   2025-06-30 13:30:20   
3  alpha_stack_model_sil    0.1497698295850667   2025-06-30 13:11:35   
4  alpha_stack_model_sil   0.05891614384944834   2025-06-30 14:10:16   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-06-30           2025-06           Test         0   
1       2025-06-30           2025-06           Test         0   
2       2025-06-30           2025-06           Test         0   
3       2025-06-30           2025-06           Test         0   
4       2025-06-30           2025-06           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v1            ALL   
1                 1     SIL-Instore             v1            ALL   
2                 1  SIL Competitor             v1            ALL   
3                 1        SIL ZERO             v1            ALL   
4                 1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2              Mall  
3         Appliance  
4         Appliance

In [89]:
df1 = dfd.copy()

### Train

In [90]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (293600, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2247264  8c79ea25-22d8-449a-8fd4-11d2b658f5a7    60822472640018   
1     2285698  f58d7c3b-0ffe-480f-8a96-d527383cf340    60822856980012   
2     2394520  7c81bcb2-9874-4164-be7c-5e75b59aee83    60823945200014   
3     2395883  311f564d-fc66-4f0a-9b19-292c1b42f845    60823958830012   
4     2393811  673c4173-225f-4541-a075-c7db0ed82645    60823938110018   

        modelDisplayName  Sil_Alpha_Stack_score appln_submit_datetime  \
0  Alpha - StackingModel               0.249668   2023-09-25 11:27:10   
1  Alpha - StackingModel               0.219559   2023-10-27 12:45:58   
2  Alpha - StackingModel               0.057626   2024-02-09 11:33:57   
3  Alpha - StackingModel               0.152820   2024-02-10 14:20:02   
4  Alpha - StackingModel               0.108917   2024-02-08 15:34:14   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2023-09-25           2023-09          Train         0   
1       2023-10-27           2023-10          Train         0   
2       2024-02-09           2024-02          Train         0   
3       2024-02-10           2024-02          Train         1   
4       2024-02-08           2024-02          Train         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [91]:
df2 = dfd.copy()

### Concat

In [92]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (331720, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3529423  739e8a3e-b1a3-41bb-afc9-df386f5b0153    60835294230018   
1    3529497  07c9b0ce-2976-49de-983f-60979714f4f6    60835294970016   
2    3529490  0bed6ad2-127e-4962-9217-3c4790ef3b6e    60835294900019   
3    3529456  18f3ca19-648c-4a92-9c2b-355aa264774d    60835294560017   
4    3529582  1b02039a-3c20-411e-94dd-78e33d7a836d    60835295820012   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil    0.1373602988355313   2025-06-30 13:05:50   
1  alpha_stack_model_sil   0.04200041578261979   2025-06-30 13:24:36   
2  alpha_stack_model_sil   0.06292534789462584   2025-06-30 13:30:20   
3  alpha_stack_model_sil    0.1497698295850667   2025-06-30 13:11:35   
4  alpha_stack_model_sil   0.05891614384944834   2025-06-30 14:10:16   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-06-30           2025-06           Test         0   
1       2025-06-30           2025-06           Test         0   
2       2025-06-30           2025-06           Test         0   
3       2025-06-30           2025-06           Test         0   
4       2025-06-30           2025-06           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v1            ALL   
1                 1     SIL-Instore             v1            ALL   
2                 1  SIL Competitor             v1            ALL   
3                 1        SIL ZERO             v1            ALL   
4                 1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2              Mall  
3         Appliance  
4         Appliance

In [93]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance            10847
                                                Mall                  3601
                SIL ZERO        v1              Appliance             1683
                SIL-Instore     v1              Appliance            18177
                                                Mall                  3812
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            28395
                                                Mall                  8305
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [94]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Sil_Alpha_Stack_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [95]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_sil', product='SIL')

In [96]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=68ca5411-7b00-4879-957e-122f0d1a4f73>

In [97]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=c569e9e7-536f-4337-b02f-7ae7aaeb108f>

### FSPD30

### Test

In [98]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (29170, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3667643  4f9d9181-a9f3-4550-b2d0-9cd5f47c7e8e    60836676430016   
1    3672802  3ed24d4c-71ab-4407-a100-7a93d7ffb0b8    60836728020018   
2    3667766  210089f8-2643-4085-831b-df09ff59ab8f    60836677660016   
3    3664307  0a429fdc-81af-409c-b9ad-30ebb02f4ab1    60836643070011   
4    3668457  11d08ad4-f4fa-4def-b3ca-9069209eb5ee    60836684570011   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.09895705793543404   2025-09-06 13:42:54   
1  alpha_stack_model_sil   0.12294548720421078   2025-09-08 17:39:37   
2  alpha_stack_model_sil   0.10442338200094169   2025-09-06 14:28:15   
3  alpha_stack_model_sil   0.08094164995033039   2025-09-04 19:16:55   
4  alpha_stack_model_sil    0.2376993728917707   2025-09-06 18:40:08   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-06           2025-09           Test          0   
1       2025-09-08           2025-09           Test          0   
2       2025-09-06           2025-09           Test          0   
3       2025-09-04           2025-09           Test          0   
4       2025-09-06           2025-09           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1     SIL-Instore             v1            ALL   
1                   1     SIL-Instore             v1            ALL   
2                   1     SIL-Instore             v1            ALL   
3                   1  SIL Competitor             v1            ALL   
4                   1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2              Mall  
3         Appliance  
4         Appliance

In [99]:
df1 = dfd.copy()

### Train

In [100]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (282811, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2220996  31ab2870-ee6c-4057-8b0b-e00d388fd861    60822209960019   
1     2265190  cf34222a-2617-4cf5-9985-bc09e9d6ab18    60822651900019   
2     2271119  9c99fb46-c98d-452e-8783-007d942b63a1    60822711190011   
3     2237087  1f511b4c-6110-464b-aeac-7234ff0208bf    60822370870014   
4     2175407  8307c082-dff3-4b27-b31a-5e6d18975639    60821754070016   

        modelDisplayName  Sil_Alpha_Stack_score appln_submit_datetime  \
0  Alpha - StackingModel               0.194307   2023-09-04 14:15:55   
1  Alpha - StackingModel               0.055639   2023-10-08 17:41:19   
2  Alpha - StackingModel               0.249187   2023-10-13 16:17:42   
3  Alpha - StackingModel               0.111481   2023-09-17 14:24:37   
4  Alpha - StackingModel               0.085856   2023-08-06 11:43:39   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2023-09-04           2023-09          Train          0   
1       2023-10-08           2023-10          Train          0   
2       2023-10-13           2023-10          Train          0   
3       2023-09-17           2023-09          Train          0   
4       2023-08-06           2023-08          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1   SIL-Instore             v1            ALL   
1                   1   SIL-Instore             v1            ALL   
2                   1   SIL-Instore             v1            ALL   
3                   1   SIL-Instore             v1            ALL   
4                   1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [101]:
df2 = dfd.copy()

### Concat

In [102]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (311981, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3667643  4f9d9181-a9f3-4550-b2d0-9cd5f47c7e8e    60836676430016   
1    3672802  3ed24d4c-71ab-4407-a100-7a93d7ffb0b8    60836728020018   
2    3667766  210089f8-2643-4085-831b-df09ff59ab8f    60836677660016   
3    3664307  0a429fdc-81af-409c-b9ad-30ebb02f4ab1    60836643070011   
4    3668457  11d08ad4-f4fa-4def-b3ca-9069209eb5ee    60836684570011   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.09895705793543404   2025-09-06 13:42:54   
1  alpha_stack_model_sil   0.12294548720421078   2025-09-08 17:39:37   
2  alpha_stack_model_sil   0.10442338200094169   2025-09-06 14:28:15   
3  alpha_stack_model_sil   0.08094164995033039   2025-09-04 19:16:55   
4  alpha_stack_model_sil    0.2376993728917707   2025-09-06 18:40:08   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-06           2025-09           Test          0   
1       2025-09-08           2025-09           Test          0   
2       2025-09-06           2025-09           Test          0   
3       2025-09-04           2025-09           Test          0   
4       2025-09-06           2025-09           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1     SIL-Instore             v1            ALL   
1                   1     SIL-Instore             v1            ALL   
2                   1     SIL-Instore             v1            ALL   
3                   1  SIL Competitor             v1            ALL   
4                   1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2              Mall  
3         Appliance  
4         Appliance

In [103]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             8012
                                                Mall                  2632
                SIL ZERO        v1              Appliance             1340
                SIL-Instore     v1              Appliance            14265
                                                Mall                  2921
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            25148
                                                Mall                  7236
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [104]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Sil_Alpha_Stack_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [105]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_sil', product='SIL')

In [106]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=41cafed4-2b83-45d7-ade1-16c3ad2df2fb>

In [107]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8675e4c8-b8df-415f-8988-641cb97d1f14>

### FSTPD30

### Test

In [108]:
sq = """ 
with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.audit_balance.ml_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (19609, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3407581  90031c09-d0fc-4834-a6cc-9b586530d7e3    60834075810017   
1    3449628  6a3068a3-f376-457f-83bf-5982961acc2f    60834496280013   
2    3347501  5b7d4cc0-6b37-4f69-813b-de5a638f98b5    60833475010015   
3    3440568  e45bb1b5-a23e-46cc-918d-4828295b3634    60834405680012   
4    3415687  888afbb4-c712-4737-b0a4-0b1d609a55a9    60834156870013   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.07422996717366957   2025-04-28 17:52:09   
1  alpha_stack_model_sil   0.12166860444575835   2025-05-21 14:10:14   
2  alpha_stack_model_sil   0.00961616325446733   2025-03-29 18:00:56   
3  alpha_stack_model_sil   0.18242585443422837   2025-05-16 16:45:23   
4  alpha_stack_model_sil   0.05579244790068675   2025-05-03 09:22:14   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-04-28           2025-04           Test           1   
1       2025-05-21           2025-05           Test           0   
2       2025-03-29           2025-03           Test           0   
3       2025-05-16           2025-05           Test           0   
4       2025-05-03           2025-05           Test           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [109]:
df1 = dfd.copy()

### Train

In [110]:
sq = """ 
  with modelname as 
  (SELECT
    customerId,digitalLoanAccountId,prediction Sil_Alpha_Stack_score,start_time,end_time,modelDisplayName,modelVersionId, 
    case when trenchCategory is null then 'ALL' 
        when trenchCategory = ''then 'ALL' 
        else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in  ('Alpha - StackingModel', 'alpha_stack_model_sil')
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Sil_Alpha_Stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Sil_Alpha_Stack_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (271286, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2107018  25868b63-4906-4781-8e55-c230522f7288    60821070180011   
1     2134961  6119ac6f-377f-4068-8d33-ca08e9f8073f    60821349610013   
2     2219465  d6f8bce0-af34-444c-9d98-41f6bf03d8d7    60822194650018   
3     2056538  7b9abb97-a8fb-4cd9-8abb-0e3e8f9f70bb    60820565380014   
4     2185576  d97f7683-6bdb-4546-8d41-3312d2e1151d    60821855760017   

        modelDisplayName  Sil_Alpha_Stack_score appln_submit_datetime  \
0  Alpha - StackingModel               0.153877   2023-06-25 10:27:58   
1  Alpha - StackingModel               0.037748   2023-07-14 12:24:41   
2  Alpha - StackingModel               0.076059   2023-09-03 11:41:04   
3  Alpha - StackingModel               0.081715   2023-05-22 17:31:13   
4  Alpha - StackingModel               0.210655   2023-08-12 14:48:06   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2023-06-25           2023-06          Train           1   
1       2023-07-14           2023-07          Train           0   
2       2023-09-03           2023-09          Train           0   
3       2023-05-22           2023-05          Train           0   
4       2023-08-12           2023-08          Train           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [111]:
df2 = dfd.copy()

### Concat

In [112]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (290895, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3407581  90031c09-d0fc-4834-a6cc-9b586530d7e3    60834075810017   
1    3449628  6a3068a3-f376-457f-83bf-5982961acc2f    60834496280013   
2    3347501  5b7d4cc0-6b37-4f69-813b-de5a638f98b5    60833475010015   
3    3440568  e45bb1b5-a23e-46cc-918d-4828295b3634    60834405680012   
4    3415687  888afbb4-c712-4737-b0a4-0b1d609a55a9    60834156870013   

        modelDisplayName Sil_Alpha_Stack_score appln_submit_datetime  \
0  alpha_stack_model_sil   0.07422996717366957   2025-04-28 17:52:09   
1  alpha_stack_model_sil   0.12166860444575835   2025-05-21 14:10:14   
2  alpha_stack_model_sil   0.00961616325446733   2025-03-29 18:00:56   
3  alpha_stack_model_sil   0.18242585443422837   2025-05-16 16:45:23   
4  alpha_stack_model_sil   0.05579244790068675   2025-05-03 09:22:14   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-04-28           2025-04           Test           1   
1       2025-05-21           2025-05           Test           0   
2       2025-03-29           2025-03           Test           0   
3       2025-05-16           2025-05           Test           0   
4       2025-05-03           2025-05           Test           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [113]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             4892
                                                Mall                  1606
                SIL ZERO        v1              Appliance              941
                SIL-Instore     v1              Appliance            10166
                                                Mall                  2004
Train           SIL Competitor  v1              Appliance             4595
                                                Mall                  1104
                                                Mobile                  45
                                v2              Appliance            21623
                                                Mall                  6102
                                                Mobile                  45
                SIL Repeat      v1              Appliance             1224
                                  

In [114]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Sil_Alpha_Stack_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [115]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (9890, 15)
The shape of the dimension table is:	 (175, 10)


In [116]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=28ce71e1-2d76-44b0-a57f-0b6698c03692>

In [117]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=bcce3e16-d0ce-418d-9ea1-26508022e824>

## Beta SIL STACK Score Model

### FPD0

### Test

In [118]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (74390, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3396587  8883bfc1-8a15-492b-a155-a6b3c7352222    60833965870018   
1    3396632  2903344d-e8f4-4fe1-bc1f-21cbfb926ab6    60833966320016   
2    3396909  a11e1a46-c913-4516-b25d-0d00d100b710    60833969090016   
3    3392736  87d8d5ca-ec2c-4b42-85d5-7458abdcb299    60833927360017   
4    3397024  8a50dc4c-7280-4f34-aeb9-295983213d18    60833970240012   

       modelDisplayName sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.09335637546223693   2025-04-23 09:22:56   
1  beta_stack_model_sil   0.0636492865596997   2025-04-23 09:54:05   
2  beta_stack_model_sil  0.07406271617159686   2025-04-23 12:10:42   
3  beta_stack_model_sil  0.10351792987483543   2025-04-23 12:43:49   
4  beta_stack_model_sil  0.09644128204927542   2025-04-23 12:45:10   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-04-23           2025-04           Test        1                1   
1       2025-04-23           2025-04           Test        1                1   
2       2025-04-23           2025-04           Test        0                1   
3       2025-04-23           2025-04           Test        0                1   
4       2025-04-23           2025-04           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL              Mall  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL              Mall

In [119]:
df1 = dfd.copy()

### Train

In [120]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (431652, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1929023  6025c590-9b85-45bf-b1b0-97676ea9a116    60819290230016   
1     1864854  b1da3ade-b822-4d01-97e8-e10fa68a9045    60818648540011   
2     2120842  ee527c36-226d-4d1c-a3ac-d562904fc0ec    60821208420016   
3     2025262  2017032e-c41a-4b13-8a3d-fa161caa3c4c    60820252620016   
4     1871004  02ab20c0-940a-4be9-9584-6cb7786cb55b    60818710040011   

         modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  Beta - StackScoreModel              0.078884   2023-03-05 12:56:56   
1  Beta - StackScoreModel              0.182797   2023-01-17 18:33:32   
2  Beta - StackScoreModel              0.040044   2023-07-05 18:53:11   
3  Beta - StackScoreModel              0.059480   2023-05-02 19:36:21   
4  Beta - StackScoreModel              0.076707   2023-01-23 11:48:54   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2023-03-05           2023-03          Train        0                1   
1       2023-01-17           2023-01          Train        0                1   
2       2023-07-05           2023-07          Train        0                1   
3       2023-05-02           2023-05          Train        0                1   
4       2023-01-23           2023-01          Train        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [121]:
df2 = dfd.copy()

### Concat

In [122]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (506042, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3396587  8883bfc1-8a15-492b-a155-a6b3c7352222    60833965870018   
1    3396632  2903344d-e8f4-4fe1-bc1f-21cbfb926ab6    60833966320016   
2    3396909  a11e1a46-c913-4516-b25d-0d00d100b710    60833969090016   
3    3392736  87d8d5ca-ec2c-4b42-85d5-7458abdcb299    60833927360017   
4    3397024  8a50dc4c-7280-4f34-aeb9-295983213d18    60833970240012   

       modelDisplayName sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.09335637546223693   2025-04-23 09:22:56   
1  beta_stack_model_sil   0.0636492865596997   2025-04-23 09:54:05   
2  beta_stack_model_sil  0.07406271617159686   2025-04-23 12:10:42   
3  beta_stack_model_sil  0.10351792987483543   2025-04-23 12:43:49   
4  beta_stack_model_sil  0.09644128204927542   2025-04-23 12:45:10   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-04-23           2025-04           Test        1                1   
1       2025-04-23           2025-04           Test        1                1   
2       2025-04-23           2025-04           Test        0                1   
3       2025-04-23           2025-04           Test        0                1   
4       2025-04-23           2025-04           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL              Mall  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL              Mall

In [123]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'sil_beta_stack_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [124]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             18622
                                                Mall                   5870
                SIL ZERO        v1              Appliance              3184
                SIL-Instore     v1              Appliance             39466
                                                Mall                   7247
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             33525
                                                Mall                   9633
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [125]:
df_concat['new_loan_type'].unique()

array(['SIL-Instore', 'SIL ZERO', 'SIL Competitor', 'SIL Repeat'],
      dtype=object)

In [126]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_stack_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [127]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (11865, 15)
The shape of the dimension table is:	 (175, 10)


In [128]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=53bce0f9-294d-43a4-8ced-7b3f2b5f1de7>

In [129]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=9dc6e354-9540-4ce7-b512-1a2bf212581d>

### FPD10

### Test

In [130]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (74390, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    1650180  8bfd5561-246c-481d-b158-7b99cc8c51eb    60816501800027   
1    3570158  ad61e4af-3f28-439b-baee-bc28b63b10dd    60835701580019   
2    3474381  9021a9d1-a8d5-46e6-83ee-59692dce9451    60834743810014   
3    3793691  3a0b7e9c-96b9-4854-808d-23f97520099d    60837936910019   
4    3465571  30f73c4b-6838-4161-b2b8-39664b10bd8e    60834655710017   

       modelDisplayName sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.09299436156488282   2025-11-08 12:39:14   
1  beta_stack_model_sil  0.03325675207165926   2025-07-21 14:50:09   
2  beta_stack_model_sil  0.07813106850171753   2025-06-02 17:38:30   
3  beta_stack_model_sil  0.03811359984019397   2025-11-05 19:18:22   
4  beta_stack_model_sil  0.13797752719372985   2025-05-29 13:30:03   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-11-08           2025-11           Test         0   
1       2025-07-21           2025-07           Test         0   
2       2025-06-02           2025-06           Test         0   
3       2025-11-05           2025-11           Test         0   
4       2025-05-29           2025-05           Test         1   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1   SIL-Instore             v1            ALL   
1                1   SIL-Instore             v1            ALL   
2                1   SIL-Instore             v1            ALL   
3                1   SIL-Instore             v1            ALL   
4                1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [131]:
df1 = dfd.copy()

### Train

In [132]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (431652, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2107079  49b8448b-2830-40e4-95b4-c4c705c549d7    60821070790013   
1     1897617  35264d86-5d00-4cf2-8065-9262596c6d64    60818976170017   
2     2157139  36232112-4a08-4224-a211-523087e65cde    60821571390013   
3     1797542  678f7245-1eeb-47da-930b-c0ce894a8940    60817975420019   
4     2150701  e45eaf8c-9fc6-414e-8069-30346723fcee    60821507010019   

         modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  Beta - StackScoreModel              0.036150   2023-06-25 11:16:51   
1  Beta - StackScoreModel              0.182145   2023-02-12 15:48:52   
2  Beta - StackScoreModel              0.134372   2023-07-26 16:32:56   
3  Beta - StackScoreModel              0.396474   2023-03-19 10:36:10   
4  Beta - StackScoreModel              0.113042   2023-07-22 19:51:27   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2023-06-25           2023-06          Train         0   
1       2023-02-12           2023-02          Train         0   
2       2023-07-26           2023-07          Train         0   
3       2023-03-19           2023-03          Train         0   
4       2023-07-22           2023-07          Train         1   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [133]:
df2 = dfd.copy()

### Concat

In [134]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (506042, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    1650180  8bfd5561-246c-481d-b158-7b99cc8c51eb    60816501800027   
1    3570158  ad61e4af-3f28-439b-baee-bc28b63b10dd    60835701580019   
2    3474381  9021a9d1-a8d5-46e6-83ee-59692dce9451    60834743810014   
3    3793691  3a0b7e9c-96b9-4854-808d-23f97520099d    60837936910019   
4    3465571  30f73c4b-6838-4161-b2b8-39664b10bd8e    60834655710017   

       modelDisplayName sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.09299436156488282   2025-11-08 12:39:14   
1  beta_stack_model_sil  0.03325675207165926   2025-07-21 14:50:09   
2  beta_stack_model_sil  0.07813106850171753   2025-06-02 17:38:30   
3  beta_stack_model_sil  0.03811359984019397   2025-11-05 19:18:22   
4  beta_stack_model_sil  0.13797752719372985   2025-05-29 13:30:03   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-11-08           2025-11           Test         0   
1       2025-07-21           2025-07           Test         0   
2       2025-06-02           2025-06           Test         0   
3       2025-11-05           2025-11           Test         0   
4       2025-05-29           2025-05           Test         1   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1   SIL-Instore             v1            ALL   
1                1   SIL-Instore             v1            ALL   
2                1   SIL-Instore             v1            ALL   
3                1   SIL-Instore             v1            ALL   
4                1   SIL-Instore             v1            ALL   

  loan_product_type  flg_mature_fpd10  
0         Appliance              <NA>  
1         Appliance              <NA>  
2         Appliance              <NA>  
3         Appliance              <NA>  
4         Appliance              <NA>

In [135]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             18622
                                                Mall                   5870
                SIL ZERO        v1              Appliance              3184
                SIL-Instore     v1              Appliance             39466
                                                Mall                   7247
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             33525
                                                Mall                   9633
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [136]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_stack_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [137]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_sil', product='SIL')

In [138]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=dd8043fe-4c4e-4e5e-926a-1fbf3661d588>

In [139]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=23dcb7e7-84ea-4e35-bb5a-3c5d3b444683>

### FPD30

### Test

In [140]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (58096, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3720849  0aa05ccc-82d2-4bee-8252-e8406cf9038d    60837208490016   
1    3644917  fcb1c6dc-4e1c-4b6b-811d-fd911113236b    60836449170011   
2    3718299  1471365e-8b6e-454a-90b8-cebcc6df0fa4    60837182990015   
3    3719351  487541cc-4751-47e4-9de2-b37e358106ed    60837193510016   
4    3405278  2137740a-1571-4cdd-aea9-0ec307a4038d    60834052780015   

       modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil   0.05288987242724022   2025-10-03 16:03:03   
1  beta_stack_model_sil  0.050149300084673526   2025-08-26 16:25:43   
2  beta_stack_model_sil   0.09177362518700413   2025-10-02 10:51:32   
3  beta_stack_model_sil   0.09615619134120854   2025-10-02 18:30:10   
4  beta_stack_model_sil  0.022108807703646073   2025-04-27 15:06:01   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-03           2025-10           Test         0   
1       2025-08-26           2025-08           Test         0   
2       2025-10-02           2025-10           Test         1   
3       2025-10-02           2025-10           Test         0   
4       2025-04-27           2025-04           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v1            ALL   
1                 1  SIL Competitor             v1            ALL   
2                 1  SIL Competitor             v1            ALL   
3                 1  SIL Competitor             v1            ALL   
4                 1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [141]:
df1 = dfd.copy()

### Train

In [142]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (427331, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     3724471  e4ac0211-d175-4a9e-a4ac-3f80ed1fd07d    60837244710018   
1     3733673  ca203e29-fb47-4691-bf37-2ae5c86db634    60837336730017   
2     3716562  f57995cc-a455-4f49-800a-a77fae54195a    60837165620013   
3     3731718  c46914a9-125f-41b6-9368-039a2bc9b280    60837317180015   
4     3717473  7eb07b41-95db-4346-9372-287a22b0be22    60837174730017   

       modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil              0.569548   2025-10-05 11:47:51   
1  beta_stack_model_sil              0.760878   2025-10-09 16:39:03   
2  beta_stack_model_sil              0.563642   2025-10-01 13:02:24   
3  beta_stack_model_sil              0.373735   2025-10-08 16:15:03   
4  beta_stack_model_sil              0.629138   2025-10-01 18:38:45   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-05           2025-10          Train         0   
1       2025-10-09           2025-10          Train         0   
2       2025-10-01           2025-10          Train         0   
3       2025-10-08           2025-10          Train         0   
4       2025-10-01           2025-10          Train         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1  SIL Competitor             v2       Trench 1   
1                 1     SIL-Instore             v2       Trench 1   
2                 1     SIL-Instore             v2       Trench 1   
3                 1  SIL Competitor             v2       Trench 1   
4                 1     SIL-Instore             v2       Trench 1   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3              Mall  
4         Appliance

In [143]:
df2 = dfd.copy()

### Concat

In [144]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (485427, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3720849  0aa05ccc-82d2-4bee-8252-e8406cf9038d    60837208490016   
1    3644917  fcb1c6dc-4e1c-4b6b-811d-fd911113236b    60836449170011   
2    3718299  1471365e-8b6e-454a-90b8-cebcc6df0fa4    60837182990015   
3    3719351  487541cc-4751-47e4-9de2-b37e358106ed    60837193510016   
4    3405278  2137740a-1571-4cdd-aea9-0ec307a4038d    60834052780015   

       modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil   0.05288987242724022   2025-10-03 16:03:03   
1  beta_stack_model_sil  0.050149300084673526   2025-08-26 16:25:43   
2  beta_stack_model_sil   0.09177362518700413   2025-10-02 10:51:32   
3  beta_stack_model_sil   0.09615619134120854   2025-10-02 18:30:10   
4  beta_stack_model_sil  0.022108807703646073   2025-04-27 15:06:01   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-03           2025-10           Test         0   
1       2025-08-26           2025-08           Test         0   
2       2025-10-02           2025-10           Test         1   
3       2025-10-02           2025-10           Test         0   
4       2025-04-27           2025-04           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v1            ALL   
1                 1  SIL Competitor             v1            ALL   
2                 1  SIL Competitor             v1            ALL   
3                 1  SIL Competitor             v1            ALL   
4                 1     SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [145]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             14005
                                                Mall                   4445
                SIL ZERO        v1              Appliance              2628
                SIL-Instore     v1              Appliance             31331
                                                Mall                   5686
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             32216
                                                Mall                   9278
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [146]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_stack_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [147]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_sil', product='SIL')

In [148]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=566be99f-756e-45eb-9cde-cbfeddc4e4e6>

In [149]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=de33aa7e-2565-4c4a-abea-5a59c7dbf6ce>

### FSPD30

### Test

In [150]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (44805, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3316303  95418f08-9591-4687-b7af-09e732b6d459    60833163030012   
1    3664338  a5872ed1-a008-45d6-b6e6-43d70c488255    60836643380018   
2    3667455  03699ad5-dec4-4971-8820-858ebbf9bfa5    60836674550014   
3    3665873  3d1f7f4e-b17b-414c-acfe-ffcb265ee6f2    60836658730011   
4    3664029  f0d83587-2353-4d64-a721-89e88481bfc6    60836640290018   

       modelDisplayName sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.07295788678668715   2025-09-05 14:55:21   
1  beta_stack_model_sil  0.04805765465512135   2025-09-04 19:38:34   
2  beta_stack_model_sil  0.08097238969066105   2025-09-06 12:36:43   
3  beta_stack_model_sil  0.03717924525968623   2025-09-05 15:36:50   
4  beta_stack_model_sil  0.04977250143760847   2025-09-04 17:11:21   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-05           2025-09           Test          0   
1       2025-09-04           2025-09           Test          0   
2       2025-09-06           2025-09           Test          0   
3       2025-09-05           2025-09           Test          0   
4       2025-09-04           2025-09           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1  SIL Competitor             v1            ALL   
1                   1        SIL ZERO             v1            ALL   
2                   1     SIL-Instore             v1            ALL   
3                   1     SIL-Instore             v1            ALL   
4                   1        SIL ZERO             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [151]:
df1 = dfd.copy()

### Train

In [152]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (414076, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     3657899  b58af653-8ca4-4097-9b11-cea08e59ddef    60836578990013   
1     2098620  f7dc62d1-6536-4fb0-9b62-02a599f8558c    60820986200015   
2     3665344  0e096da2-0f2a-4763-a699-6a45b89491a8    60836653440011   
3     3670404  b4a2c2cd-148b-4f2f-b73d-e796c78a42c4    60836704040011   
4     3656777  4418a042-b62f-457a-a093-dcbacd9fae6f    60836567770011   

         modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0    beta_stack_model_sil              0.188028   2025-09-01 19:03:47   
1  Beta - StackScoreModel              0.076143   2023-06-18 16:57:05   
2    beta_stack_model_sil              0.166888   2025-09-05 12:18:37   
3    beta_stack_model_sil              0.229232   2025-09-07 15:46:26   
4    beta_stack_model_sil              0.361157   2025-09-01 12:45:31   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-01           2025-09          Train          0   
1       2023-06-18           2023-06          Train          0   
2       2025-09-05           2025-09          Train          0   
3       2025-09-07           2025-09          Train          0   
4       2025-09-01           2025-09          Train          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1  SIL Competitor             v2       Trench 1   
1                   1     SIL-Instore             v1            ALL   
2                   1  SIL Competitor             v2       Trench 1   
3                   1  SIL Competitor             v2       Trench 1   
4                   1     SIL-Instore             v2       Trench 1   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [153]:
df2 = dfd.copy()

### Concat

In [154]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (458881, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3316303  95418f08-9591-4687-b7af-09e732b6d459    60833163030012   
1    3664338  a5872ed1-a008-45d6-b6e6-43d70c488255    60836643380018   
2    3667455  03699ad5-dec4-4971-8820-858ebbf9bfa5    60836674550014   
3    3665873  3d1f7f4e-b17b-414c-acfe-ffcb265ee6f2    60836658730011   
4    3664029  f0d83587-2353-4d64-a721-89e88481bfc6    60836640290018   

       modelDisplayName sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.07295788678668715   2025-09-05 14:55:21   
1  beta_stack_model_sil  0.04805765465512135   2025-09-04 19:38:34   
2  beta_stack_model_sil  0.08097238969066105   2025-09-06 12:36:43   
3  beta_stack_model_sil  0.03717924525968623   2025-09-05 15:36:50   
4  beta_stack_model_sil  0.04977250143760847   2025-09-04 17:11:21   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-05           2025-09           Test          0   
1       2025-09-04           2025-09           Test          0   
2       2025-09-06           2025-09           Test          0   
3       2025-09-05           2025-09           Test          0   
4       2025-09-04           2025-09           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1  SIL Competitor             v1            ALL   
1                   1        SIL ZERO             v1            ALL   
2                   1     SIL-Instore             v1            ALL   
3                   1     SIL-Instore             v1            ALL   
4                   1        SIL ZERO             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [155]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             10306
                                                Mall                   3250
                SIL ZERO        v1              Appliance              2106
                SIL-Instore     v1              Appliance             24772
                                                Mall                   4371
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             28521
                                                Mall                   8086
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [156]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_stack_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [157]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_sil', product='SIL')

In [158]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=37b0e5fa-0840-4abf-ab69-224698c331c6>

In [159]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=c4f080a6-1d06-4b22-b025-df9ca250310e>

### FSTPD30

### Test

In [160]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (30595, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3606879  c5b823b4-a2b9-4a3a-836f-cbffbba5bcfd    60836068790011   
1    3603572  c62ab930-a2ec-48a1-be00-44f6e56d106c    60836035720012   
2    3603221  67c928fa-e469-4471-b6fa-0ccfc459d6b5    60836032210012   
3    3452144  e5ced157-e148-4f14-8843-9e9a78bd3455    60834521440015   
4    3381741  64dc0d73-2ee4-402f-a011-75b2a711d917    60833817410015   

       modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.044824363157075324   2025-08-08 11:20:04   
1  beta_stack_model_sil   0.05430837975564202   2025-08-06 17:01:13   
2  beta_stack_model_sil   0.08273620456983281   2025-08-06 15:08:17   
3  beta_stack_model_sil   0.05862410283639893   2025-05-22 19:37:58   
4  beta_stack_model_sil   0.20303947113753779   2025-04-15 18:26:12   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-08           2025-08           Test           0   
1       2025-08-06           2025-08           Test           0   
2       2025-08-06           2025-08           Test           0   
3       2025-05-22           2025-05           Test           0   
4       2025-04-15           2025-04           Test           0   

   flg_mature_fstpd_30   new_loan_type modelVersionId trenchCategory  \
0                    1     SIL-Instore             v1            ALL   
1                    1  SIL Competitor             v1            ALL   
2                    1     SIL-Instore             v1            ALL   
3                    1     SIL-Instore             v1            ALL   
4                    1     SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1         Appliance  
2              Mall  
3              Mall  
4         Appliance

In [161]:
df1 = dfd.copy()

### Train

In [162]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
            case when trenchCategory is null then 'ALL'
         when trenchCategory = '' then 'ALL'
         else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - StackScoreModel', 'beta_stack_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_stack_score,
  modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_stack_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (399872, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2159147  6fc81f9f-3474-4eff-b798-a9f7d52d78f5    60821591470011   
1     2163452  730e6e6a-0591-4173-acf9-5442dcd1deca    60821634520018   
2     1892118  986bec82-9b87-46ee-b7e5-dfcf8db1473b    60818921180013   
3     2007540  a102ccec-7d12-4c58-a436-72b1a026eb43    60820075400017   
4     2004034  d5f2c34e-acef-40ed-a3e7-07a40fe2634b    60820040340012   

         modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  Beta - StackScoreModel              0.096962   2023-07-27 19:07:35   
1  Beta - StackScoreModel              0.195955   2023-07-30 13:36:03   
2  Beta - StackScoreModel              0.058851   2023-02-08 18:16:02   
3  Beta - StackScoreModel              0.218888   2023-04-21 18:31:58   
4  Beta - StackScoreModel              0.127020   2023-04-19 17:37:45   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2023-07-27           2023-07          Train           0   
1       2023-07-30           2023-07          Train           0   
2       2023-02-08           2023-02          Train           0   
3       2023-04-21           2023-04          Train           0   
4       2023-04-19           2023-04          Train           1   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [163]:
df2 = dfd.copy()

### Concat

In [164]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (430467, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3606879  c5b823b4-a2b9-4a3a-836f-cbffbba5bcfd    60836068790011   
1    3603572  c62ab930-a2ec-48a1-be00-44f6e56d106c    60836035720012   
2    3603221  67c928fa-e469-4471-b6fa-0ccfc459d6b5    60836032210012   
3    3452144  e5ced157-e148-4f14-8843-9e9a78bd3455    60834521440015   
4    3381741  64dc0d73-2ee4-402f-a011-75b2a711d917    60833817410015   

       modelDisplayName  sil_beta_stack_score appln_submit_datetime  \
0  beta_stack_model_sil  0.044824363157075324   2025-08-08 11:20:04   
1  beta_stack_model_sil   0.05430837975564202   2025-08-06 17:01:13   
2  beta_stack_model_sil   0.08273620456983281   2025-08-06 15:08:17   
3  beta_stack_model_sil   0.05862410283639893   2025-05-22 19:37:58   
4  beta_stack_model_sil   0.20303947113753779   2025-04-15 18:26:12   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-08           2025-08           Test           0   
1       2025-08-06           2025-08           Test           0   
2       2025-08-06           2025-08           Test           0   
3       2025-05-22           2025-05           Test           0   
4       2025-04-15           2025-04           Test           0   

   flg_mature_fstpd_30   new_loan_type modelVersionId trenchCategory  \
0                    1     SIL-Instore             v1            ALL   
1                    1  SIL Competitor             v1            ALL   
2                    1     SIL-Instore             v1            ALL   
3                    1     SIL-Instore             v1            ALL   
4                    1     SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1         Appliance  
2              Mall  
3              Mall  
4         Appliance

In [165]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance              6358
                                                Mall                   1985
                SIL ZERO        v1              Appliance              1505
                SIL-Instore     v1              Appliance             17705
                                                Mall                   3042
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             24575
                                                Mall                   6823
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [166]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_stack_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [167]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (10231, 15)
The shape of the dimension table is:	 (175, 10)


In [168]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=42d35129-e85d-45dc-9347-0a4fd3078690>

In [169]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=5c125031-4bbf-42f2-8af8-970bf2f0b396>

## Beta Sil App Score

### FPD0

### Test

In [170]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
    case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,

    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
   ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64) as sil_beta_app_score,
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (65529, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3438015  ac0cbff8-323a-41e3-b9e5-a7276d48f3be    60834380150011   
1    3438031  57fb7dda-2157-4cba-a811-a1dc8ef2563e    60834380310011   
2    3438005  a8df8183-f2b3-4ab1-974e-40cbc3125bd2    60834380050019   
3    3438126  5a30255e-726d-4027-a1ff-241a0dcbaf42    60834381260017   
4    3438304  bc4c8159-d2b8-4475-8bd4-5737b4b131f1    60834383040017   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.376520   2025-05-15 11:40:08   
1  apps_score_model_sil            0.423818   2025-05-15 11:41:07   
2  apps_score_model_sil            0.526019   2025-05-15 11:50:10   
3  apps_score_model_sil            0.450542   2025-05-15 12:27:46   
4  apps_score_model_sil            0.470836   2025-05-15 13:51:18   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-05-15           2025-05           Test        0                1   
1       2025-05-15           2025-05           Test        0                1   
2       2025-05-15           2025-05           Test        0                1   
3       2025-05-15           2025-05           Test        0                1   
4       2025-05-15           2025-05           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [171]:
df1 = dfd.copy()

### Train

In [172]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
        case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(cast(prediction as string), "'", '"'), "None", "null") AS prediction_clean
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
    ),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  coalesce(prediction, safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64)) as sil_beta_app_score, 
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (376762, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2157194  41eabbf4-fd6e-4456-bff7-e2f4f0224bb8    60821571940011   
1     2177330  1c6da460-6586-4806-b9ce-0881816db9af    60821773300011   
2     1888417  842390b0-0c41-4b8c-a833-0c7e4a2d97dd    60818884170011   
3     2136221  23f98da6-becf-44c7-934a-e4a70bfc5dc6    60821362210012   
4     2201256  c93cc22c-8f5f-4c67-b7ce-590b1454fc30    60822012560014   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.650250   2023-07-26 16:55:15   
1  apps_score_model_sil            0.551564   2023-08-07 13:02:34   
2  apps_score_model_sil            0.539517   2023-02-06 10:09:39   
3  apps_score_model_sil            0.384648   2023-07-14 10:43:17   
4  apps_score_model_sil            0.521462   2023-08-26 14:50:56   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2023-07-26           2023-07          Train        0                1   
1       2023-08-07           2023-08          Train        0                1   
2       2023-02-06           2023-02          Train        0                1   
3       2023-07-14           2023-07          Train        1                1   
4       2023-08-26           2023-08          Train        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [173]:
df2 = dfd.copy()

### Concat

In [174]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (442291, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3438015  ac0cbff8-323a-41e3-b9e5-a7276d48f3be    60834380150011   
1    3438031  57fb7dda-2157-4cba-a811-a1dc8ef2563e    60834380310011   
2    3438005  a8df8183-f2b3-4ab1-974e-40cbc3125bd2    60834380050019   
3    3438126  5a30255e-726d-4027-a1ff-241a0dcbaf42    60834381260017   
4    3438304  bc4c8159-d2b8-4475-8bd4-5737b4b131f1    60834383040017   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.376520   2025-05-15 11:40:08   
1  apps_score_model_sil            0.423818   2025-05-15 11:41:07   
2  apps_score_model_sil            0.526019   2025-05-15 11:50:10   
3  apps_score_model_sil            0.450542   2025-05-15 12:27:46   
4  apps_score_model_sil            0.470836   2025-05-15 13:51:18   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-05-15           2025-05           Test        0                1   
1       2025-05-15           2025-05           Test        0                1   
2       2025-05-15           2025-05           Test        0                1   
3       2025-05-15           2025-05           Test        0                1   
4       2025-05-15           2025-05           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [175]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'sil_beta_app_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [176]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             16788
                                                Mall                   4774
                SIL ZERO        v1              Appliance              2747
                SIL-Instore     v1              Appliance             35341
                                                Mall                   5866
Train           SIL Competitor  v1              Appliance              4718
                                                Mall                   1007
                                                Mobile                   50
                                v2              Appliance             32975
                                                Mall                   8680
                                                Mobile                   50
                SIL Repeat      v1              Appliance              1129
                      

In [177]:
df_concat['new_loan_type'].unique()

array(['SIL-Instore', 'SIL ZERO', 'SIL Competitor', 'SIL Repeat'],
      dtype=object)

In [178]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_app_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [179]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (12172, 15)
The shape of the dimension table is:	 (188, 10)


In [180]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=b24c3f46-d06a-47aa-9ec5-1c11acace714>

In [181]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=9fad6eb7-2380-4eab-bf64-8aebaec6817d>

### FPD10

### Test

In [182]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
    case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,

    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
   ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64) as sil_beta_app_score,
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (65529, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3743750  617c69f6-219c-4de5-add7-cfc525ab7874    60837437500018   
1    3789657  c24330d3-45f1-486f-8101-bd7f74f2b6de    60837896570016   
2    3797547  27e785b1-5db0-456f-928c-3d15429048ff    60837975470018   
3    3800834  8e425baf-a824-43fb-9081-e5b831aee176    60838008340015   
4    3793505  9bd4f857-20c6-4849-a1bb-4af767e8b904    60837935050012   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.548034   2025-10-14 13:40:43   
1  apps_score_model_sil            0.425508   2025-11-03 18:08:06   
2  apps_score_model_sil            0.399941   2025-11-07 16:44:27   
3  apps_score_model_sil            0.346494   2025-11-09 12:30:30   
4  apps_score_model_sil            0.636669   2025-11-05 17:58:29   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-14           2025-10           Test         0   
1       2025-11-03           2025-11           Test         0   
2       2025-11-07           2025-11           Test         0   
3       2025-11-09           2025-11           Test         0   
4       2025-11-05           2025-11           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1   SIL-Instore             v1            ALL   
1                1   SIL-Instore             v1            ALL   
2                1   SIL-Instore             v1            ALL   
3                1   SIL-Instore             v1            ALL   
4                1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3              Mall  
4         Appliance

In [183]:
df1 = dfd.copy()

### Train

In [184]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
        case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(cast(prediction as string), "'", '"'), "None", "null") AS prediction_clean
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
    ),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  coalesce(prediction, safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64)) as sil_beta_app_score, 
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (370023, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2129178  b69214c2-2ae3-4bba-b942-a6c2905b58bd    60821291780013   
1     1973747  36a4c276-3fef-4ee1-9946-79a8fc524bed    60819737470016   
2     2198661  697e1c2a-ad87-4c4a-8128-fe488e2842bc    60821986610011   
3     2169179  7a1859c1-f559-4498-8b9c-4ee86f8850fb    60821691790014   
4     2065522  3fe094d1-232c-4c18-9975-f137b88fea87    60820655220017   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.466669   2023-07-10 17:18:34   
1  apps_score_model_sil            0.471495   2023-04-02 11:27:11   
2  apps_score_model_sil            0.625250   2023-08-20 11:22:37   
3  apps_score_model_sil            0.479114   2023-08-02 17:32:30   
4  apps_score_model_sil            0.694932   2023-05-28 16:42:49   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2023-07-10           2023-07          Train         0   
1       2023-04-02           2023-04          Train         0   
2       2023-08-20           2023-08          Train         0   
3       2023-08-02           2023-08          Train         0   
4       2023-05-28           2023-05          Train         1   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [185]:
df2 = dfd.copy()

### Concat

In [186]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (435552, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3743750  617c69f6-219c-4de5-add7-cfc525ab7874    60837437500018   
1    3789657  c24330d3-45f1-486f-8101-bd7f74f2b6de    60837896570016   
2    3797547  27e785b1-5db0-456f-928c-3d15429048ff    60837975470018   
3    3800834  8e425baf-a824-43fb-9081-e5b831aee176    60838008340015   
4    3793505  9bd4f857-20c6-4849-a1bb-4af767e8b904    60837935050012   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.548034   2025-10-14 13:40:43   
1  apps_score_model_sil            0.425508   2025-11-03 18:08:06   
2  apps_score_model_sil            0.399941   2025-11-07 16:44:27   
3  apps_score_model_sil            0.346494   2025-11-09 12:30:30   
4  apps_score_model_sil            0.636669   2025-11-05 17:58:29   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-14           2025-10           Test         0   
1       2025-11-03           2025-11           Test         0   
2       2025-11-07           2025-11           Test         0   
3       2025-11-09           2025-11           Test         0   
4       2025-11-05           2025-11           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1   SIL-Instore             v1            ALL   
1                1   SIL-Instore             v1            ALL   
2                1   SIL-Instore             v1            ALL   
3                1   SIL-Instore             v1            ALL   
4                1   SIL-Instore             v1            ALL   

  loan_product_type  flg_mature_fpd10  
0         Appliance              <NA>  
1         Appliance              <NA>  
2         Appliance              <NA>  
3              Mall              <NA>  
4         Appliance              <NA>

In [187]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             16788
                                                Mall                   4774
                SIL ZERO        v1              Appliance              2747
                SIL-Instore     v1              Appliance             35341
                                                Mall                   5866
Train           SIL Competitor  v1              Appliance              4718
                                                Mall                   1007
                                                Mobile                   50
                                v2              Appliance             31129
                                                Mall                   8183
                                                Mobile                   50
                SIL Repeat      v1              Appliance              1129
                      

In [188]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_app_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [189]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_model_sil', product='SIL')

In [190]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=2005ce5c-ad3f-4df4-9840-15dd85fa66c2>

In [191]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8782b8c7-fdbc-42d1-be7a-732c4af99dbd>

### FPD30

### Test

In [192]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
    case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,

    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
   ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64) as sil_beta_app_score,
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (51169, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3431691  14fc254d-3bd4-4527-bab5-191c38d3cb0a    60834316910013   
1    3489521  7250a467-f015-4d2e-aae2-6ab6e0a4037f    60834895210013   
2    3432887  51e50e8d-72ea-4ab2-93c6-8646f2391ac7    60834328870017   
3    3575481  85f2ab28-fafd-4667-a1d0-2e1485603ddc    60835754810017   
4    3450339  d2d08301-1c2b-450f-9215-748d609906e8    60834503390016   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.512617   2025-05-11 16:07:56   
1  apps_score_model_sil            0.567587   2025-06-10 17:42:15   
2  apps_score_model_sil            0.485154   2025-05-12 12:16:28   
3  apps_score_model_sil            0.537053   2025-07-24 14:49:26   
4  apps_score_model_sil            0.422946   2025-05-21 19:08:59   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-05-11           2025-05           Test         0   
1       2025-06-10           2025-06           Test         0   
2       2025-05-12           2025-05           Test         0   
3       2025-07-24           2025-07           Test         0   
4       2025-05-21           2025-05           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [193]:
df1 = dfd.copy()

### Train

In [194]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
        case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(cast(prediction as string), "'", '"'), "None", "null") AS prediction_clean
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
    ),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  coalesce(prediction, safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64)) as sil_beta_app_score, 
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (361395, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2065194  71d1a2d3-d5c0-465e-a923-17a4cc7fd818    60820651940011   
1     2214071  e6a10337-13db-405c-b639-63fa02f4f1f4    60822140710014   
2     2198670  09f93ec1-3a5c-4072-abfa-bb9139ed69b1    60821986700011   
3     2117998  fe48f427-9b3c-42af-988b-158b07641da4    60821179980018   
4     2117543  a2b5df77-5a09-48d2-8f59-d040698c3a61    60821175430011   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.620883   2023-05-28 14:10:16   
1  apps_score_model_sil            0.315278   2023-08-30 12:05:01   
2  apps_score_model_sil            0.608525   2023-08-20 11:20:47   
3  apps_score_model_sil            0.385577   2023-07-03 18:01:21   
4  apps_score_model_sil            0.592476   2023-07-03 13:29:56   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2023-05-28           2023-05          Train         0   
1       2023-08-30           2023-08          Train         0   
2       2023-08-20           2023-08          Train         0   
3       2023-07-03           2023-07          Train         0   
4       2023-07-03           2023-07          Train         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [195]:
df2 = dfd.copy()

### Concat

In [196]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (412564, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3431691  14fc254d-3bd4-4527-bab5-191c38d3cb0a    60834316910013   
1    3489521  7250a467-f015-4d2e-aae2-6ab6e0a4037f    60834895210013   
2    3432887  51e50e8d-72ea-4ab2-93c6-8646f2391ac7    60834328870017   
3    3575481  85f2ab28-fafd-4667-a1d0-2e1485603ddc    60835754810017   
4    3450339  d2d08301-1c2b-450f-9215-748d609906e8    60834503390016   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.512617   2025-05-11 16:07:56   
1  apps_score_model_sil            0.567587   2025-06-10 17:42:15   
2  apps_score_model_sil            0.485154   2025-05-12 12:16:28   
3  apps_score_model_sil            0.537053   2025-07-24 14:49:26   
4  apps_score_model_sil            0.422946   2025-05-21 19:08:59   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-05-11           2025-05           Test         0   
1       2025-06-10           2025-06           Test         0   
2       2025-05-12           2025-05           Test         0   
3       2025-07-24           2025-07           Test         0   
4       2025-05-21           2025-05           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [197]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             12616
                                                Mall                   3628
                SIL ZERO        v1              Appliance              2275
                SIL-Instore     v1              Appliance             28037
                                                Mall                   4601
Train           SIL Competitor  v1              Appliance              4718
                                                Mall                   1007
                                                Mobile                   50
                                v2              Appliance             28806
                                                Mall                   7535
                                                Mobile                   50
                SIL Repeat      v1              Appliance              1129
                      

In [198]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_app_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [199]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_model_sil', product='SIL')

In [200]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=30c62415-d19e-42bb-b195-fc4537b52a97>

In [201]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=e8eaad84-45d8-4321-8d88-6122e7c8f09e>

### FSPD30

### Test

In [202]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
    case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,

    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
   ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64) as sil_beta_app_score,
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (39372, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3664338  a5872ed1-a008-45d6-b6e6-43d70c488255    60836643380018   
1    3667455  03699ad5-dec4-4971-8820-858ebbf9bfa5    60836674550014   
2    3664029  f0d83587-2353-4d64-a721-89e88481bfc6    60836640290018   
3    3667324  be0913e6-ae5c-49f8-86e6-7017cf6cffe2    60836673240014   
4    3646617  3c2e6eeb-41b2-4f43-8ea8-f82f205b32c9    60836466170011   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.526327   2025-09-04 19:38:34   
1  apps_score_model_sil            0.486146   2025-09-06 12:36:43   
2  apps_score_model_sil            0.387442   2025-09-04 17:11:21   
3  apps_score_model_sil            0.612341   2025-09-06 11:48:09   
4  apps_score_model_sil            0.522413   2025-08-27 17:21:20   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-04           2025-09           Test          0   
1       2025-09-06           2025-09           Test          0   
2       2025-09-04           2025-09           Test          0   
3       2025-09-06           2025-09           Test          0   
4       2025-08-27           2025-08           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1        SIL ZERO             v1            ALL   
1                   1     SIL-Instore             v1            ALL   
2                   1        SIL ZERO             v1            ALL   
3                   1  SIL Competitor             v1            ALL   
4                   1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [203]:
df1 = dfd.copy()

### Train

In [204]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
        case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(cast(prediction as string), "'", '"'), "None", "null") AS prediction_clean
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
    ),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  coalesce(prediction, safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64)) as sil_beta_app_score, 
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (348541, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1917154  343d84b7-ddf8-4992-a77c-3c34c6ad3116    60819171540013   
1     2025135  41b3cc36-24f4-4691-9e53-37140a084ff4    60820251350011   
2     2109962  11ed3c5d-fe0d-44dd-bdeb-2064237407e7    60821099620019   
3     1878133  e710c269-ed84-4a5b-a997-23446995f249    60818781330016   
4     2079178  d837179c-92a9-47aa-9f86-cc360b7e18f5    60820791780012   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.455035   2023-02-25 18:23:09   
1  apps_score_model_sil            0.575271   2023-05-02 18:30:34   
2  apps_score_model_sil            0.558414   2023-06-27 17:26:24   
3  apps_score_model_sil            0.460506   2023-01-29 15:40:53   
4  apps_score_model_sil            0.411032   2023-06-05 17:50:37   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2023-02-25           2023-02          Train          0   
1       2023-05-02           2023-05          Train          0   
2       2023-06-27           2023-06          Train          0   
3       2023-01-29           2023-01          Train          0   
4       2023-06-05           2023-06          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1   SIL-Instore             v1            ALL   
1                   1   SIL-Instore             v1            ALL   
2                   1   SIL-Instore             v1            ALL   
3                   1   SIL-Instore             v1            ALL   
4                   1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [205]:
df2 = dfd.copy()

### Concat

In [206]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (387913, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3664338  a5872ed1-a008-45d6-b6e6-43d70c488255    60836643380018   
1    3667455  03699ad5-dec4-4971-8820-858ebbf9bfa5    60836674550014   
2    3664029  f0d83587-2353-4d64-a721-89e88481bfc6    60836640290018   
3    3667324  be0913e6-ae5c-49f8-86e6-7017cf6cffe2    60836673240014   
4    3646617  3c2e6eeb-41b2-4f43-8ea8-f82f205b32c9    60836466170011   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.526327   2025-09-04 19:38:34   
1  apps_score_model_sil            0.486146   2025-09-06 12:36:43   
2  apps_score_model_sil            0.387442   2025-09-04 17:11:21   
3  apps_score_model_sil            0.612341   2025-09-06 11:48:09   
4  apps_score_model_sil            0.522413   2025-08-27 17:21:20   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-04           2025-09           Test          0   
1       2025-09-06           2025-09           Test          0   
2       2025-09-04           2025-09           Test          0   
3       2025-09-06           2025-09           Test          0   
4       2025-08-27           2025-08           Test          0   

   flg_mature_fspd_30   new_loan_type modelVersionId trenchCategory  \
0                   1        SIL ZERO             v1            ALL   
1                   1     SIL-Instore             v1            ALL   
2                   1        SIL ZERO             v1            ALL   
3                   1  SIL Competitor             v1            ALL   
4                   1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [207]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance              9284
                                                Mall                   2647
                SIL ZERO        v1              Appliance              1818
                SIL-Instore     v1              Appliance             22101
                                                Mall                   3510
Train           SIL Competitor  v1              Appliance              4718
                                                Mall                   1007
                                                Mobile                   50
                                v2              Appliance             25478
                                                Mall                   6557
                                                Mobile                   50
                SIL Repeat      v1              Appliance              1129
                      

In [208]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_app_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [209]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_model_sil', product='SIL')

In [210]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=c1b19a8b-d0b2-4527-8103-fdff16770588>

In [211]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=3f82b7ca-b021-4fdb-85b7-b8323d1a6d1f>

### FSTPD30

### Test

In [212]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
    case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,

    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
   ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64) as sil_beta_app_score,
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (26853, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3606934  116add38-991d-460f-953a-cdde2c67afe8    60836069340011   
1    3393038  ca680779-eed1-478b-9ab2-1ed52ea4fb89    60833930380012   
2    3607395  ebc49383-8aaa-4529-8f6a-a3ed216133a4    60836073950019   
3    3382644  113bc519-7dd7-4d88-870e-76c67548fe9e    60833826440019   
4    3601372  3e289618-9157-47ff-af20-b4a8cce0f86f    60836013720018   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.524990   2025-08-08 11:59:34   
1  apps_score_model_sil            0.513952   2025-04-21 13:47:33   
2  apps_score_model_sil            0.617742   2025-08-08 14:59:02   
3  apps_score_model_sil            0.538290   2025-04-16 11:17:31   
4  apps_score_model_sil            0.452687   2025-08-05 16:41:46   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-08           2025-08           Test           0   
1       2025-04-21           2025-04           Test           0   
2       2025-08-08           2025-08           Test           0   
3       2025-04-16           2025-04           Test           1   
4       2025-08-06           2025-08           Test           0   

   flg_mature_fstpd_30   new_loan_type modelVersionId trenchCategory  \
0                    1     SIL-Instore             v1            ALL   
1                    1     SIL-Instore             v1            ALL   
2                    1  SIL Competitor             v1            ALL   
3                    1     SIL-Instore             v1            ALL   
4                    1     SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1              Mall  
2         Appliance  
3         Appliance  
4         Appliance

In [213]:
df1 = dfd.copy()

### Train

In [214]:
sq = """ 
WITH cleaned AS (
  SELECT
    customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
        case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
    REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature,
    REPLACE(REPLACE(cast(prediction as string), "'", '"'), "None", "null") AS prediction_clean
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - AppsScoreModel', 'apps_score_model_sil')
    ),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  coalesce(prediction, safe_cast(JSON_VALUE(prediction_clean, "$.combined_score") AS float64)) as sil_beta_app_score, 
  case when modelDisplayName = 'Beta - AppsScoreModel' then 'apps_score_model_sil'
       else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_app_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (335033, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2065194  71d1a2d3-d5c0-465e-a923-17a4cc7fd818    60820651940011   
1     2117998  fe48f427-9b3c-42af-988b-158b07641da4    60821179980018   
2     2117543  a2b5df77-5a09-48d2-8f59-d040698c3a61    60821175430011   
3     1968323  75d352e3-89e5-445d-8b5a-ee769f52c4d8    60819683230011   
4     1891979  07d71b05-eebb-4e3f-b2c9-77a057d91539    60818919790016   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.620883   2023-05-28 14:10:16   
1  apps_score_model_sil            0.385577   2023-07-03 18:01:21   
2  apps_score_model_sil            0.592476   2023-07-03 13:29:56   
3  apps_score_model_sil            0.525730   2023-03-30 12:17:45   
4  apps_score_model_sil            0.447169   2023-02-08 16:19:56   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2023-05-28           2023-05          Train           0   
1       2023-07-03           2023-07          Train           0   
2       2023-07-03           2023-07          Train           0   
3       2023-03-30           2023-03          Train           1   
4       2023-02-08           2023-02          Train           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [215]:
df2 = dfd.copy()

### Concat

In [216]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (361886, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3606934  116add38-991d-460f-953a-cdde2c67afe8    60836069340011   
1    3393038  ca680779-eed1-478b-9ab2-1ed52ea4fb89    60833930380012   
2    3607395  ebc49383-8aaa-4529-8f6a-a3ed216133a4    60836073950019   
3    3382644  113bc519-7dd7-4d88-870e-76c67548fe9e    60833826440019   
4    3601372  3e289618-9157-47ff-af20-b4a8cce0f86f    60836013720018   

       modelDisplayName  sil_beta_app_score appln_submit_datetime  \
0  apps_score_model_sil            0.524990   2025-08-08 11:59:34   
1  apps_score_model_sil            0.513952   2025-04-21 13:47:33   
2  apps_score_model_sil            0.617742   2025-08-08 14:59:02   
3  apps_score_model_sil            0.538290   2025-04-16 11:17:31   
4  apps_score_model_sil            0.452687   2025-08-05 16:41:46   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-08           2025-08           Test           0   
1       2025-04-21           2025-04           Test           0   
2       2025-08-08           2025-08           Test           0   
3       2025-04-16           2025-04           Test           1   
4       2025-08-06           2025-08           Test           0   

   flg_mature_fstpd_30   new_loan_type modelVersionId trenchCategory  \
0                    1     SIL-Instore             v1            ALL   
1                    1     SIL-Instore             v1            ALL   
2                    1  SIL Competitor             v1            ALL   
3                    1     SIL-Instore             v1            ALL   
4                    1     SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1              Mall  
2         Appliance  
3         Appliance  
4         Appliance

In [217]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance              5732
                                                Mall                   1586
                SIL ZERO        v1              Appliance              1310
                SIL-Instore     v1              Appliance             15812
                                                Mall                   2401
Train           SIL Competitor  v1              Appliance              4718
                                                Mall                   1007
                                                Mobile                   50
                                v2              Appliance             21927
                                                Mall                   5498
                                                Mobile                   50
                SIL Repeat      v1              Appliance              1129
                      

In [218]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_app_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [219]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (10010, 15)
The shape of the dimension table is:	 (188, 10)


In [220]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=56149265-18b3-4a8d-be52-c7867ff74484>

In [221]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=1eb5a960-2410-4688-88e4-9ef0bfe1a052>

# Beta SIL Demo Score

### FPD0

### Test

In [222]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (74390, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2054362  63651091-b874-4027-8a18-23d8750a3fd8    60820543620044   
1    2351236  37c7748a-9368-44c0-b085-6a29a85897d5    60823512360029   
2    2395940  aff8c182-3aab-470d-a20c-1e47862dfd13    60823959400022   
3    2395948  83c53ee9-6019-4bb3-8c7e-0dc28d007c15    60823959480021   
4    2548208  887737eb-8b14-4895-a49a-bd8ad0392d13    60825482080012   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.1265775507   2025-06-06 10:59:40   
1  beta_demo_model_sil        0.0904819316   2025-06-06 13:28:51   
2  beta_demo_model_sil        0.1308548204   2025-06-06 11:20:23   
3  beta_demo_model_sil        0.1877443231   2025-06-06 13:21:29   
4  beta_demo_model_sil        0.1672469584   2025-06-06 14:30:03   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-06-06           2025-06           Test        0                1   
1       2025-06-06           2025-06           Test        0                1   
2       2025-06-06           2025-06           Test        1                1   
3       2025-06-06           2025-06           Test        1                1   
4       2025-06-06           2025-06           Test        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL              Mall

In [223]:
df1 = dfd.copy()

### Train

In [224]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  case when modelDisplayName = 'Beta - DemoScoreModel' then 'beta_demo_model_sil' else modelDisplayName end as modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (432869, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2203567  8ee62498-6c5e-4f83-85e6-4f3df81ec8ec    60822035670014   
1     1997748  8e52532f-f642-4789-b331-4b91db0cbed5    60819977480013   
2     2147251  6d02a641-f415-4404-ab84-8aa0c04576cf    60821472510017   
3     1835069  bcb838ae-ca45-4a05-a28b-9ca1605f5402    60818350690021   
4     2205358  a84032a6-f60c-48af-a440-282ccc345066    60822053580015   

      modelDisplayName  sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil             0.092292   2023-08-23 10:51:24   
1  beta_demo_model_sil             0.086895   2023-04-16 11:17:59   
2  beta_demo_model_sil             0.139366   2023-07-20 16:40:58   
3  beta_demo_model_sil             0.248088   2023-05-28 17:04:12   
4  beta_demo_model_sil             0.095769   2023-08-24 14:37:46   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2023-08-23           2023-08          Train        0                1   
1       2023-04-16           2023-04          Train        0                1   
2       2023-07-20           2023-07          Train        0                1   
3       2023-05-28           2023-05          Train        0                1   
4       2023-08-24           2023-08          Train        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL         Appliance

In [225]:
df2 = dfd.copy()

### Concat

In [226]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (507259, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2054362  63651091-b874-4027-8a18-23d8750a3fd8    60820543620044   
1    2351236  37c7748a-9368-44c0-b085-6a29a85897d5    60823512360029   
2    2395940  aff8c182-3aab-470d-a20c-1e47862dfd13    60823959400022   
3    2395948  83c53ee9-6019-4bb3-8c7e-0dc28d007c15    60823959480021   
4    2548208  887737eb-8b14-4895-a49a-bd8ad0392d13    60825482080012   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.1265775507   2025-06-06 10:59:40   
1  beta_demo_model_sil        0.0904819316   2025-06-06 13:28:51   
2  beta_demo_model_sil        0.1308548204   2025-06-06 11:20:23   
3  beta_demo_model_sil        0.1877443231   2025-06-06 13:21:29   
4  beta_demo_model_sil        0.1672469584   2025-06-06 14:30:03   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-06-06           2025-06           Test        0                1   
1       2025-06-06           2025-06           Test        0                1   
2       2025-06-06           2025-06           Test        1                1   
3       2025-06-06           2025-06           Test        1                1   
4       2025-06-06           2025-06           Test        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0   SIL-Instore             v1            ALL         Appliance  
1   SIL-Instore             v1            ALL         Appliance  
2   SIL-Instore             v1            ALL         Appliance  
3   SIL-Instore             v1            ALL         Appliance  
4   SIL-Instore             v1            ALL              Mall

In [227]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'sil_beta_demo_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [228]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             18622
                                                Mall                   5870
                SIL ZERO        v1              Appliance              3184
                SIL-Instore     v1              Appliance             39466
                                                Mall                   7247
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             33736
                                                Mall                   9713
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [229]:
df_concat['new_loan_type'].unique()

array(['SIL-Instore', 'SIL ZERO', 'SIL Competitor', 'SIL Repeat'],
      dtype=object)

In [230]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_demo_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [231]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (11890, 15)
The shape of the dimension table is:	 (175, 10)


In [232]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=eb16eb8a-c2d8-4751-b424-b0965424ad56>

In [233]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=e145695f-32e9-4682-8993-66907966b022>

### FPD10

### Test

In [234]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (74390, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3742609  fd8d32cd-417b-4dba-9e38-e0cf68aebd1e    60837426090011   
1    3500827  440aa0ed-2215-4043-b81b-0a25626c4d4a    60835008270018   
2    3569876  ed52ffca-5b3b-4227-a3e4-939bcd961649    60835698760013   
3    3630615  415a76ac-87ec-4664-95cf-e083acf1cf31    60836306150019   
4    3503423  c40efaef-2f81-4909-b011-42650913bbec    60835034230014   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0889733495   2025-10-14 14:49:41   
1  beta_demo_model_sil        0.0208679852   2025-06-16 11:44:02   
2  beta_demo_model_sil        0.0849329375   2025-07-21 12:56:51   
3  beta_demo_model_sil        0.1203414947   2025-08-19 14:00:29   
4  beta_demo_model_sil        0.0506546052   2025-06-17 16:02:24   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-14           2025-10           Test         0   
1       2025-06-16           2025-06           Test         0   
2       2025-07-21           2025-07           Test         0   
3       2025-08-19           2025-08           Test         0   
4       2025-06-17           2025-06           Test         0   

   flg_mature_fpd0   new_loan_type modelVersionId trenchCategory  \
0                1     SIL-Instore             v1            ALL   
1                1     SIL-Instore             v1            ALL   
2                1  SIL Competitor             v1            ALL   
3                1  SIL Competitor             v1            ALL   
4                1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [235]:
df1 = dfd.copy()

### Train

In [236]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  case when modelDisplayName = 'Beta - DemoScoreModel' then 'beta_demo_model_sil' else modelDisplayName end as modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (432869, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2170759  3c80d7e5-ebd5-4caa-a7cf-c36c7bd35875    60821707590017   
1     2185659  08ab4a7f-da76-4e48-857d-78681af18286    60821856590019   
2     1887853  7e147530-52cd-4f5f-9c54-4ae611d2ba66    60818878530012   
3     2106137  9788636c-1d26-4828-b030-d18fdf91750d    60821061370012   
4     1861462  4f2404d5-2d6c-4d74-9c03-eadb3c689898    60818614620017   

      modelDisplayName  sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil             0.163745   2023-08-03 14:51:27   
1  beta_demo_model_sil             0.084582   2023-08-12 15:41:07   
2  beta_demo_model_sil             0.044824   2023-02-05 18:52:23   
3  beta_demo_model_sil             0.211567   2023-06-24 13:57:41   
4  beta_demo_model_sil             0.045228   2023-01-14 14:20:17   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2023-08-03           2023-08          Train         0   
1       2023-08-12           2023-08          Train         0   
2       2023-02-05           2023-02          Train         0   
3       2023-06-24           2023-06          Train         0   
4       2023-01-14           2023-01          Train         0   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1   SIL-Instore             v1            ALL   
1                 1   SIL-Instore             v1            ALL   
2                 1   SIL-Instore             v1            ALL   
3                 1   SIL-Instore             v1            ALL   
4                 1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [237]:
df2 = dfd.copy()

### Concat

In [238]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (507259, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3742609  fd8d32cd-417b-4dba-9e38-e0cf68aebd1e    60837426090011   
1    3500827  440aa0ed-2215-4043-b81b-0a25626c4d4a    60835008270018   
2    3569876  ed52ffca-5b3b-4227-a3e4-939bcd961649    60835698760013   
3    3630615  415a76ac-87ec-4664-95cf-e083acf1cf31    60836306150019   
4    3503423  c40efaef-2f81-4909-b011-42650913bbec    60835034230014   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0889733495   2025-10-14 14:49:41   
1  beta_demo_model_sil        0.0208679852   2025-06-16 11:44:02   
2  beta_demo_model_sil        0.0849329375   2025-07-21 12:56:51   
3  beta_demo_model_sil        0.1203414947   2025-08-19 14:00:29   
4  beta_demo_model_sil        0.0506546052   2025-06-17 16:02:24   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-14           2025-10           Test         0   
1       2025-06-16           2025-06           Test         0   
2       2025-07-21           2025-07           Test         0   
3       2025-08-19           2025-08           Test         0   
4       2025-06-17           2025-06           Test         0   

   flg_mature_fpd0   new_loan_type modelVersionId trenchCategory  \
0                1     SIL-Instore             v1            ALL   
1                1     SIL-Instore             v1            ALL   
2                1  SIL Competitor             v1            ALL   
3                1  SIL Competitor             v1            ALL   
4                1  SIL Competitor             v1            ALL   

  loan_product_type  flg_mature_fpd10  
0         Appliance              <NA>  
1         Appliance              <NA>  
2         Appliance              <NA>  
3         Appliance              <NA>  
4         Appliance              <NA>

In [239]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             18622
                                                Mall                   5870
                SIL ZERO        v1              Appliance              3184
                SIL-Instore     v1              Appliance             39466
                                                Mall                   7247
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             33736
                                                Mall                   9713
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [240]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_demo_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [241]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_sil', product='SIL')

In [242]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=1c099e3b-e793-48e8-a89c-7bdfeca697f9>

In [243]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=9aebfd2c-3875-4c4d-9629-06308d341934>

### FPD30

### Test

In [244]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (58096, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3719323  56bb3877-ed71-4608-a0d7-0e666fdf8493    60837193230012   
1    3644966  fe09cbc4-6a46-41e7-bc97-cfaaa30d20cd    60836449660011   
2    3720957  b93553c4-254b-4605-80b7-cc89989d7383    60837209570019   
3    3430038  b3dfb478-dda5-4391-934c-331b226ed457    60834300380016   
4    3644655  477a1a34-dd5f-4921-9868-e160af647fd4    60836446550018   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0612427966   2025-10-02 18:03:26   
1  beta_demo_model_sil        0.1385639572   2025-08-26 16:40:32   
2  beta_demo_model_sil        0.0368944675   2025-10-03 16:34:34   
3  beta_demo_model_sil        0.1434522522   2025-05-10 17:55:59   
4  beta_demo_model_sil        0.0363633269   2025-08-26 14:13:26   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-02           2025-10           Test         0   
1       2025-08-26           2025-08           Test         0   
2       2025-10-03           2025-10           Test         0   
3       2025-05-10           2025-05           Test         0   
4       2025-08-26           2025-08           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v1            ALL   
1                 1     SIL-Instore             v1            ALL   
2                 1     SIL-Instore             v1            ALL   
3                 1     SIL-Instore             v1            ALL   
4                 1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [245]:
df1 = dfd.copy()

### Train

In [246]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  case when modelDisplayName = 'Beta - DemoScoreModel' then 'beta_demo_model_sil' else modelDisplayName end as modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (427768, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     3724912  3f87215f-d98e-4417-a583-04731531f620    60837249120012   
1     3725001  6a130b2c-6c50-41e1-9dcf-ce486f57c103    60837250010016   
2     3724296  0a8b2334-784b-486f-80a7-a116b87249a0    60837242960011   
3     3718072  55fc58b2-d527-4dcc-a3b5-a5f984e218e4    60837180720018   
4     3731740  f7934b6f-48ac-434a-9d92-c1f63feab17d    60837317400013   

      modelDisplayName  sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil             0.640039   2025-10-05 14:16:55   
1  beta_demo_model_sil             0.270990   2025-10-05 14:32:34   
2  beta_demo_model_sil             0.482767   2025-10-05 10:54:48   
3  beta_demo_model_sil             0.411544   2025-10-02 11:08:34   
4  beta_demo_model_sil             0.483678   2025-10-08 16:30:30   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-05           2025-10          Train         0   
1       2025-10-05           2025-10          Train         0   
2       2025-10-05           2025-10          Train         0   
3       2025-10-02           2025-10          Train         0   
4       2025-10-08           2025-10          Train         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v2       Trench 1   
1                 1     SIL-Instore             v2       Trench 1   
2                 1     SIL-Instore             v2       Trench 1   
3                 1  SIL Competitor             v2       Trench 1   
4                 1  SIL Competitor             v2       Trench 1   

  loan_product_type  
0         Appliance  
1              Mall  
2         Appliance  
3         Appliance  
4         Appliance

In [247]:
df2 = dfd.copy()

### Concat

In [248]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (485864, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3719323  56bb3877-ed71-4608-a0d7-0e666fdf8493    60837193230012   
1    3644966  fe09cbc4-6a46-41e7-bc97-cfaaa30d20cd    60836449660011   
2    3720957  b93553c4-254b-4605-80b7-cc89989d7383    60837209570019   
3    3430038  b3dfb478-dda5-4391-934c-331b226ed457    60834300380016   
4    3644655  477a1a34-dd5f-4921-9868-e160af647fd4    60836446550018   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0612427966   2025-10-02 18:03:26   
1  beta_demo_model_sil        0.1385639572   2025-08-26 16:40:32   
2  beta_demo_model_sil        0.0368944675   2025-10-03 16:34:34   
3  beta_demo_model_sil        0.1434522522   2025-05-10 17:55:59   
4  beta_demo_model_sil        0.0363633269   2025-08-26 14:13:26   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-02           2025-10           Test         0   
1       2025-08-26           2025-08           Test         0   
2       2025-10-03           2025-10           Test         0   
3       2025-05-10           2025-05           Test         0   
4       2025-08-26           2025-08           Test         0   

   flg_mature_fpd30   new_loan_type modelVersionId trenchCategory  \
0                 1     SIL-Instore             v1            ALL   
1                 1     SIL-Instore             v1            ALL   
2                 1     SIL-Instore             v1            ALL   
3                 1     SIL-Instore             v1            ALL   
4                 1  SIL Competitor             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [249]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             14005
                                                Mall                   4445
                SIL ZERO        v1              Appliance              2628
                SIL-Instore     v1              Appliance             31331
                                                Mall                   5686
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             32225
                                                Mall                   9283
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [250]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_demo_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [251]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_sil', product='SIL')

In [252]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=4a1c854a-34b9-4cf6-af69-c754baff7494>

In [253]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=14116591-1251-4f12-a645-3af98ebef0aa>

### FSPD30

### Test

In [254]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (44805, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3665224  94013b43-d4a7-4201-ad93-04feb9e1e2d4    60836652240013   
1    3663648  5ef24ef1-e9c8-487e-bd2f-80e3444b0b97    60836636480015   
2    3646444  e30b7d42-d4d4-4fe6-809d-e5d9d830d5ae    60836464440017   
3    3667643  4f9d9181-a9f3-4550-b2d0-9cd5f47c7e8e    60836676430016   
4    3646478  3ad5e65e-7d35-4b67-a9fe-a23d5e1964ce    60836464780017   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0570831722   2025-09-05 11:34:25   
1  beta_demo_model_sil        0.0498420575   2025-09-04 14:48:57   
2  beta_demo_model_sil        0.1259541574   2025-08-27 16:08:16   
3  beta_demo_model_sil        0.0977999347   2025-09-06 13:42:54   
4  beta_demo_model_sil        0.0198869654   2025-08-27 16:05:08   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-05           2025-09           Test          0   
1       2025-09-04           2025-09           Test          0   
2       2025-08-27           2025-08           Test          0   
3       2025-09-06           2025-09           Test          0   
4       2025-08-27           2025-08           Test          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1   SIL-Instore             v1            ALL   
1                   1   SIL-Instore             v1            ALL   
2                   1   SIL-Instore             v1            ALL   
3                   1   SIL-Instore             v1            ALL   
4                   1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [255]:
df1 = dfd.copy()

### Train

In [256]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  case when modelDisplayName = 'Beta - DemoScoreModel' then 'beta_demo_model_sil' else modelDisplayName end as modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (414469, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     3355796  6876e44d-c0e8-4570-98c3-367a45ecccbc    60833557960029   
1     3665483  1746d204-b7fb-4928-95ac-72318e50d1c7    60836654830011   
2     3661306  f2737e64-9081-4fa8-a4af-ecf8585fcc78    60836613060018   
3     3669987  3aa22564-81c1-402b-a079-84ff30b2b40c    60836699870015   
4     1907825  fb5e9de9-8f84-4f40-b36e-03677d76400d    60819078250014   

      modelDisplayName  sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil             0.420363   2025-09-05 09:19:30   
1  beta_demo_model_sil             0.523329   2025-09-05 13:15:58   
2  beta_demo_model_sil             0.284664   2025-09-03 13:03:30   
3  beta_demo_model_sil             0.569435   2025-09-07 13:50:02   
4  beta_demo_model_sil             0.132308   2023-02-19 18:01:03   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-05           2025-09          Train          0   
1       2025-09-05           2025-09          Train          0   
2       2025-09-03           2025-09          Train          0   
3       2025-09-07           2025-09          Train          0   
4       2023-02-19           2023-02          Train          1   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1   SIL-Instore             v2       Trench 3   
1                   1   SIL-Instore             v2       Trench 1   
2                   1   SIL-Instore             v2       Trench 1   
3                   1   SIL-Instore             v2       Trench 1   
4                   1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [257]:
df2 = dfd.copy()

### Concat

In [258]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (459274, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3665224  94013b43-d4a7-4201-ad93-04feb9e1e2d4    60836652240013   
1    3663648  5ef24ef1-e9c8-487e-bd2f-80e3444b0b97    60836636480015   
2    3646444  e30b7d42-d4d4-4fe6-809d-e5d9d830d5ae    60836464440017   
3    3667643  4f9d9181-a9f3-4550-b2d0-9cd5f47c7e8e    60836676430016   
4    3646478  3ad5e65e-7d35-4b67-a9fe-a23d5e1964ce    60836464780017   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0570831722   2025-09-05 11:34:25   
1  beta_demo_model_sil        0.0498420575   2025-09-04 14:48:57   
2  beta_demo_model_sil        0.1259541574   2025-08-27 16:08:16   
3  beta_demo_model_sil        0.0977999347   2025-09-06 13:42:54   
4  beta_demo_model_sil        0.0198869654   2025-08-27 16:05:08   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2025-09-05           2025-09           Test          0   
1       2025-09-04           2025-09           Test          0   
2       2025-08-27           2025-08           Test          0   
3       2025-09-06           2025-09           Test          0   
4       2025-08-27           2025-08           Test          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1   SIL-Instore             v1            ALL   
1                   1   SIL-Instore             v1            ALL   
2                   1   SIL-Instore             v1            ALL   
3                   1   SIL-Instore             v1            ALL   
4                   1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [259]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance             10306
                                                Mall                   3250
                SIL ZERO        v1              Appliance              2106
                SIL-Instore     v1              Appliance             24772
                                                Mall                   4371
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             28526
                                                Mall                   8088
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [260]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_demo_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [261]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_sil', product='SIL')

In [262]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=43db550d-f76a-414b-a826-78256cc2bb92>

In [263]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=6496bd1f-723c-4f06-8f04-edd3b797b071>

### FSTPD30

### Test

In [264]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (30595, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3606879  c5b823b4-a2b9-4a3a-836f-cbffbba5bcfd    60836068790011   
1    3603572  c62ab930-a2ec-48a1-be00-44f6e56d106c    60836035720012   
2    3603221  67c928fa-e469-4471-b6fa-0ccfc459d6b5    60836032210012   
3    3452144  e5ced157-e148-4f14-8843-9e9a78bd3455    60834521440015   
4    3381741  64dc0d73-2ee4-402f-a011-75b2a711d917    60833817410015   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0462201083   2025-08-08 11:20:04   
1  beta_demo_model_sil        0.0553451698   2025-08-06 17:01:13   
2  beta_demo_model_sil        0.0827231193   2025-08-06 15:08:17   
3  beta_demo_model_sil         0.074376438   2025-05-22 19:37:58   
4  beta_demo_model_sil        0.0892592066   2025-04-15 18:26:12   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-08           2025-08           Test           0   
1       2025-08-06           2025-08           Test           0   
2       2025-08-06           2025-08           Test           0   
3       2025-05-22           2025-05           Test           0   
4       2025-04-15           2025-04           Test           0   

   flg_mature_fstpd_30   new_loan_type modelVersionId trenchCategory  \
0                    1     SIL-Instore             v1            ALL   
1                    1  SIL Competitor             v1            ALL   
2                    1     SIL-Instore             v1            ALL   
3                    1     SIL-Instore             v1            ALL   
4                    1     SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1         Appliance  
2              Mall  
3              Mall  
4         Appliance

In [265]:
df1 = dfd.copy()

### Train

In [266]:
sq = """ 
WITH cleaned AS (
  SELECT
  customerId,digitalLoanAccountId,prediction,start_time,end_time,modelDisplayName,modelVersionId,
  case when trenchCategory is null then 'ALL'
 when trenchCategory = '' then 'ALL'
 else trenchCategory end as trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeature_cleaned
  FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
  WHERE modelDisplayName in ('Beta - DemoScoreModel', 'beta_demo_model_sil')
  ), 
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction sil_beta_demo_score,
  case when modelDisplayName = 'Beta - DemoScoreModel' then 'beta_demo_model_sil' else modelDisplayName end as modelDisplayName,
  modelVersionId, trenchCategory,
  from cleaned
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.sil_beta_demo_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.sil_beta_demo_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (400241, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2159147  6fc81f9f-3474-4eff-b798-a9f7d52d78f5    60821591470011   
1     2163452  730e6e6a-0591-4173-acf9-5442dcd1deca    60821634520018   
2     1892118  986bec82-9b87-46ee-b7e5-dfcf8db1473b    60818921180013   
3     2007540  a102ccec-7d12-4c58-a436-72b1a026eb43    60820075400017   
4     2004034  d5f2c34e-acef-40ed-a3e7-07a40fe2634b    60820040340012   

      modelDisplayName  sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil             0.086259   2023-07-27 19:07:35   
1  beta_demo_model_sil             0.109389   2023-07-30 13:36:03   
2  beta_demo_model_sil             0.120230   2023-02-08 18:16:02   
3  beta_demo_model_sil             0.148729   2023-04-21 18:31:58   
4  beta_demo_model_sil             0.136767   2023-04-19 17:37:45   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2023-07-27           2023-07          Train           0   
1       2023-07-30           2023-07          Train           0   
2       2023-02-08           2023-02          Train           0   
3       2023-04-21           2023-04          Train           0   
4       2023-04-19           2023-04          Train           1   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1   SIL-Instore             v1            ALL   
1                    1   SIL-Instore             v1            ALL   
2                    1   SIL-Instore             v1            ALL   
3                    1   SIL-Instore             v1            ALL   
4                    1   SIL-Instore             v1            ALL   

  loan_product_type  
0         Appliance  
1         Appliance  
2         Appliance  
3         Appliance  
4         Appliance

In [267]:
df2 = dfd.copy()

### Concat

In [268]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (430836, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3606879  c5b823b4-a2b9-4a3a-836f-cbffbba5bcfd    60836068790011   
1    3603572  c62ab930-a2ec-48a1-be00-44f6e56d106c    60836035720012   
2    3603221  67c928fa-e469-4471-b6fa-0ccfc459d6b5    60836032210012   
3    3452144  e5ced157-e148-4f14-8843-9e9a78bd3455    60834521440015   
4    3381741  64dc0d73-2ee4-402f-a011-75b2a711d917    60833817410015   

      modelDisplayName sil_beta_demo_score appln_submit_datetime  \
0  beta_demo_model_sil        0.0462201083   2025-08-08 11:20:04   
1  beta_demo_model_sil        0.0553451698   2025-08-06 17:01:13   
2  beta_demo_model_sil        0.0827231193   2025-08-06 15:08:17   
3  beta_demo_model_sil         0.074376438   2025-05-22 19:37:58   
4  beta_demo_model_sil        0.0892592066   2025-04-15 18:26:12   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2025-08-08           2025-08           Test           0   
1       2025-08-06           2025-08           Test           0   
2       2025-08-06           2025-08           Test           0   
3       2025-05-22           2025-05           Test           0   
4       2025-04-15           2025-04           Test           0   

   flg_mature_fstpd_30   new_loan_type modelVersionId trenchCategory  \
0                    1     SIL-Instore             v1            ALL   
1                    1  SIL Competitor             v1            ALL   
2                    1     SIL-Instore             v1            ALL   
3                    1     SIL-Instore             v1            ALL   
4                    1     SIL-Instore             v1            ALL   

  loan_product_type  
0              Mall  
1         Appliance  
2              Mall  
3              Mall  
4         Appliance

In [269]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            SIL Competitor  v1              Appliance              6358
                                                Mall                   1985
                SIL ZERO        v1              Appliance              1505
                SIL-Instore     v1              Appliance             17705
                                                Mall                   3042
Train           SIL Competitor  v1              Appliance              5179
                                                Mall                   1249
                                                Mobile                   52
                                v2              Appliance             24577
                                                Mall                   6823
                                                Mobile                   52
                SIL Repeat      v1              Appliance              1281
                      

In [270]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'sil_beta_demo_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [271]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_sil', product='SIL')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (10231, 15)
The shape of the dimension table is:	 (175, 10)


In [272]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=68e12356-5277-4ff4-a24a-985a0bf4500e>

In [273]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=78776293-b65f-4fae-8822-db9ffe3338a5>

# CASH

# Alpha-Cash-CIC-Model

### FPD0

### Test

In [274]:
sq = r"""
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
--REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aCicScore,
  case when p.modelDisplayName like 'Alpha%' then 'cic_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (3968, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3710316  6a214ab0-f3e6-43bb-953f-a2a62f1dad2d    60837103160017   
1    2356365  d01e4c2d-6453-4ea5-8aa1-98882a04b299    60823563650077   
2    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
3    3307096  e8d69ec8-866a-47c8-a944-067cb83ac800    60833070960021   
4    3710758  abe5f29c-f306-47f0-b43e-4a2cc3d02656    60837107580019   

  modelDisplayName            aCicScore appln_submit_datetime  \
0   cic_model_cash  0.47817705242930436   2025-09-28 13:24:51   
1   cic_model_cash   0.5777952129511873   2025-09-28 22:28:18   
2   cic_model_cash   0.3961675848446604   2025-09-28 18:26:57   
3   cic_model_cash  0.34108436389611596   2025-09-28 17:18:59   
4   cic_model_cash   0.4496536743439154   2025-09-28 17:24:26   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-09-28           2025-09           Test        0                1   
1       2025-09-30           2025-09           Test        0                1   
2       2025-09-28           2025-09           Test        0                1   
3       2025-09-29           2025-09           Test        0                1   
4       2025-09-29           2025-09           Test        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 3    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [275]:
df1 = dfd.copy()

### Train

In [276]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aCicScore,
  case when modelDisplayName like 'Alpha%' then 'cic_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (40128, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2854781  61fcd94a-c8eb-49e7-8113-9a2abecab6d7    60828547810013   
1     2146456  c8561cee-f925-4805-99f4-37c471bf0a44    60821464560014   
2     1901412  2ec56bdb-84d5-4feb-b979-015b1ea392f5    60819014120021   
3     1620906  0b671ae7-7295-4853-8015-c2174935d208    60816209060018   
4     2822595  0e76cf94-51e6-4795-b3c5-4c68bec13fd6    60828225950011   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.641524   2024-09-18 14:00:44       2024-09-23   
1   cic_model_cash   0.484505   2024-09-01 22:52:29       2024-09-02   
2   cic_model_cash   0.473522   2024-09-19 12:10:12       2024-09-19   
3   cic_model_cash   0.492672   2024-09-04 08:38:26       2024-09-05   
4   cic_model_cash   0.435419   2024-09-04 21:04:13       2024-09-06   

  Application_month Data_selection  deffpd0  flg_mature_fpd0 new_loan_type  \
0           2024-09          Train        0                1         Quick   
1           2024-09          Train        0                1         Quick   
2           2024-09          Train        1                1         Quick   
3           2024-09          Train        1                1         Quick   
4           2024-09          Train        1                1         Quick   

  modelVersionId trenchCategory loan_product_type  
0             v1       Trench 1    not applicable  
1             v1       Trench 2    not applicable  
2             v1       Trench 2    not applicable  
3             v1       Trench 2    not applicable  
4             v1       Trench 1    not applicable

In [277]:
df2 = dfd.copy()

### Concat

In [278]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (44096, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3710316  6a214ab0-f3e6-43bb-953f-a2a62f1dad2d    60837103160017   
1    2356365  d01e4c2d-6453-4ea5-8aa1-98882a04b299    60823563650077   
2    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
3    3307096  e8d69ec8-866a-47c8-a944-067cb83ac800    60833070960021   
4    3710758  abe5f29c-f306-47f0-b43e-4a2cc3d02656    60837107580019   

  modelDisplayName            aCicScore appln_submit_datetime  \
0   cic_model_cash  0.47817705242930436   2025-09-28 13:24:51   
1   cic_model_cash   0.5777952129511873   2025-09-28 22:28:18   
2   cic_model_cash   0.3961675848446604   2025-09-28 18:26:57   
3   cic_model_cash  0.34108436389611596   2025-09-28 17:18:59   
4   cic_model_cash   0.4496536743439154   2025-09-28 17:24:26   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-09-28           2025-09           Test        0                1   
1       2025-09-30           2025-09           Test        0                1   
2       2025-09-28           2025-09           Test        0                1   
3       2025-09-29           2025-09           Test        0                1   
4       2025-09-29           2025-09           Test        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 3    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [279]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'aCicScore', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [280]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        3968
Train           Quick          v1              not applicable       40128
Name: digitalLoanAccountId, dtype: int64

In [281]:
df_concat['new_loan_type'].unique()

array(['Quick'], dtype=object)

In [282]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aCicScore', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [283]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (2528, 15)
The shape of the dimension table is:	 (32, 10)


In [284]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=2e2ae243-62bd-4478-990b-6c4b430addfc>

In [285]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8a714981-b4f5-4f18-8c16-34911678c03d>

### FPD10

### Test

In [286]:
sq = r"""
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
--REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aCicScore,
  case when p.modelDisplayName like 'Alpha%' then 'cic_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (3968, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3762085  4371b1c2-171b-4b54-8041-9e5d2c5b1388    60837620850014   
1    3693379  ee12002f-1ad5-47e7-ad5b-669b7dff89d9    60836933790018   
2    2410790  7baa5b0c-725b-4510-9431-ea557e833579    60824107900014   
3    2825504  0942b5cb-f232-446f-be82-9d48b4975391    60828255040013   
4    3572216  134ec65d-9302-4bce-89c1-31902f6a65da    60835722160028   

  modelDisplayName            aCicScore appln_submit_datetime  \
0   cic_model_cash   0.4779141311501369   2025-10-23 08:29:17   
1   cic_model_cash   0.4158921298635784   2025-10-23 08:55:31   
2   cic_model_cash   0.3525422254821958   2025-10-23 09:02:13   
3   cic_model_cash  0.47290540967011496   2025-10-23 09:04:17   
4   cic_model_cash  0.44785785920616455   2025-10-23 09:05:34   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-23           2025-10           Test         0   
1       2025-10-23           2025-10           Test         0   
2       2025-10-29           2025-10           Test         0   
3       2025-10-29           2025-10           Test         0   
4       2025-10-23           2025-10           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 1   
1                1         Quick             v1       Trench 2   
2                1         Quick             v1       Trench 2   
3                1         Quick             v1       Trench 2   
4                1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [287]:
df1 = dfd.copy()

### Train

In [288]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aCicScore,
  case when modelDisplayName like 'Alpha%' then 'cic_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (40126, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2889389  3a565951-4e43-405a-9708-481991215e45    60828893890014   
1     2806618  a68f31c2-7f5e-43c3-9243-f9aad88c9a7c    60828066180032   
2     2846874  bdf8184f-fa97-418e-a0b0-a2dc96927b08    60828468740011   
3     2878574  f6298ab9-0031-4e3d-8da6-16863fe4c4eb    60828785740014   
4     2254685  e48adfbc-fafc-4fbd-8073-768c384d10cf    60822546850026   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.461177   2024-09-29 21:21:11       2024-09-30   
1   cic_model_cash   0.472733   2024-09-12 09:52:50       2024-09-12   
2   cic_model_cash   0.417480   2024-09-15 10:00:11       2024-09-15   
3   cic_model_cash   0.388709   2024-09-25 02:51:52       2024-09-25   
4   cic_model_cash   0.497494   2024-09-21 21:17:31       2024-09-21   

  Application_month Data_selection  deffpd10  flg_mature_fpd10 new_loan_type  \
0           2024-09          Train         0                 1         Quick   
1           2024-09          Train         0                 1         Quick   
2           2024-09          Train         1                 1         Quick   
3           2024-09          Train         0                 1         Quick   
4           2024-09          Train         0                 1         Quick   

  modelVersionId trenchCategory loan_product_type  
0             v1       Trench 1    not applicable  
1             v1       Trench 3    not applicable  
2             v1       Trench 1    not applicable  
3             v1       Trench 1    not applicable  
4             v1       Trench 3    not applicable

In [289]:
df2 = dfd.copy()

### Concat

In [290]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (44094, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3762085  4371b1c2-171b-4b54-8041-9e5d2c5b1388    60837620850014   
1    3693379  ee12002f-1ad5-47e7-ad5b-669b7dff89d9    60836933790018   
2    2410790  7baa5b0c-725b-4510-9431-ea557e833579    60824107900014   
3    2825504  0942b5cb-f232-446f-be82-9d48b4975391    60828255040013   
4    3572216  134ec65d-9302-4bce-89c1-31902f6a65da    60835722160028   

  modelDisplayName            aCicScore appln_submit_datetime  \
0   cic_model_cash   0.4779141311501369   2025-10-23 08:29:17   
1   cic_model_cash   0.4158921298635784   2025-10-23 08:55:31   
2   cic_model_cash   0.3525422254821958   2025-10-23 09:02:13   
3   cic_model_cash  0.47290540967011496   2025-10-23 09:04:17   
4   cic_model_cash  0.44785785920616455   2025-10-23 09:05:34   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-23           2025-10           Test         0   
1       2025-10-23           2025-10           Test         0   
2       2025-10-29           2025-10           Test         0   
3       2025-10-29           2025-10           Test         0   
4       2025-10-23           2025-10           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 1   
1                1         Quick             v1       Trench 2   
2                1         Quick             v1       Trench 2   
3                1         Quick             v1       Trench 2   
4                1         Quick             v1       Trench 2   

  loan_product_type  flg_mature_fpd10  
0    not applicable              <NA>  
1    not applicable              <NA>  
2    not applicable              <NA>  
3    not applicable              <NA>  
4    not applicable              <NA>

In [291]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        3968
Train           Quick          v1              not applicable       40126
Name: digitalLoanAccountId, dtype: int64

In [292]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aCicScore', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [293]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_cash', product='CASH')

In [294]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=34acefb2-bc11-4685-996e-85fd74cc1325>

In [295]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=7732bfd0-d833-4f3f-a3ea-40e71d45c28b>

### FPD30

### Test

In [296]:
sq = r"""
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
--REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aCicScore,
  case when p.modelDisplayName like 'Alpha%' then 'cic_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (89, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3230169  9ed41d23-400d-4654-b0a7-dbd7e514bdfa    60832301690022   
1    3190544  e5324fe5-34e5-4718-803c-84b1b2402b7d    60831905440011   
2    3724716  ebfbd098-aa48-4161-a112-cf2e0b25ba9a    60837247160011   
3    3090214  8b4e0f30-db10-4bff-ba1d-fd96ffdc34b1    60830902140011   
4    3726073  b6e2666e-d8d8-409e-8315-907d922e8d23    60837260730016   

  modelDisplayName            aCicScore appln_submit_datetime  \
0   cic_model_cash   0.4807114066732938   2025-10-05 09:38:47   
1   cic_model_cash  0.39925777456965084   2025-10-05 12:24:42   
2   cic_model_cash  0.45634464860970425   2025-10-05 13:12:34   
3   cic_model_cash   0.5541771663277403   2025-10-05 20:30:05   
4   cic_model_cash   0.4044819242828416   2025-10-05 20:20:43   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-05           2025-10           Test         0   
1       2025-10-06           2025-10           Test         0   
2       2025-10-05           2025-10           Test         0   
3       2025-10-05           2025-10           Test         0   
4       2025-10-06           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 2   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 2   
4                 1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [297]:
df1 = dfd.copy()

### Train

In [298]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aCicScore,
  case when modelDisplayName like 'Alpha%' then 'cic_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (40099, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2876044  31a8605b-f783-4d54-b89c-9dcac0351089    60828760440015   
1     2876868  3ef0ddb9-0af9-4e2d-92a4-6ce32db0859f    60828768680017   
2     2816800  d05f3151-f0b2-4828-8f3d-33d122998410    60828168000017   
3     2842278  38920bd1-fd53-43a2-9ed6-afbdd051d227    60828422780011   
4     2887824  8f51eb69-912c-44c8-aa66-3ebb0dadc0ef    60828878240014   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.427749   2024-09-24 08:52:27       2024-09-24   
1   cic_model_cash   0.511224   2024-09-24 14:32:57       2024-09-24   
2   cic_model_cash   0.479134   2024-09-03 09:19:39       2024-09-03   
3   cic_model_cash   0.504232   2024-09-17 11:19:38       2024-09-17   
4   cic_model_cash   0.423450   2024-09-28 07:58:16       2024-09-28   

  Application_month Data_selection  deffpd30  flg_mature_fpd30 new_loan_type  \
0           2024-09          Train         1                 1         Quick   
1           2024-09          Train         0                 1         Quick   
2           2024-09          Train         0                 1         Quick   
3           2024-09          Train         0                 1         Quick   
4           2024-09          Train         0                 1         Quick   

  modelVersionId trenchCategory loan_product_type  
0             v1       Trench 1    not applicable  
1             v1       Trench 1    not applicable  
2             v1       Trench 1    not applicable  
3             v1       Trench 1    not applicable  
4             v1       Trench 1    not applicable

In [299]:
df2 = dfd.copy()

### Concat

In [300]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (40188, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3230169  9ed41d23-400d-4654-b0a7-dbd7e514bdfa    60832301690022   
1    3190544  e5324fe5-34e5-4718-803c-84b1b2402b7d    60831905440011   
2    3724716  ebfbd098-aa48-4161-a112-cf2e0b25ba9a    60837247160011   
3    3090214  8b4e0f30-db10-4bff-ba1d-fd96ffdc34b1    60830902140011   
4    3726073  b6e2666e-d8d8-409e-8315-907d922e8d23    60837260730016   

  modelDisplayName            aCicScore appln_submit_datetime  \
0   cic_model_cash   0.4807114066732938   2025-10-05 09:38:47   
1   cic_model_cash  0.39925777456965084   2025-10-05 12:24:42   
2   cic_model_cash  0.45634464860970425   2025-10-05 13:12:34   
3   cic_model_cash   0.5541771663277403   2025-10-05 20:30:05   
4   cic_model_cash   0.4044819242828416   2025-10-05 20:20:43   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-05           2025-10           Test         0   
1       2025-10-06           2025-10           Test         0   
2       2025-10-05           2025-10           Test         0   
3       2025-10-05           2025-10           Test         0   
4       2025-10-06           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 2   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 2   
4                 1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [301]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable          89
Train           Quick          v1              not applicable       40099
Name: digitalLoanAccountId, dtype: int64

In [302]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aCicScore', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [303]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_cash', product='CASH')

In [304]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=b8b068e0-7749-4222-8310-f321f5f51ab3>

In [305]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=c6ea5f5e-688b-4b24-8dd3-9730f122c4ad>

### FSPD30

### Test

In [306]:
sq = r"""
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
--REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aCicScore,
  case when p.modelDisplayName like 'Alpha%' then 'cic_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, aCicScore, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffspd30, flg_mature_fspd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [307]:
df1 = dfd.copy()

### Train

In [308]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aCicScore,
  case when modelDisplayName like 'Alpha%' then 'cic_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (37711, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2857943  752a523b-0df3-42df-836c-0553b63a810c    60828579430015   
1     2174562  172210a1-7a29-46ce-b466-9fecdafa8840    60821745620046   
2     2494158  34beb536-3f38-4208-aeab-ce94036e8995    60824941580012   
3     2616060  5c200b02-38cc-4831-9bca-60362ef90eb9    60826160600021   
4     2894371  6d29b8e6-603e-4782-b84f-856f96f5bb47    60828943710019   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.594781   2024-09-18 15:24:50       2024-09-18   
1   cic_model_cash   0.482082   2024-09-16 09:42:06       2024-09-16   
2   cic_model_cash   0.517382   2024-09-09 09:54:20       2024-09-11   
3   cic_model_cash   0.436681   2024-09-28 19:36:17       2024-09-28   
4   cic_model_cash   0.766358   2024-09-30 07:00:34       2024-09-30   

  Application_month Data_selection  deffspd30  flg_mature_fspd_30  \
0           2024-09          Train          1                   1   
1           2024-09          Train          1                   1   
2           2024-09          Train          1                   1   
3           2024-09          Train          0                   1   
4           2024-09          Train          1                   1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 2    not applicable  
2         Quick             v1       Trench 2    not applicable  
3         Quick             v1       Trench 2    not applicable  
4         Quick             v1       Trench 1    not applicable

In [309]:
df2 = dfd.copy()

### Concat

In [310]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (37711, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2857943  752a523b-0df3-42df-836c-0553b63a810c    60828579430015   
1     2174562  172210a1-7a29-46ce-b466-9fecdafa8840    60821745620046   
2     2494158  34beb536-3f38-4208-aeab-ce94036e8995    60824941580012   
3     2616060  5c200b02-38cc-4831-9bca-60362ef90eb9    60826160600021   
4     2894371  6d29b8e6-603e-4782-b84f-856f96f5bb47    60828943710019   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.594781   2024-09-18 15:24:50       2024-09-18   
1   cic_model_cash   0.482082   2024-09-16 09:42:06       2024-09-16   
2   cic_model_cash   0.517382   2024-09-09 09:54:20       2024-09-11   
3   cic_model_cash   0.436681   2024-09-28 19:36:17       2024-09-28   
4   cic_model_cash   0.766358   2024-09-30 07:00:34       2024-09-30   

  Application_month Data_selection  deffspd30  flg_mature_fspd_30  \
0           2024-09          Train          1                   1   
1           2024-09          Train          1                   1   
2           2024-09          Train          1                   1   
3           2024-09          Train          0                   1   
4           2024-09          Train          1                   1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 2    not applicable  
2         Quick             v1       Trench 2    not applicable  
3         Quick             v1       Trench 2    not applicable  
4         Quick             v1       Trench 1    not applicable

In [311]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       37711
Name: digitalLoanAccountId, dtype: int64

In [312]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aCicScore', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [313]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_cash', product='CASH')

In [314]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=d9742036-9ad7-4350-9c48-32606390d06d>

In [315]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8e149e93-1d3d-46fb-b79d-565abce25667>

### FSTPD30

### Test

In [316]:
sq = r"""
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
--REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aCicScore,
  case when p.modelDisplayName like 'Alpha%' then 'cic_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, aCicScore, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffstpd30, flg_mature_fstpd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [317]:
df1 = dfd.copy()

### Train

In [318]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-CIC-Model','Alpha Cash CIC Model','cic_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aCicScore,
  case when modelDisplayName like 'Alpha%' then 'cic_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aCicScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aCicScore is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (34591, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2823628  13487bcc-35bf-4edf-866a-9180dfbf7a9d    60828236280016   
1     2816431  b70fdd85-51d3-40b4-8062-4b7800ce21b9    60828164310012   
2     2846247  143e38da-2ff5-4f03-9c27-a839486fdb57    60828462470019   
3     1739588  9e7bef08-c46a-4307-a7c8-569486b1ef91    60817395880045   
4     2819814  d8cbe09a-af6c-4ec1-a62b-d69d80b1b3f4    60828198140015   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.486590   2024-09-05 13:51:35       2024-09-05   
1   cic_model_cash   0.735493   2024-09-02 12:44:21       2024-09-02   
2   cic_model_cash   0.604074   2024-09-18 05:18:44       2024-09-19   
3   cic_model_cash   0.507028   2024-09-23 11:09:30       2024-09-23   
4   cic_model_cash   0.466235   2024-09-03 15:10:17       2024-09-03   

  Application_month Data_selection  deffstpd30  flg_mature_fstpd_30  \
0           2024-09          Train           0                    1   
1           2024-09          Train           1                    1   
2           2024-09          Train           0                    1   
3           2024-09          Train           0                    1   
4           2024-09          Train           0                    1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [319]:
df2 = dfd.copy()

### Concat

In [320]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (34591, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2823628  13487bcc-35bf-4edf-866a-9180dfbf7a9d    60828236280016   
1     2816431  b70fdd85-51d3-40b4-8062-4b7800ce21b9    60828164310012   
2     2846247  143e38da-2ff5-4f03-9c27-a839486fdb57    60828462470019   
3     1739588  9e7bef08-c46a-4307-a7c8-569486b1ef91    60817395880045   
4     2819814  d8cbe09a-af6c-4ec1-a62b-d69d80b1b3f4    60828198140015   

  modelDisplayName  aCicScore appln_submit_datetime disbursementdate  \
0   cic_model_cash   0.486590   2024-09-05 13:51:35       2024-09-05   
1   cic_model_cash   0.735493   2024-09-02 12:44:21       2024-09-02   
2   cic_model_cash   0.604074   2024-09-18 05:18:44       2024-09-19   
3   cic_model_cash   0.507028   2024-09-23 11:09:30       2024-09-23   
4   cic_model_cash   0.466235   2024-09-03 15:10:17       2024-09-03   

  Application_month Data_selection  deffstpd30  flg_mature_fstpd_30  \
0           2024-09          Train           0                    1   
1           2024-09          Train           1                    1   
2           2024-09          Train           0                    1   
3           2024-09          Train           0                    1   
4           2024-09          Train           0                    1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [321]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       34591
Name: digitalLoanAccountId, dtype: int64

In [322]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aCicScore', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [323]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='cic_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (2040, 15)
The shape of the dimension table is:	 (32, 10)


In [324]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=afa58042-c9a2-43f4-95da-5c5c141715b6>

In [325]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=b1407f5f-1219-456c-abb7-a06580262c5b>

# Alpha-Cash-Stack-Model

### FPD0

### Test

In [326]:
sq = r""" 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (3968, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3705340  026a6ada-efc6-4e5e-968a-0d37e382d9ad    60837053400012   
1    3705891  ec2bf9f2-ee68-44de-9f2e-9690f53ec824    60837058910018   
2    3071399  fc78cc72-651b-4e92-b0df-a906c23fc167    60830713990042   
3    3301484  96d1d523-5824-4b1c-abb7-5c6b43f74c75    60833014840017   
4    3706096  98118b0f-5bae-4544-8a77-f77404a58b50    60837060960013   

         modelDisplayName          aStackScore appln_submit_datetime  \
0  alpha_stack_model_cash  0.37316971605586724   2025-09-26 14:04:27   
1  alpha_stack_model_cash   0.3802428197781405   2025-09-26 14:01:57   
2  alpha_stack_model_cash  0.43455965241990185   2025-09-26 12:34:08   
3  alpha_stack_model_cash  0.30585731391943394   2025-09-26 19:26:32   
4  alpha_stack_model_cash   0.4543684030611348   2025-09-26 17:13:14   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-09-26           2025-09           Test        0                1   
1       2025-10-02           2025-09           Test        1                1   
2       2025-09-26           2025-09           Test        1                1   
3       2025-09-30           2025-09           Test        0                1   
4       2025-09-27           2025-09           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 2    not applicable  
4         Quick             v1       Trench 1    not applicable

In [327]:
df1 = dfd.copy()

### Train

In [328]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  trenchCategory
  from parsed p
  ) ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (36491, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2973387  a016ed33-2086-45d9-9a35-2739303f394f    60829733870019   
1     2231422  182cd65b-ff3e-4514-bc6c-aef821bc193b    60822314220023   
2     2660652  e9b8d38c-0242-4770-b6c2-976b66d5727b    60826606520012   
3     2315941  4e6a9ac2-ed71-4122-90de-1d02c878d017    60823159410015   
4     2911289  92cef2ac-9ab6-45ca-a55b-9caa2b597008    60829112890011   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.587061   2024-10-26 10:57:14       2024-10-26   
1  alpha_stack_model_cash     0.744346   2024-10-31 05:04:00       2024-10-31   
2  alpha_stack_model_cash     0.601607   2024-10-29 18:18:47       2024-10-29   
3  alpha_stack_model_cash     0.937665   2024-10-20 08:23:34       2024-10-31   
4  alpha_stack_model_cash     0.690870   2024-10-05 06:31:22       2024-10-05   

  Application_month Data_selection  deffpd0  flg_mature_fpd0 new_loan_type  \
0           2024-10          Train        1                1         Quick   
1           2024-10          Train        0                1         Quick   
2           2024-10          Train        1                1         Quick   
3           2024-10          Train        1                1         Quick   
4           2024-10          Train        0                1         Quick   

  modelVersionId trenchCategory loan_product_type  
0             v1       Trench 1    not applicable  
1             v1       Trench 2    not applicable  
2             v1       Trench 2    not applicable  
3             v1       Trench 2    not applicable  
4             v1       Trench 1    not applicable

In [329]:
df2 = dfd.copy()

### Concat

In [330]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (40459, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3705340  026a6ada-efc6-4e5e-968a-0d37e382d9ad    60837053400012   
1    3705891  ec2bf9f2-ee68-44de-9f2e-9690f53ec824    60837058910018   
2    3071399  fc78cc72-651b-4e92-b0df-a906c23fc167    60830713990042   
3    3301484  96d1d523-5824-4b1c-abb7-5c6b43f74c75    60833014840017   
4    3706096  98118b0f-5bae-4544-8a77-f77404a58b50    60837060960013   

         modelDisplayName          aStackScore appln_submit_datetime  \
0  alpha_stack_model_cash  0.37316971605586724   2025-09-26 14:04:27   
1  alpha_stack_model_cash   0.3802428197781405   2025-09-26 14:01:57   
2  alpha_stack_model_cash  0.43455965241990185   2025-09-26 12:34:08   
3  alpha_stack_model_cash  0.30585731391943394   2025-09-26 19:26:32   
4  alpha_stack_model_cash   0.4543684030611348   2025-09-26 17:13:14   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-09-26           2025-09           Test        0                1   
1       2025-10-02           2025-09           Test        1                1   
2       2025-09-26           2025-09           Test        1                1   
3       2025-09-30           2025-09           Test        0                1   
4       2025-09-27           2025-09           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 2    not applicable  
4         Quick             v1       Trench 1    not applicable

In [331]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'aStackScore', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [332]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        3968
Train           Quick          v1              not applicable       36491
Name: digitalLoanAccountId, dtype: int64

In [333]:
df_concat['new_loan_type'].unique()

array(['Quick'], dtype=object)

In [334]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aStackScore', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [335]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (2336, 15)
The shape of the dimension table is:	 (32, 10)


In [336]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=27ba0bf6-f653-4c45-82f6-78d259a96b4a>

In [337]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=b42ff052-966f-4cad-b64a-54b2673bddee>

### FPD10

### Test

In [338]:
sq = r""" 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (3968, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2807107  67527945-fff7-4bb3-add4-a5a452bf9121    60828071070038   
1    3701246  9c698895-ba1e-4a18-a058-c4cae1311e82    60837012460019   
2    2473116  70dedacb-577f-433e-bfbf-4d57973ff5ea    60824731160018   
3    3721496  60214522-18c8-4ed1-b085-03ec2496c643    60837214960015   
4    3479077  628bb8f9-78bd-4a36-bd17-80d4f85852d9    60834790770019   

         modelDisplayName          aStackScore appln_submit_datetime  \
0  alpha_stack_model_cash   0.3309888071459822   2025-10-03 14:02:40   
1  alpha_stack_model_cash  0.05593874817037861   2025-10-03 20:32:40   
2  alpha_stack_model_cash   0.4871555473798478   2025-10-03 20:45:57   
3  alpha_stack_model_cash  0.36385755873462694   2025-10-03 21:36:23   
4  alpha_stack_model_cash   0.4693781318585817   2025-10-03 19:44:09   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-03           2025-10           Test         1   
1       2025-10-03           2025-10           Test         0   
2       2025-10-03           2025-10           Test         0   
3       2025-10-03           2025-10           Test         0   
4       2025-10-03           2025-10           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 3   
1                1         Quick             v1       Trench 1   
2                1         Quick             v1       Trench 2   
3                1         Quick             v1       Trench 1   
4                1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [339]:
df1 = dfd.copy()

### Train

In [340]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  trenchCategory
  from parsed p
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (36489, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2973866  f425349e-48cc-4387-9615-ceaff934da49    60829738660019   
1     2744532  0c107735-997e-4dbf-929a-32015b074b09    60827445320017   
2     2891262  7df48882-dcea-45e0-9de3-c961ed46fa98    60828912620013   
3     2447392  de0afa7a-0df4-41b8-98be-6a9958f7ef68    60824473920025   
4     2955601  cb3dc207-23a9-4524-9e6f-0dc927ab39a8    60829556010014   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.684020   2024-10-26 13:28:52       2024-10-28   
1  alpha_stack_model_cash     0.780193   2024-10-05 09:33:32       2024-10-05   
2  alpha_stack_model_cash     0.847976   2024-10-03 11:05:39       2024-10-03   
3  alpha_stack_model_cash     0.475227   2024-10-02 14:16:59       2024-10-02   
4  alpha_stack_model_cash     0.548666   2024-10-20 13:45:26       2024-10-20   

  Application_month Data_selection  deffpd10  flg_mature_fpd10 new_loan_type  \
0           2024-10          Train         1                 1         Quick   
1           2024-10          Train         0                 1         Quick   
2           2024-10          Train         0                 1         Quick   
3           2024-10          Train         1                 1         Quick   
4           2024-10          Train         0                 1         Quick   

  modelVersionId trenchCategory loan_product_type  
0             v1       Trench 1    not applicable  
1             v1       Trench 2    not applicable  
2             v1       Trench 1    not applicable  
3             v1       Trench 3    not applicable  
4             v1       Trench 1    not applicable

In [341]:
df2 = dfd.copy()

### Concat

In [342]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (40457, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2807107  67527945-fff7-4bb3-add4-a5a452bf9121    60828071070038   
1    3701246  9c698895-ba1e-4a18-a058-c4cae1311e82    60837012460019   
2    2473116  70dedacb-577f-433e-bfbf-4d57973ff5ea    60824731160018   
3    3721496  60214522-18c8-4ed1-b085-03ec2496c643    60837214960015   
4    3479077  628bb8f9-78bd-4a36-bd17-80d4f85852d9    60834790770019   

         modelDisplayName          aStackScore appln_submit_datetime  \
0  alpha_stack_model_cash   0.3309888071459822   2025-10-03 14:02:40   
1  alpha_stack_model_cash  0.05593874817037861   2025-10-03 20:32:40   
2  alpha_stack_model_cash   0.4871555473798478   2025-10-03 20:45:57   
3  alpha_stack_model_cash  0.36385755873462694   2025-10-03 21:36:23   
4  alpha_stack_model_cash   0.4693781318585817   2025-10-03 19:44:09   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-03           2025-10           Test         1   
1       2025-10-03           2025-10           Test         0   
2       2025-10-03           2025-10           Test         0   
3       2025-10-03           2025-10           Test         0   
4       2025-10-03           2025-10           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 3   
1                1         Quick             v1       Trench 1   
2                1         Quick             v1       Trench 2   
3                1         Quick             v1       Trench 1   
4                1         Quick             v1       Trench 2   

  loan_product_type  flg_mature_fpd10  
0    not applicable              <NA>  
1    not applicable              <NA>  
2    not applicable              <NA>  
3    not applicable              <NA>  
4    not applicable              <NA>

In [343]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        3968
Train           Quick          v1              not applicable       36489
Name: digitalLoanAccountId, dtype: int64

In [344]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aStackScore', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [345]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_cash', product='CASH')

In [346]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=843c7c02-0ff0-4267-a2c1-6e23b4fa04cc>

In [347]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=4ea71623-399e-496b-b5f7-71cf2f020a18>

### FPD30

### Test

In [348]:
sq = r""" 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (89, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3056951  ef88f86a-58f8-44a7-8989-6f3fefc444f1    60830569510044   
1    3732908  c06b6d3a-5c1c-4159-b032-eb5734e961e7    60837329080013   
2    3732985  a51a6129-a36f-43b2-9b56-f5897824a443    60837329850016   
3    3733014  fe0e6523-44f8-4c52-8e5c-cc1596f581c7    60837330140018   
4    3733252  034a1064-7f3b-4087-8337-fe0f2eb91e6f    60837332520011   

         modelDisplayName          aStackScore appln_submit_datetime  \
0  alpha_stack_model_cash  0.23552026234338302   2025-10-09 11:43:56   
1  alpha_stack_model_cash  0.33412102596292587   2025-10-09 11:13:44   
2  alpha_stack_model_cash    0.400134108741866   2025-10-09 11:56:58   
3  alpha_stack_model_cash  0.38226740666971737   2025-10-09 12:15:10   
4  alpha_stack_model_cash   0.3378641043975119   2025-10-09 13:52:08   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-09           2025-10           Test         0   
1       2025-10-09           2025-10           Test         0   
2       2025-10-09           2025-10           Test         0   
3       2025-10-09           2025-10           Test         0   
4       2025-10-09           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 3   
1                 1         Quick             v1       Trench 1   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [349]:
df1 = dfd.copy()

### Train

In [350]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  trenchCategory
  from parsed p
  ) ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (36463, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2919121  722f9195-c12a-429a-a625-bce0afbbc990    60829191210019   
1     2947718  550a1fdc-6901-4e0e-a2ad-3daebe31d669    60829477180019   
2     2838216  25a7baac-4b95-43e1-b8bf-2501744acc09    60828382160015   
3     2947267  41e3c4e5-7f03-4ccc-b57c-af6cf3f55fff    60829472670013   
4     2908949  0ee3e791-3903-4155-9cca-3a542683203a    60829089490016   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.423985   2024-10-07 15:38:56       2024-10-07   
1  alpha_stack_model_cash     0.109487   2024-10-17 10:54:25       2024-10-17   
2  alpha_stack_model_cash     0.319246   2024-10-17 09:24:02       2024-10-17   
3  alpha_stack_model_cash     0.612112   2024-10-30 19:19:09       2024-10-31   
4  alpha_stack_model_cash     0.492286   2024-10-05 16:41:39       2024-10-05   

  Application_month Data_selection  deffpd30  flg_mature_fpd30 new_loan_type  \
0           2024-10          Train         0                 1         Quick   
1           2024-10          Train         0                 1         Quick   
2           2024-10          Train         0                 1         Quick   
3           2024-10          Train         1                 1         Quick   
4           2024-10          Train         0                 1         Quick   

  modelVersionId trenchCategory loan_product_type  
0             v1       Trench 1    not applicable  
1             v1       Trench 1    not applicable  
2             v1       Trench 2    not applicable  
3             v1       Trench 1    not applicable  
4             v1       Trench 1    not applicable

In [351]:
df2 = dfd.copy()

### Concat

In [352]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (36552, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3056951  ef88f86a-58f8-44a7-8989-6f3fefc444f1    60830569510044   
1    3732908  c06b6d3a-5c1c-4159-b032-eb5734e961e7    60837329080013   
2    3732985  a51a6129-a36f-43b2-9b56-f5897824a443    60837329850016   
3    3733014  fe0e6523-44f8-4c52-8e5c-cc1596f581c7    60837330140018   
4    3733252  034a1064-7f3b-4087-8337-fe0f2eb91e6f    60837332520011   

         modelDisplayName          aStackScore appln_submit_datetime  \
0  alpha_stack_model_cash  0.23552026234338302   2025-10-09 11:43:56   
1  alpha_stack_model_cash  0.33412102596292587   2025-10-09 11:13:44   
2  alpha_stack_model_cash    0.400134108741866   2025-10-09 11:56:58   
3  alpha_stack_model_cash  0.38226740666971737   2025-10-09 12:15:10   
4  alpha_stack_model_cash   0.3378641043975119   2025-10-09 13:52:08   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-09           2025-10           Test         0   
1       2025-10-09           2025-10           Test         0   
2       2025-10-09           2025-10           Test         0   
3       2025-10-09           2025-10           Test         0   
4       2025-10-09           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 3   
1                 1         Quick             v1       Trench 1   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [353]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable          89
Train           Quick          v1              not applicable       36463
Name: digitalLoanAccountId, dtype: int64

In [354]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aStackScore', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [355]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_cash', product='CASH')

In [356]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=cdf19748-7992-4962-874f-1973fdcd4bde>

In [357]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=d7665379-f2b4-47e2-881a-2ec56b97a244>

### FSPD30

### Test

In [358]:
sq = r""" 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, aStackScore, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffspd30, flg_mature_fspd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [359]:
df1 = dfd.copy()

### Train

In [360]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  trenchCategory
  from parsed p
  ) 
  , 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (34104, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2979960  602c4809-9ba3-478a-99d8-d64d20774eff    60829799600011   
1     2981329  11631e4b-2500-4e7d-adce-5337c7ae4d33    60829813290016   
2     1908689  a5ca9745-02d1-4576-a135-00ec194a6a10    60819086890042   
3     2912409  adbced36-acde-41d6-8b1d-2161bfb146c4    60829124090014   
4     1025654  8e25f1c7-b28f-41cf-893b-5f6a7608cabc    60810256540053   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.539407   2024-10-29 09:04:18       2024-10-29   
1  alpha_stack_model_cash     0.708528   2024-10-30 06:17:40       2024-10-30   
2  alpha_stack_model_cash     0.507631   2024-10-12 18:38:26       2024-10-12   
3  alpha_stack_model_cash     0.657837   2024-10-23 17:37:37       2024-10-23   
4  alpha_stack_model_cash     0.195087   2024-10-06 01:14:17       2024-10-06   

  Application_month Data_selection  deffspd30  flg_mature_fspd_30  \
0           2024-10          Train          1                   1   
1           2024-10          Train          0                   1   
2           2024-10          Train          1                   1   
3           2024-10          Train          0                   1   
4           2024-10          Train          0                   1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 1    not applicable  
4         Quick             v1       Trench 2    not applicable

In [361]:
df2 = dfd.copy()

### Concat

In [362]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (34104, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2979960  602c4809-9ba3-478a-99d8-d64d20774eff    60829799600011   
1     2981329  11631e4b-2500-4e7d-adce-5337c7ae4d33    60829813290016   
2     1908689  a5ca9745-02d1-4576-a135-00ec194a6a10    60819086890042   
3     2912409  adbced36-acde-41d6-8b1d-2161bfb146c4    60829124090014   
4     1025654  8e25f1c7-b28f-41cf-893b-5f6a7608cabc    60810256540053   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.539407   2024-10-29 09:04:18       2024-10-29   
1  alpha_stack_model_cash     0.708528   2024-10-30 06:17:40       2024-10-30   
2  alpha_stack_model_cash     0.507631   2024-10-12 18:38:26       2024-10-12   
3  alpha_stack_model_cash     0.657837   2024-10-23 17:37:37       2024-10-23   
4  alpha_stack_model_cash     0.195087   2024-10-06 01:14:17       2024-10-06   

  Application_month Data_selection  deffspd30  flg_mature_fspd_30  \
0           2024-10          Train          1                   1   
1           2024-10          Train          0                   1   
2           2024-10          Train          1                   1   
3           2024-10          Train          0                   1   
4           2024-10          Train          0                   1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 1    not applicable  
4         Quick             v1       Trench 2    not applicable

In [363]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       34104
Name: digitalLoanAccountId, dtype: int64

In [364]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aStackScore', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [365]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_cash', product='CASH')

In [366]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=268cd181-aaf2-40dc-bcd9-030a92843e93>

In [367]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=fb891aae-c8f7-42cb-b028-9e19e4a319dc>

### FSTPD30

### Test

In [368]:
sq = r""" 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,requestPayload as requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Alpha-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  p.start_time,
  p.prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce (p.trenchCategory, REGEXP_EXTRACT(m.requestPayload_clean, r"trenchCategory[:=]['\"]?([^'\"]+)['\"]?")) trenchCategory
  from parsed p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, aStackScore, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffstpd30, flg_mature_fstpd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [369]:
df1 = dfd.copy()

### Train

In [370]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Alpha-Cash-Stack-Model', 'alpha_stack_model_cash')
and modelVersionId = 'v1'
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction aStackScore,
  case when p.modelDisplayName like 'Alpha%' then 'alpha_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  trenchCategory
  from parsed p
  ) , 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.aStackScore,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.aStackScore is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (31012, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1484156  02b27ef7-1cd6-4e92-8c90-4490b266b84a    60814841560084   
1     2945302  45c12a07-25b7-478b-8d8e-3785aaa4956e    60829453020011   
2     2232785  fe5c54c6-b0c1-4ac7-ad50-7011ade449e4    60822327850013   
3     2611711  19362360-a87c-481a-bf1e-8ab027cee215    60826117110023   
4     2987156  ee3610c7-faa0-4418-8223-d939bc33756f    60829871560017   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.550317   2024-10-06 10:00:27       2024-10-06   
1  alpha_stack_model_cash     0.903650   2024-10-16 14:08:30       2024-10-16   
2  alpha_stack_model_cash     0.387415   2024-10-26 22:56:54       2024-10-27   
3  alpha_stack_model_cash     0.661221   2024-10-09 10:50:57       2024-10-09   
4  alpha_stack_model_cash     0.569556   2024-10-31 13:14:54       2024-10-31   

  Application_month Data_selection  deffstpd30  flg_mature_fstpd_30  \
0           2024-10          Train           1                    1   
1           2024-10          Train           1                    1   
2           2024-10          Train           0                    1   
3           2024-10          Train           1                    1   
4           2024-10          Train           1                    1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 2    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 2    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [371]:
df2 = dfd.copy()

### Concat

In [372]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (31012, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1484156  02b27ef7-1cd6-4e92-8c90-4490b266b84a    60814841560084   
1     2945302  45c12a07-25b7-478b-8d8e-3785aaa4956e    60829453020011   
2     2232785  fe5c54c6-b0c1-4ac7-ad50-7011ade449e4    60822327850013   
3     2611711  19362360-a87c-481a-bf1e-8ab027cee215    60826117110023   
4     2987156  ee3610c7-faa0-4418-8223-d939bc33756f    60829871560017   

         modelDisplayName  aStackScore appln_submit_datetime disbursementdate  \
0  alpha_stack_model_cash     0.550317   2024-10-06 10:00:27       2024-10-06   
1  alpha_stack_model_cash     0.903650   2024-10-16 14:08:30       2024-10-16   
2  alpha_stack_model_cash     0.387415   2024-10-26 22:56:54       2024-10-27   
3  alpha_stack_model_cash     0.661221   2024-10-09 10:50:57       2024-10-09   
4  alpha_stack_model_cash     0.569556   2024-10-31 13:14:54       2024-10-31   

  Application_month Data_selection  deffstpd30  flg_mature_fstpd_30  \
0           2024-10          Train           1                    1   
1           2024-10          Train           1                    1   
2           2024-10          Train           0                    1   
3           2024-10          Train           1                    1   
4           2024-10          Train           1                    1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 2    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 2    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [373]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       31012
Name: digitalLoanAccountId, dtype: int64

In [374]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'aStackScore', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [375]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='alpha_stack_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (1848, 15)
The shape of the dimension table is:	 (32, 10)


In [376]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8d803f63-53f0-4527-b4a1-0f0387a3c456>

In [377]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=7b9af58b-84a6-46cd-9f8d-3d50e67d9ed5>

# Beta-Cash-Demo-Model

### FPD0

### Test

In [378]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when p.modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p 
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (4147, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
1    3716782  1616f4ec-1811-4744-8ec4-9ec17cf862bb    60837167820013   
2    3727723  c647341b-ea28-4be3-85e7-97e48b462499    60837277230011   
3    3721729  4a79f936-068e-4436-8c0c-c78982598fa4    60837217290013   
4    3796589  de913354-b762-41dc-ad5d-7a265f272069    60837965890014   

       modelDisplayName Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash   0.3754082371818635   2025-09-28 18:26:57   
1  beta_demo_model_cash  0.37695104300773075   2025-10-01 14:33:37   
2  beta_demo_model_cash  0.48534037812761277   2025-10-06 17:02:24   
3  beta_demo_model_cash   0.4915565700163809   2025-10-04 08:37:07   
4  beta_demo_model_cash  0.39076094822867696   2025-11-07 11:55:46   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-09-28           2025-09           Test        0                1   
1       2025-10-06           2025-10           Test        0                1   
2       2025-10-06           2025-10           Test        0                1   
3       2025-10-04           2025-10           Test        0                1   
4       2025-11-07           2025-11           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 3    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 1    not applicable  
4         Quick             v1       Trench 1    not applicable

In [379]:
df1 = dfd.copy()

### Train

In [380]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  case when modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ) 
  ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (38711, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2973109  c8e9412b-8f02-4c18-bf67-260481887ca2    60829731090019   
1     2907528  3e9ad64f-fa23-4418-9f4c-414738eca555    60829075280015   
2     2858650  51043bbc-7303-4a5d-9c8c-7c592c48ac80    60828586500019   
3     2537031  3e288216-a1de-4a3d-80e2-65a405c94672    60825370310016   
4     2517106  ddc34bee-489c-412d-b6fe-1d40658f6d03    60825171060026   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.429170   2024-10-26 09:41:38   
1  beta_demo_model_cash              0.717620   2024-10-03 19:04:26   
2  beta_demo_model_cash              0.444915   2024-10-22 11:38:03   
3  beta_demo_model_cash              0.451184   2024-10-11 20:32:24   
4  beta_demo_model_cash              0.441410   2024-10-29 18:20:31   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2024-10-27           2024-10          Train        0                1   
1       2024-10-03           2024-10          Train        1                1   
2       2024-10-22           2024-10          Train        1                1   
3       2024-10-11           2024-10          Train        1                1   
4       2024-10-30           2024-10          Train        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 2    not applicable  
3         Quick             v1       Trench 2    not applicable  
4         Quick             v1       Trench 3    not applicable

In [381]:
df2 = dfd.copy()

### Concat

In [382]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (42858, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
1    3716782  1616f4ec-1811-4744-8ec4-9ec17cf862bb    60837167820013   
2    3727723  c647341b-ea28-4be3-85e7-97e48b462499    60837277230011   
3    3721729  4a79f936-068e-4436-8c0c-c78982598fa4    60837217290013   
4    3796589  de913354-b762-41dc-ad5d-7a265f272069    60837965890014   

       modelDisplayName Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash   0.3754082371818635   2025-09-28 18:26:57   
1  beta_demo_model_cash  0.37695104300773075   2025-10-01 14:33:37   
2  beta_demo_model_cash  0.48534037812761277   2025-10-06 17:02:24   
3  beta_demo_model_cash   0.4915565700163809   2025-10-04 08:37:07   
4  beta_demo_model_cash  0.39076094822867696   2025-11-07 11:55:46   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-09-28           2025-09           Test        0                1   
1       2025-10-06           2025-10           Test        0                1   
2       2025-10-06           2025-10           Test        0                1   
3       2025-10-04           2025-10           Test        0                1   
4       2025-11-07           2025-11           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 3    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 1    not applicable  
4         Quick             v1       Trench 1    not applicable

In [383]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'Beta_Cash_Demo_Score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [384]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        4147
Train           Quick          v1              not applicable       38711
Name: digitalLoanAccountId, dtype: int64

In [385]:
df_concat['new_loan_type'].unique()

array(['Quick'], dtype=object)

In [386]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_Cash_Demo_Score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [387]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (2344, 15)
The shape of the dimension table is:	 (32, 10)


In [388]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=ae31d9f3-77fe-4e53-ac8d-3f112cc3085d>

In [389]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=6ad3d33a-a40c-40db-86d3-0ed00ce4b564>

### FPD10

### Test

In [390]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when p.modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p 
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (4147, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
1    3719554  2d648aa0-e65e-4b23-9547-a1c3fcb1f740    60837195540015   
2    3427045  399798f3-47e7-4cf6-8c2b-11b4a0afba4e    60834270450018   
3    3265528  615609a7-eff2-4f61-9277-11baf7e5eda2    60832655280021   
4    3728222  6fb8902e-fe57-42d2-9994-25a40b69ac75    60837282220019   

       modelDisplayName Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash   0.3754082371818635   2025-09-28 18:26:57   
1  beta_demo_model_cash   0.4711101792602317   2025-10-02 20:04:28   
2  beta_demo_model_cash   0.4381901270235617   2025-09-27 14:40:49   
3  beta_demo_model_cash   0.4901048795818221   2025-10-19 16:14:46   
4  beta_demo_model_cash   0.4667790730545179   2025-10-07 04:55:21   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-09-28           2025-09           Test         0   
1       2025-10-02           2025-10           Test         0   
2       2025-10-03           2025-09           Test         0   
3       2025-11-13           2025-10           Test         0   
4       2025-10-07           2025-10           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 3   
1                1         Quick             v1       Trench 1   
2                1         Quick             v1       Trench 2   
3                1         Quick             v1       Trench 2   
4                1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [391]:
df1 = dfd.copy()

### Train

In [392]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  case when modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  )
  ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (38709, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1871036  a2d4eb8c-3152-40ad-b9a2-9a4c53373ad8    60818710360018   
1     2954041  eb573281-b263-4d5d-9c01-b6aa280f6b48    60829540410011   
2     2977116  600cdda9-e266-4694-ab0a-2ca7e8a4333d    60829771160014   
3     2940887  d3d311af-1a04-434f-a0a3-0ec141810ca3    60829408870017   
4     2981753  29882edc-d0f0-433f-a4a0-201b10d60e90    60829817530018   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.457542   2024-10-06 10:05:56   
1  beta_demo_model_cash              0.507218   2024-10-19 12:07:01   
2  beta_demo_model_cash              0.598890   2024-10-27 22:27:53   
3  beta_demo_model_cash              0.559716   2024-10-15 11:44:53   
4  beta_demo_model_cash              0.486578   2024-10-30 10:39:25   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2024-10-06           2024-10          Train         1   
1       2024-10-19           2024-10          Train         0   
2       2024-10-31           2024-10          Train         1   
3       2024-10-15           2024-10          Train         1   
4       2024-10-30           2024-10          Train         0   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 1   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [393]:
df2 = dfd.copy()

### Concat

In [394]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (42856, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
1    3719554  2d648aa0-e65e-4b23-9547-a1c3fcb1f740    60837195540015   
2    3427045  399798f3-47e7-4cf6-8c2b-11b4a0afba4e    60834270450018   
3    3265528  615609a7-eff2-4f61-9277-11baf7e5eda2    60832655280021   
4    3728222  6fb8902e-fe57-42d2-9994-25a40b69ac75    60837282220019   

       modelDisplayName Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash   0.3754082371818635   2025-09-28 18:26:57   
1  beta_demo_model_cash   0.4711101792602317   2025-10-02 20:04:28   
2  beta_demo_model_cash   0.4381901270235617   2025-09-27 14:40:49   
3  beta_demo_model_cash   0.4901048795818221   2025-10-19 16:14:46   
4  beta_demo_model_cash   0.4667790730545179   2025-10-07 04:55:21   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-09-28           2025-09           Test         0   
1       2025-10-02           2025-10           Test         0   
2       2025-10-03           2025-09           Test         0   
3       2025-11-13           2025-10           Test         0   
4       2025-10-07           2025-10           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 3   
1                1         Quick             v1       Trench 1   
2                1         Quick             v1       Trench 2   
3                1         Quick             v1       Trench 2   
4                1         Quick             v1       Trench 1   

  loan_product_type  flg_mature_fpd10  
0    not applicable              <NA>  
1    not applicable              <NA>  
2    not applicable              <NA>  
3    not applicable              <NA>  
4    not applicable              <NA>

In [395]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        4147
Train           Quick          v1              not applicable       38709
Name: digitalLoanAccountId, dtype: int64

In [396]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_Cash_Demo_Score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [397]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_cash', product='CASH')

In [398]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=0ed0c95e-b536-4bb7-bc98-0d6ed92e5af4>

In [399]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=765f4017-f783-41d6-8405-948790291561>

### FPD30

### Test

In [400]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when p.modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p 
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (111, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3719077  70b0e190-3125-4e0a-acab-ce37fa7ea02a    60837190770017   
1    1081564  eb47dde4-59bc-49fc-a2f0-d384fa91bcf0    60810815640056   
2    3724716  ebfbd098-aa48-4161-a112-cf2e0b25ba9a    60837247160011   
3    3357515  58f0e9c2-1805-4158-a3d6-c8f5759aa2af    60833575150024   
4    1080796  27ed2366-6b6c-4c53-b984-ef57da6466bd    60810807960064   

       modelDisplayName Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash  0.45830241485823703   2025-10-02 16:31:08   
1  beta_demo_model_cash   0.5996452294106355   2025-10-08 22:13:17   
2  beta_demo_model_cash  0.45622004160933866   2025-10-05 13:12:34   
3  beta_demo_model_cash  0.41511694419907225   2025-10-02 16:13:23   
4  beta_demo_model_cash  0.31458623119673257   2025-10-02 01:05:15   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-02           2025-10           Test         0   
1       2025-10-09           2025-10           Test         0   
2       2025-10-05           2025-10           Test         0   
3       2025-10-02           2025-10           Test         0   
4       2025-10-02           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 1   
1                 1         Quick             v1       Trench 2   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 3   
4                 1         Quick             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [401]:
df1 = dfd.copy()

### Train

In [402]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  case when modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ) ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (38682, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2923349  c70a3e97-1d9e-4bbf-ac30-a382819e7a4c    60829233490018   
1     1919009  be9dc240-56a4-493d-8931-8a43d7002f28    60819190090013   
2     2510905  65e65043-185b-4f15-9a74-b2616e066d43    60825109050013   
3     2975488  8f144425-048a-4016-a895-232263e6d5b2    60829754880011   
4     2562259  e879cb89-58cc-4e80-8138-239328086e13    60825622590019   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.525168   2024-10-09 22:29:29   
1  beta_demo_model_cash              0.563746   2024-10-24 23:19:52   
2  beta_demo_model_cash              0.524240   2024-10-22 17:19:02   
3  beta_demo_model_cash              0.563819   2024-10-26 23:21:03   
4  beta_demo_model_cash              0.624271   2024-10-15 05:24:08   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2024-10-14           2024-10          Train         0   
1       2024-10-25           2024-10          Train         1   
2       2024-10-22           2024-10          Train         1   
3       2024-10-27           2024-10          Train         0   
4       2024-10-16           2024-10          Train         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 1   
1                 1         Quick             v1       Trench 2   
2                 1         Quick             v1       Trench 2   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [403]:
df2 = dfd.copy()

### Concat

In [404]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (38793, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3719077  70b0e190-3125-4e0a-acab-ce37fa7ea02a    60837190770017   
1    1081564  eb47dde4-59bc-49fc-a2f0-d384fa91bcf0    60810815640056   
2    3724716  ebfbd098-aa48-4161-a112-cf2e0b25ba9a    60837247160011   
3    3357515  58f0e9c2-1805-4158-a3d6-c8f5759aa2af    60833575150024   
4    1080796  27ed2366-6b6c-4c53-b984-ef57da6466bd    60810807960064   

       modelDisplayName Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash  0.45830241485823703   2025-10-02 16:31:08   
1  beta_demo_model_cash   0.5996452294106355   2025-10-08 22:13:17   
2  beta_demo_model_cash  0.45622004160933866   2025-10-05 13:12:34   
3  beta_demo_model_cash  0.41511694419907225   2025-10-02 16:13:23   
4  beta_demo_model_cash  0.31458623119673257   2025-10-02 01:05:15   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-02           2025-10           Test         0   
1       2025-10-09           2025-10           Test         0   
2       2025-10-05           2025-10           Test         0   
3       2025-10-02           2025-10           Test         0   
4       2025-10-02           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 1   
1                 1         Quick             v1       Trench 2   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 3   
4                 1         Quick             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [405]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable         111
Train           Quick          v1              not applicable       38682
Name: digitalLoanAccountId, dtype: int64

In [406]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_Cash_Demo_Score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [407]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_cash', product='CASH')

In [408]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=74f49dcc-9b4d-4bac-91cc-49f3f0fde7d6>

In [409]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=b5b4d19c-76ec-4361-86b5-17b9d942e715>

### FSPD30

### Test

In [410]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when p.modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p 
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, Beta_Cash_Demo_Score, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffspd30, flg_mature_fspd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [411]:
df1 = dfd.copy()

### Train

In [412]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  case when modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  )
  , 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (36234, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2973387  a016ed33-2086-45d9-9a35-2739303f394f    60829733870019   
1     2231422  182cd65b-ff3e-4514-bc6c-aef821bc193b    60822314220023   
2     2660652  e9b8d38c-0242-4770-b6c2-976b66d5727b    60826606520012   
3     2410773  e4e0848b-73ac-4b86-bd2d-6f18f6b0affa    60824107730013   
4     2315941  4e6a9ac2-ed71-4122-90de-1d02c878d017    60823159410015   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.612042   2024-10-26 10:57:14   
1  beta_demo_model_cash              0.593849   2024-10-31 05:04:00   
2  beta_demo_model_cash              0.645592   2024-10-29 18:18:47   
3  beta_demo_model_cash              0.589815   2024-10-04 21:17:48   
4  beta_demo_model_cash              0.437452   2024-10-20 08:23:34   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2024-10-26           2024-10          Train          1   
1       2024-10-31           2024-10          Train          1   
2       2024-10-29           2024-10          Train          0   
3       2024-10-05           2024-10          Train          0   
4       2024-10-31           2024-10          Train          1   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1         Quick             v1       Trench 1   
1                   1         Quick             v1       Trench 2   
2                   1         Quick             v1       Trench 2   
3                   1         Quick             v1       Trench 2   
4                   1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [413]:
df2 = dfd.copy()

### Concat

In [414]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (36234, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2973387  a016ed33-2086-45d9-9a35-2739303f394f    60829733870019   
1     2231422  182cd65b-ff3e-4514-bc6c-aef821bc193b    60822314220023   
2     2660652  e9b8d38c-0242-4770-b6c2-976b66d5727b    60826606520012   
3     2410773  e4e0848b-73ac-4b86-bd2d-6f18f6b0affa    60824107730013   
4     2315941  4e6a9ac2-ed71-4122-90de-1d02c878d017    60823159410015   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.612042   2024-10-26 10:57:14   
1  beta_demo_model_cash              0.593849   2024-10-31 05:04:00   
2  beta_demo_model_cash              0.645592   2024-10-29 18:18:47   
3  beta_demo_model_cash              0.589815   2024-10-04 21:17:48   
4  beta_demo_model_cash              0.437452   2024-10-20 08:23:34   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2024-10-26           2024-10          Train          1   
1       2024-10-31           2024-10          Train          1   
2       2024-10-29           2024-10          Train          0   
3       2024-10-05           2024-10          Train          0   
4       2024-10-31           2024-10          Train          1   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1         Quick             v1       Trench 1   
1                   1         Quick             v1       Trench 2   
2                   1         Quick             v1       Trench 2   
3                   1         Quick             v1       Trench 2   
4                   1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [415]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       36234
Name: digitalLoanAccountId, dtype: int64

In [416]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_Cash_Demo_Score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [417]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_cash', product='CASH')

In [418]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=a25f0805-5013-4545-98be-baf0e15e974f>

In [419]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=212fc8a3-efe4-4927-ab94-e9ff6897196e>

### FSTPD30

### Test

In [420]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),
model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when p.modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p 
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, Beta_Cash_Demo_Score, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffstpd30, flg_mature_fstpd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [421]:
df1 = dfd.copy()

### Train

In [422]:
sq = """ 
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in ('Beta-Cash-Demo-Model', 'beta_demo_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_Cash_Demo_Score,
  case when modelDisplayName like 'Beta-Cash-Demo-Model' then 'beta_demo_model_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_Cash_Demo_Score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_Cash_Demo_Score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (33057, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2923349  c70a3e97-1d9e-4bbf-ac30-a382819e7a4c    60829233490018   
1     1919009  be9dc240-56a4-493d-8931-8a43d7002f28    60819190090013   
2     2510905  65e65043-185b-4f15-9a74-b2616e066d43    60825109050013   
3     2975488  8f144425-048a-4016-a895-232263e6d5b2    60829754880011   
4     2562259  e879cb89-58cc-4e80-8138-239328086e13    60825622590019   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.525168   2024-10-09 22:29:29   
1  beta_demo_model_cash              0.563746   2024-10-24 23:19:52   
2  beta_demo_model_cash              0.524240   2024-10-22 17:19:02   
3  beta_demo_model_cash              0.563819   2024-10-26 23:21:03   
4  beta_demo_model_cash              0.624271   2024-10-15 05:24:08   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2024-10-14           2024-10          Train           1   
1       2024-10-25           2024-10          Train           1   
2       2024-10-22           2024-10          Train           1   
3       2024-10-27           2024-10          Train           0   
4       2024-10-16           2024-10          Train           1   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1         Quick             v1       Trench 1   
1                    1         Quick             v1       Trench 2   
2                    1         Quick             v1       Trench 2   
3                    1         Quick             v1       Trench 1   
4                    1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [423]:
df2 = dfd.copy()

### Concat

In [424]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (33057, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2923349  c70a3e97-1d9e-4bbf-ac30-a382819e7a4c    60829233490018   
1     1919009  be9dc240-56a4-493d-8931-8a43d7002f28    60819190090013   
2     2510905  65e65043-185b-4f15-9a74-b2616e066d43    60825109050013   
3     2975488  8f144425-048a-4016-a895-232263e6d5b2    60829754880011   
4     2562259  e879cb89-58cc-4e80-8138-239328086e13    60825622590019   

       modelDisplayName  Beta_Cash_Demo_Score appln_submit_datetime  \
0  beta_demo_model_cash              0.525168   2024-10-09 22:29:29   
1  beta_demo_model_cash              0.563746   2024-10-24 23:19:52   
2  beta_demo_model_cash              0.524240   2024-10-22 17:19:02   
3  beta_demo_model_cash              0.563819   2024-10-26 23:21:03   
4  beta_demo_model_cash              0.624271   2024-10-15 05:24:08   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2024-10-14           2024-10          Train           1   
1       2024-10-25           2024-10          Train           1   
2       2024-10-22           2024-10          Train           1   
3       2024-10-27           2024-10          Train           0   
4       2024-10-16           2024-10          Train           1   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1         Quick             v1       Trench 1   
1                    1         Quick             v1       Trench 2   
2                    1         Quick             v1       Trench 2   
3                    1         Quick             v1       Trench 1   
4                    1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [425]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       33057
Name: digitalLoanAccountId, dtype: int64

In [426]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_Cash_Demo_Score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [427]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_demo_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (1848, 15)
The shape of the dimension table is:	 (32, 10)


In [428]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8412a330-ecab-4474-9d73-ecb74bcfe17a>

In [429]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=438c9986-01e7-4370-9db5-b63880ae2b6c>

# Beta-Cash-AppScore-Model

### FPD0

### Test

In [430]:

sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  coalesce(SAFE_CAST(JSON_VALUE(p.prediction_clean, "$.combined_score") AS Float64)) AS beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory"))  trenchCategory
  from latest_request p
  left join model_run m on p.digitalLoanAccountId = m.digitalLoanAccountId
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (2553, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3496922  15ee9c2a-8dfa-479e-aaa2-4b53c32ce63e    60834969220019   
1    3783377  2744fcba-a5f4-4c44-91a4-587cba9ce3e4    60837833770017   
2    3779282  ce39b256-dfa3-4df2-bfcd-a5d09e4d637b    60837792820011   
3    3789164  64b1e5d1-063f-452d-8235-92a4e29bb66c    60837891640011   
4    3738318  27f4006b-b993-48b5-b6b7-2581caae64b5    60837383180011   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.498198   2025-10-13 19:57:38   
1  apps_score_cash             0.462186   2025-11-01 00:18:45   
2  apps_score_cash             0.484637   2025-10-30 12:15:03   
3  apps_score_cash             0.489405   2025-11-03 18:55:22   
4  apps_score_cash             0.514194   2025-10-12 02:18:17   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-10-13           2025-10           Test        0                1   
1       2025-11-01           2025-11           Test        0                1   
2       2025-10-30           2025-10           Test        0                1   
3       2025-11-03           2025-11           Test        0                1   
4       2025-10-12           2025-10           Test        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 2    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 1    not applicable  
4         Quick             v1       Trench 1    not applicable

In [431]:
df1 = dfd.copy()

### Train

In [432]:
sq = """WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  )
  ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (60358, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1439180  899291cd-c8e3-4529-a632-56a4c69f28bc    60814391800021   
1     2093691  7a4d835a-7666-42e2-9bed-1568fc75f915    60820936910011   
2     1933279  e3808876-e212-49a9-9b6a-fcdfc261d902    60819332790027   
3     1254822  c7cbe930-8585-4d8d-a864-560c84dd97ab    60812548220021   
4     1965795  8d048602-255b-457b-8263-5a8f6bef6137    60819657950025   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.500458   2023-03-03 10:00:47   
1  apps_score_cash             0.370256   2024-01-30 10:25:21   
2  apps_score_cash             0.494249   2023-05-18 13:48:59   
3  apps_score_cash             0.470700   2023-08-30 06:52:19   
4  apps_score_cash             0.434754   2023-04-28 08:22:17   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2023-03-09           2023-03          Train        1                1   
1       2024-02-01           2024-01          Train        0                1   
2       2023-05-18           2023-05          Train        0                1   
3       2023-08-30           2023-08          Train        0                1   
4       2023-04-28           2023-04          Train        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0          Flex             v1       Trench 3    not applicable  
1          Flex             v1       Trench 2    not applicable  
2          Flex             v1       Trench 3    not applicable  
3          Flex             v1       Trench 3    not applicable  
4          Flex             v1       Trench 3    not applicable

In [433]:
df2 = dfd.copy()

### Concat

In [434]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (62911, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3496922  15ee9c2a-8dfa-479e-aaa2-4b53c32ce63e    60834969220019   
1    3783377  2744fcba-a5f4-4c44-91a4-587cba9ce3e4    60837833770017   
2    3779282  ce39b256-dfa3-4df2-bfcd-a5d09e4d637b    60837792820011   
3    3789164  64b1e5d1-063f-452d-8235-92a4e29bb66c    60837891640011   
4    3738318  27f4006b-b993-48b5-b6b7-2581caae64b5    60837383180011   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.498198   2025-10-13 19:57:38   
1  apps_score_cash             0.462186   2025-11-01 00:18:45   
2  apps_score_cash             0.484637   2025-10-30 12:15:03   
3  apps_score_cash             0.489405   2025-11-03 18:55:22   
4  apps_score_cash             0.514194   2025-10-12 02:18:17   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-10-13           2025-10           Test        0                1   
1       2025-11-01           2025-11           Test        0                1   
2       2025-10-30           2025-10           Test        0                1   
3       2025-11-03           2025-11           Test        0                1   
4       2025-10-12           2025-10           Test        1                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 2    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 1    not applicable  
4         Quick             v1       Trench 1    not applicable

In [435]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'beta_cash_app_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [436]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            Quick           v1              not applicable        2553
Train           ACL TSA         v1              not applicable        1401
                Flex            v1              not applicable         233
                Flex XL         v1              not applicable          10
                Flex-up         v1              not applicable       24282
                Quick           v1              not applicable       22107
                SIL Competitor  v1              Appliance             1220
                                                Mall                   127
                SIL Repeat      v1              Appliance             4836
                                                Mall                   342
                SIL ZERO        v1              Appliance              490
                                                Mobile                  13
                SIL-Instore     v1

In [437]:
df_concat['new_loan_type'].unique()

array(['Quick', 'Flex', 'Flex XL', 'ACL TSA', 'Flex-up', 'SIL Competitor',
       'SIL Repeat', 'SIL ZERO', 'SIL-Instore'], dtype=object)

In [438]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'beta_cash_app_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [439]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (11624, 15)
The shape of the dimension table is:	 (136, 10)


In [440]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=1a478a19-47d1-42f9-aa8d-0d4441d61353>

In [441]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=16c9a80c-4f46-4eb8-a374-372cdc21a62c>

### FPD10

### Test

In [442]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  coalesce(SAFE_CAST(JSON_VALUE(p.prediction_clean, "$.combined_score") AS Float64)) AS beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory"))  trenchCategory
  from latest_request p
  left join model_run m on p.digitalLoanAccountId = m.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (2553, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3777300  bac345f6-5c75-45da-b6d7-59caa0d2d065    60837773000017   
1    3777909  67af5c6f-ca99-47f5-886b-9ea51341211a    60837779090014   
2    3753526  e594ce53-4cc5-458c-88e7-04cc495f7661    60837535260017   
3    2642293  c81869ae-c522-4839-91a8-b8e7285e3c0f    60826422930033   
4    1900616  dffc8334-aa22-41d7-ad69-ee43b3b18d13    60819006160035   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.478367   2025-10-29 13:19:47   
1  apps_score_cash             0.380922   2025-10-29 16:59:29   
2  apps_score_cash             0.471471   2025-10-19 09:33:48   
3  apps_score_cash             0.552986   2025-09-26 15:49:49   
4  apps_score_cash             0.424054   2025-10-20 18:33:08   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-29           2025-10           Test         0   
1       2025-10-29           2025-10           Test         0   
2       2025-10-20           2025-10           Test         0   
3       2025-09-26           2025-09           Test         1   
4       2025-10-21           2025-10           Test         1   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 1   
1                1         Quick             v1       Trench 1   
2                1         Quick             v1       Trench 1   
3                1         Quick             v1       Trench 3   
4                1         Quick             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [443]:
df1 = dfd.copy()

### Train

In [444]:
sq = """WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  )
  ,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (60355, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2376280  a3d94f32-3f85-4e0c-80d4-dbf8a3657026    60823762800015   
1     1037377  0766a817-5728-4588-9588-d1eeeb5613ff    60810373770054   
2     1436171  84ce76df-185b-4860-9690-f2907aab69cd    60814361710028   
3     2041968  884e127c-4c44-433d-a5a1-f35d95b6f098    60820419680025   
4     2054740  85440a89-ee5d-412a-8b0c-ebd40801e7a3    60820547400024   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.309969   2024-01-26 12:43:17   
1  apps_score_cash             0.427596   2023-04-05 00:04:57   
2  apps_score_cash             0.434885   2023-02-18 18:09:59   
3  apps_score_cash             0.473072   2023-05-21 07:34:17   
4  apps_score_cash             0.465616   2023-07-29 18:43:23   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2024-01-30           2024-01          Train         0   
1       2023-04-06           2023-04          Train         0   
2       2023-02-20           2023-02          Train         0   
3       2023-05-21           2023-05          Train         0   
4       2023-07-29           2023-07          Train         0   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1          Flex             v1       Trench 1   
1                 1          Flex             v1       Trench 3   
2                 1          Flex             v1       Trench 3   
3                 1          Flex             v1       Trench 3   
4                 1          Flex             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [445]:
df2 = dfd.copy()

### Concat

In [446]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (62908, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3777300  bac345f6-5c75-45da-b6d7-59caa0d2d065    60837773000017   
1    3777909  67af5c6f-ca99-47f5-886b-9ea51341211a    60837779090014   
2    3753526  e594ce53-4cc5-458c-88e7-04cc495f7661    60837535260017   
3    2642293  c81869ae-c522-4839-91a8-b8e7285e3c0f    60826422930033   
4    1900616  dffc8334-aa22-41d7-ad69-ee43b3b18d13    60819006160035   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.478367   2025-10-29 13:19:47   
1  apps_score_cash             0.380922   2025-10-29 16:59:29   
2  apps_score_cash             0.471471   2025-10-19 09:33:48   
3  apps_score_cash             0.552986   2025-09-26 15:49:49   
4  apps_score_cash             0.424054   2025-10-20 18:33:08   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-29           2025-10           Test         0   
1       2025-10-29           2025-10           Test         0   
2       2025-10-20           2025-10           Test         0   
3       2025-09-26           2025-09           Test         1   
4       2025-10-21           2025-10           Test         1   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 1   
1                1         Quick             v1       Trench 1   
2                1         Quick             v1       Trench 1   
3                1         Quick             v1       Trench 3   
4                1         Quick             v1       Trench 3   

  loan_product_type  flg_mature_fpd10  
0    not applicable              <NA>  
1    not applicable              <NA>  
2    not applicable              <NA>  
3    not applicable              <NA>  
4    not applicable              <NA>

In [447]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            Quick           v1              not applicable        2553
Train           ACL TSA         v1              not applicable        1401
                Flex            v1              not applicable         233
                Flex XL         v1              not applicable          10
                Flex-up         v1              not applicable       24280
                Quick           v1              not applicable       22106
                SIL Competitor  v1              Appliance             1220
                                                Mall                   127
                SIL Repeat      v1              Appliance             4836
                                                Mall                   342
                SIL ZERO        v1              Appliance              490
                                                Mobile                  13
                SIL-Instore     v1

In [448]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'beta_cash_app_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [449]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_cash', product='CASH')

In [450]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=376356da-05a7-43c2-87c5-45ac4257ca7e>

In [451]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=e092bd7f-e1b8-46a0-adbd-d22171b62f05>

### FPD30

### Test

In [452]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  coalesce(SAFE_CAST(JSON_VALUE(p.prediction_clean, "$.combined_score") AS Float64)) AS beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory"))  trenchCategory
  from latest_request p
  left join model_run m on p.digitalLoanAccountId = m.digitalLoanAccountId
  ), 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (55, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2972716  f3ddbb3e-afea-4f96-861b-768c1abb7e5b    60829727160012   
1    3714015  577e2c33-6a05-4f5d-ac37-de55ae801b98    60837140150013   
2    2311054  f70db2ce-13de-48e0-8ea3-0ef3279fd38e    60823110540033   
3    3730944  acabba1e-4470-41d0-b943-fd46b34617af    60837309440027   
4    1242524  059f2133-161e-43bd-b5fa-0192e86991ab    60812425240046   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.539352   2025-09-29 09:20:58   
1  apps_score_cash             0.407089   2025-09-30 09:03:02   
2  apps_score_cash             0.515071   2025-10-09 10:48:02   
3  apps_score_cash             0.357790   2025-10-08 11:04:29   
4  apps_score_cash             0.458683   2025-10-01 21:40:29   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-09-29           2025-09           Test         0   
1       2025-09-30           2025-09           Test         0   
2       2025-10-09           2025-10           Test         0   
3       2025-10-08           2025-10           Test         0   
4       2025-10-01           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 1   
2                 1         Quick             v1       Trench 3   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [453]:
df1 = dfd.copy()

### Train

In [454]:
sq = """WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (59984, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1846363  8c3e7cfa-f3c6-4890-a885-a826b2c433f7    60818463630023   
1     1517405  9f21b1de-0674-43f6-8a08-fd4fd424be69    60815174050077   
2     1677927  578641c9-997f-4cad-aa51-345cd1d23a45    60816779270024   
3     1589324  95c074d7-efd0-4160-a36e-9349f7c91470    60815893240021   
4     1403048  ac894999-e7a3-4d4a-801f-0a81832b5b76    60814030480029   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.472817   2023-08-25 15:06:00   
1  apps_score_cash             0.473077   2023-03-09 13:02:57   
2  apps_score_cash             0.465629   2023-04-15 11:21:40   
3  apps_score_cash             0.472861   2023-03-13 17:22:54   
4  apps_score_cash             0.423100   2023-05-29 11:09:42   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2023-08-25           2023-08          Train         0   
1       2023-03-09           2023-03          Train         0   
2       2023-04-17           2023-04          Train         0   
3       2023-03-17           2023-03          Train         0   
4       2023-05-29           2023-05          Train         1   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1          Flex             v1       Trench 3   
1                 1          Flex             v1       Trench 3   
2                 1          Flex             v1       Trench 3   
3                 1          Flex             v1       Trench 3   
4                 1          Flex             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [455]:
df2 = dfd.copy()

### Concat

In [456]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (60039, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    2972716  f3ddbb3e-afea-4f96-861b-768c1abb7e5b    60829727160012   
1    3714015  577e2c33-6a05-4f5d-ac37-de55ae801b98    60837140150013   
2    2311054  f70db2ce-13de-48e0-8ea3-0ef3279fd38e    60823110540033   
3    3730944  acabba1e-4470-41d0-b943-fd46b34617af    60837309440027   
4    1242524  059f2133-161e-43bd-b5fa-0192e86991ab    60812425240046   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.539352   2025-09-29 09:20:58   
1  apps_score_cash             0.407089   2025-09-30 09:03:02   
2  apps_score_cash             0.515071   2025-10-09 10:48:02   
3  apps_score_cash             0.357790   2025-10-08 11:04:29   
4  apps_score_cash             0.458683   2025-10-01 21:40:29   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-09-29           2025-09           Test         0   
1       2025-09-30           2025-09           Test         0   
2       2025-10-09           2025-10           Test         0   
3       2025-10-08           2025-10           Test         0   
4       2025-10-01           2025-10           Test         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 1   
2                 1         Quick             v1       Trench 3   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [457]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Test            Quick           v1              not applicable          55
Train           ACL TSA         v1              not applicable        1401
                Flex            v1              not applicable         233
                Flex XL         v1              not applicable          10
                Flex-up         v1              not applicable       23921
                Quick           v1              not applicable       22096
                SIL Competitor  v1              Appliance             1219
                                                Mall                   127
                SIL Repeat      v1              Appliance             4835
                                                Mall                   342
                SIL ZERO        v1              Appliance              490
                                                Mobile                  13
                SIL-Instore     v1

In [458]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'beta_cash_app_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [459]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_cash', product='CASH')

In [460]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=56ab07cf-eba9-434d-b420-898dec6aed09>

In [461]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=aef5c859-fb76-4adf-a8f6-45964ccdce6d>

### FSPD30

### Test

In [462]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  coalesce(SAFE_CAST(JSON_VALUE(p.prediction_clean, "$.combined_score") AS Float64)) AS beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory"))  trenchCategory
  from latest_request p
  left join model_run m on p.digitalLoanAccountId = m.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, beta_cash_app_score, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffspd30, flg_mature_fspd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [463]:
df1 = dfd.copy()

### Train

In [464]:
sq = """WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  )
  , 
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (55594, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1762797  144dedce-1716-4cc2-951f-a50925dee594    60817627970031   
1     3427574  eb7e12e9-58a5-4af0-9bee-5a55e2d0fa92    60834275740026   
2     1992819  e791458e-c842-40f5-b920-a724fa4342c5    60819928190029   
3     2279162  fd46f286-62e3-49eb-b468-d38d4f6fc875    60822791620024   
4     2382039  6f54addf-63fa-4371-9e0b-855828ecae08    60823820390017   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.455775   2023-05-29 10:56:19   
1  apps_score_cash             0.545652   2025-07-14 20:11:09   
2  apps_score_cash             0.497108   2023-06-01 16:20:37   
3  apps_score_cash             0.328123   2024-01-03 17:39:17   
4  apps_score_cash             0.498382   2024-01-28 08:22:12   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2023-05-29           2023-05          Train          0   
1       2025-07-18           2025-07          Train          0   
2       2023-06-01           2023-06          Train          1   
3       2024-01-10           2024-01          Train          0   
4       2024-01-28           2024-01          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1          Flex             v1       Trench 3   
1                   1       Flex XL             v1       Trench 2   
2                   1          Flex             v1       Trench 3   
3                   1          Flex             v1       Trench 2   
4                   1          Flex             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [465]:
df2 = dfd.copy()

### Concat

In [466]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (55594, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     1762797  144dedce-1716-4cc2-951f-a50925dee594    60817627970031   
1     3427574  eb7e12e9-58a5-4af0-9bee-5a55e2d0fa92    60834275740026   
2     1992819  e791458e-c842-40f5-b920-a724fa4342c5    60819928190029   
3     2279162  fd46f286-62e3-49eb-b468-d38d4f6fc875    60822791620024   
4     2382039  6f54addf-63fa-4371-9e0b-855828ecae08    60823820390017   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.455775   2023-05-29 10:56:19   
1  apps_score_cash             0.545652   2025-07-14 20:11:09   
2  apps_score_cash             0.497108   2023-06-01 16:20:37   
3  apps_score_cash             0.328123   2024-01-03 17:39:17   
4  apps_score_cash             0.498382   2024-01-28 08:22:12   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2023-05-29           2023-05          Train          0   
1       2025-07-18           2025-07          Train          0   
2       2023-06-01           2023-06          Train          1   
3       2024-01-10           2024-01          Train          0   
4       2024-01-28           2024-01          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1          Flex             v1       Trench 3   
1                   1       Flex XL             v1       Trench 2   
2                   1          Flex             v1       Trench 3   
3                   1          Flex             v1       Trench 2   
4                   1          Flex             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [467]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Train           ACL TSA         v1              not applicable        1401
                Flex            v1              not applicable         233
                Flex XL         v1              not applicable          10
                Flex-up         v1              not applicable       22059
                Quick           v1              not applicable       20897
                SIL Competitor  v1              Appliance             1125
                                                Mall                   114
                SIL Repeat      v1              Appliance             3963
                                                Mall                   277
                SIL ZERO        v1              Appliance              469
                                                Mobile                  13
                SIL-Instore     v1              Appliance             4719
                                  

In [468]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'beta_cash_app_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [469]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_cash', product='CASH')

In [470]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=840e2951-3ad8-4618-aa19-b7cd3b008c53>

In [471]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=e87b83cc-9275-4a0d-9cb4-ecea3a9355e6>

### FSTPD30

### Test

In [472]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  coalesce(SAFE_CAST(JSON_VALUE(p.prediction_clean, "$.combined_score") AS Float64)) AS beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  p.modelVersionId,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory"))  trenchCategory
  from latest_request p
  left join model_run m on p.digitalLoanAccountId = m.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, beta_cash_app_score, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffstpd30, flg_mature_fstpd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [473]:
df1 = dfd.copy()

### Train

In [474]:
sq = """WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-AppScore-Model', 'apps_score_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction beta_cash_app_score,
  case when modelDisplayName like 'Beta-Cash-AppScore-Model' then 'apps_score_cash' else modelDisplayName end as modelDisplayName,
  modelVersionId,
  trenchCategory
  from parsed
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.beta_cash_app_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.beta_cash_app_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (50032, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2379068  30fad2a2-f110-4691-93d0-ab52e842f27d    60823790680015   
1     1104437  66fc2607-94bb-42fb-a7d8-16a00781d1b7    60811044370024   
2     1862224  97b6a0be-d903-40e4-9c88-63b278cbec48    60818622240027   
3     1606415  cc61a1e0-f7ed-4936-bf4d-31a2bd130d81    60816064150026   
4     1571073  b9bd3e08-ac19-4bd5-bd9e-1c5919421b23    60815710730023   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.321094   2024-01-25 09:05:47   
1  apps_score_cash             0.472966   2023-04-13 09:24:03   
2  apps_score_cash             0.514162   2023-03-04 10:51:44   
3  apps_score_cash             0.486978   2023-02-27 11:11:27   
4  apps_score_cash             0.504207   2023-05-02 09:03:51   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2024-02-05           2024-01          Train           1   
1       2023-04-13           2023-04          Train           0   
2       2023-03-04           2023-03          Train           0   
3       2023-02-27           2023-02          Train           0   
4       2023-05-02           2023-05          Train           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1          Flex             v1       Trench 1   
1                    1          Flex             v1       Trench 3   
2                    1          Flex             v1       Trench 3   
3                    1          Flex             v1       Trench 3   
4                    1          Flex             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [475]:
df2 = dfd.copy()

### Concat

In [476]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (50032, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2379068  30fad2a2-f110-4691-93d0-ab52e842f27d    60823790680015   
1     1104437  66fc2607-94bb-42fb-a7d8-16a00781d1b7    60811044370024   
2     1862224  97b6a0be-d903-40e4-9c88-63b278cbec48    60818622240027   
3     1606415  cc61a1e0-f7ed-4936-bf4d-31a2bd130d81    60816064150026   
4     1571073  b9bd3e08-ac19-4bd5-bd9e-1c5919421b23    60815710730023   

  modelDisplayName  beta_cash_app_score appln_submit_datetime  \
0  apps_score_cash             0.321094   2024-01-25 09:05:47   
1  apps_score_cash             0.472966   2023-04-13 09:24:03   
2  apps_score_cash             0.514162   2023-03-04 10:51:44   
3  apps_score_cash             0.486978   2023-02-27 11:11:27   
4  apps_score_cash             0.504207   2023-05-02 09:03:51   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2024-02-05           2024-01          Train           1   
1       2023-04-13           2023-04          Train           0   
2       2023-03-04           2023-03          Train           0   
3       2023-02-27           2023-02          Train           0   
4       2023-05-02           2023-05          Train           0   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1          Flex             v1       Trench 1   
1                    1          Flex             v1       Trench 3   
2                    1          Flex             v1       Trench 3   
3                    1          Flex             v1       Trench 3   
4                    1          Flex             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [477]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type   modelVersionId  loan_product_type
Train           ACL TSA         v1              not applicable        1401
                Flex            v1              not applicable         233
                Flex XL         v1              not applicable           8
                Flex-up         v1              not applicable       19404
                Quick           v1              not applicable       19477
                SIL Competitor  v1              Appliance             1016
                                                Mall                    88
                SIL Repeat      v1              Appliance             3043
                                                Mall                   204
                SIL ZERO        v1              Appliance              447
                                                Mobile                  13
                SIL-Instore     v1              Appliance             4418
                                  

In [478]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'beta_cash_app_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [479]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='apps_score_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (10476, 15)
The shape of the dimension table is:	 (136, 10)


In [480]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=e8a1b083-e248-4606-837d-69f91efa4e24>

In [481]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=31732595-9992-4459-b478-22cf18811209>

# Beta-Cash-Stack-Model

### FPD0

### Test

In [482]:

sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
and modelVersionId = 'v1'
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction AS Beta_cash_stack_score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (4147, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3728222  6fb8902e-fe57-42d2-9994-25a40b69ac75    60837282220019   
1    3526036  d14bfb96-1685-4da9-989f-7fffb94d96eb    60835260360019   
2    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
3    3450487  3f85a529-ed37-4e8e-a494-487058987b51    60834504870025   
4    3706434  48e3eccc-296c-4696-9d17-bf71a0640d53    60837064340011   

        modelDisplayName Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash   0.33776509992611536   2025-10-07 04:55:21   
1  beta_stack_model_cash    0.3397320576057747   2025-10-06 16:35:09   
2  beta_stack_model_cash   0.46852337037040115   2025-09-28 18:26:57   
3  beta_stack_model_cash    0.4963557547454851   2025-09-30 11:23:16   
4  beta_stack_model_cash    0.6167984129851222   2025-09-28 11:16:08   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-10-07           2025-10           Test        1                1   
1       2025-10-06           2025-10           Test        0                1   
2       2025-09-28           2025-09           Test        0                1   
3       2025-10-01           2025-09           Test        1                1   
4       2025-10-02           2025-09           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 2    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [483]:
df1 = dfd.copy()

### Train

In [484]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_cash_stack_score,
    case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else modelDisplayName end as modelDisplayName,
    modelVersionId,
  trenchCategory
  from parsed
  )
,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    deffpd0,
  flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and flg_mature_fpd0 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (38093, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2095371  c92f1171-d529-4542-9ccc-db5de0923fa1    60820953710023   
1     2934794  54614a81-b3df-4648-abab-e1592ccfb194    60829347940014   
2     2919026  34e24707-2447-490d-9226-a797eda64da2    60829190260011   
3     1792561  72dcbfcd-6a48-48ee-9b51-5e3b18b5ca2a    60817925610038   
4     2922752  f16fc686-2f25-48b0-ab11-8b6b0175e7ae    60829227520011   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.719737   2024-10-26 15:04:19   
1  beta_stack_model_cash               0.636466   2024-10-12 22:15:45   
2  beta_stack_model_cash               0.500973   2024-10-08 15:09:05   
3  beta_stack_model_cash               0.147136   2024-10-27 14:41:34   
4  beta_stack_model_cash               0.550913   2024-10-08 22:14:46   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2024-10-26           2024-10          Train        1                1   
1       2024-10-13           2024-10          Train        1                1   
2       2024-10-09           2024-10          Train        0                1   
3       2024-10-27           2024-10          Train        0                1   
4       2024-10-09           2024-10          Train        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 2    not applicable  
1         Quick             v1       Trench 1    not applicable  
2         Quick             v1       Trench 1    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [485]:
df2 = dfd.copy()

### Concat

In [486]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (42240, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3728222  6fb8902e-fe57-42d2-9994-25a40b69ac75    60837282220019   
1    3526036  d14bfb96-1685-4da9-989f-7fffb94d96eb    60835260360019   
2    1886335  883ef202-4aa4-41d7-99ff-fd6be2ef69db    60818863350053   
3    3450487  3f85a529-ed37-4e8e-a494-487058987b51    60834504870025   
4    3706434  48e3eccc-296c-4696-9d17-bf71a0640d53    60837064340011   

        modelDisplayName Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash   0.33776509992611536   2025-10-07 04:55:21   
1  beta_stack_model_cash    0.3397320576057747   2025-10-06 16:35:09   
2  beta_stack_model_cash   0.46852337037040115   2025-09-28 18:26:57   
3  beta_stack_model_cash    0.4963557547454851   2025-09-30 11:23:16   
4  beta_stack_model_cash    0.6167984129851222   2025-09-28 11:16:08   

  disbursementdate Application_month Data_selection  deffpd0  flg_mature_fpd0  \
0       2025-10-07           2025-10           Test        1                1   
1       2025-10-06           2025-10           Test        0                1   
2       2025-09-28           2025-09           Test        0                1   
3       2025-10-01           2025-09           Test        1                1   
4       2025-10-02           2025-09           Test        0                1   

  new_loan_type modelVersionId trenchCategory loan_product_type  
0         Quick             v1       Trench 1    not applicable  
1         Quick             v1       Trench 2    not applicable  
2         Quick             v1       Trench 3    not applicable  
3         Quick             v1       Trench 3    not applicable  
4         Quick             v1       Trench 1    not applicable

In [487]:
df_concat.columns

Index(['customerId', 'digitalLoanAccountId', 'loanAccountNumber',
       'modelDisplayName', 'Beta_cash_stack_score', 'appln_submit_datetime',
       'disbursementdate', 'Application_month', 'Data_selection', 'deffpd0',
       'flg_mature_fpd0', 'new_loan_type', 'modelVersionId', 'trenchCategory',
       'loan_product_type'],
      dtype='object')

In [488]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        4147
Train           Quick          v1              not applicable       38093
Name: digitalLoanAccountId, dtype: int64

In [489]:
df_concat['new_loan_type'].unique()

array(['Quick'], dtype=object)

In [490]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_cash_stack_score', 
    'deffpd0', 
    'FPD0',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [491]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (2344, 15)
The shape of the dimension table is:	 (32, 10)


In [492]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=8d346373-e4aa-4cd0-8bab-0b045d186632>

In [493]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=15ef2518-248b-4fb4-a122-22eae7e9c170>

### FPD10

### Test

In [494]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
and modelVersionId = 'v1'
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction AS Beta_cash_stack_score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd10,
  del.flg_mature_fpd0,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fpd0 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (4147, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3427045  399798f3-47e7-4cf6-8c2b-11b4a0afba4e    60834270450018   
1    3129817  df6278b7-1352-465f-a22d-fd7a93e92553    60831298170018   
2    2807107  67527945-fff7-4bb3-add4-a5a452bf9121    60828071070038   
3    2193432  154f68d6-e38e-4e17-bb35-a9d61de32168    60821934320027   
4    2972716  f3ddbb3e-afea-4f96-861b-768c1abb7e5b    60829727160012   

        modelDisplayName Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash    0.2944272257925552   2025-09-27 14:40:49   
1  beta_stack_model_cash   0.38819717862003145   2025-10-05 13:43:34   
2  beta_stack_model_cash   0.27462729854256773   2025-10-03 14:02:40   
3  beta_stack_model_cash    0.7925616629605761   2025-09-26 22:01:48   
4  beta_stack_model_cash    0.6812381103531799   2025-09-29 09:20:58   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-03           2025-09           Test         0   
1       2025-10-05           2025-10           Test         0   
2       2025-10-03           2025-10           Test         1   
3       2025-09-27           2025-09           Test         1   
4       2025-09-29           2025-09           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 2   
1                1         Quick             v1       Trench 2   
2                1         Quick             v1       Trench 3   
3                1         Quick             v1       Trench 3   
4                1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [495]:
df1 = dfd.copy()

### Train

In [496]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_cash_stack_score,
    case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else modelDisplayName end as modelDisplayName,
    modelVersionId,
  trenchCategory
  from parsed
  )
,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd10,
  del.flg_mature_fpd10,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fpd10 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (38091, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2930426  d70cda1e-dcff-4153-aa23-4202795b1106    60829304260017   
1     2158818  8aa80216-bb3d-44b3-9229-b382efb58de4    60821588180013   
2     2973018  68d63477-d602-4875-b161-af35469823ab    60829730180017   
3     1904948  605dbb9d-9939-4aa4-9238-b252da46e420    60819049480021   
4     2967699  0b519934-9ee3-4a4c-9e41-093606d0a065    60829676990013   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.555993   2024-10-15 10:01:17   
1  beta_stack_model_cash               0.550313   2024-10-21 10:53:44   
2  beta_stack_model_cash               0.725361   2024-10-27 13:34:48   
3  beta_stack_model_cash               0.448566   2024-10-09 00:20:22   
4  beta_stack_model_cash               0.454920   2024-10-24 06:38:41   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2024-10-15           2024-10          Train         0   
1       2024-10-21           2024-10          Train         0   
2       2024-10-27           2024-10          Train         1   
3       2024-10-09           2024-10          Train         1   
4       2024-10-24           2024-10          Train         0   

   flg_mature_fpd10 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 1   
1                 1         Quick             v1       Trench 2   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 3   
4                 1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [497]:
df2 = dfd.copy()

### Concat

In [498]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (42238, 16)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3427045  399798f3-47e7-4cf6-8c2b-11b4a0afba4e    60834270450018   
1    3129817  df6278b7-1352-465f-a22d-fd7a93e92553    60831298170018   
2    2807107  67527945-fff7-4bb3-add4-a5a452bf9121    60828071070038   
3    2193432  154f68d6-e38e-4e17-bb35-a9d61de32168    60821934320027   
4    2972716  f3ddbb3e-afea-4f96-861b-768c1abb7e5b    60829727160012   

        modelDisplayName Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash    0.2944272257925552   2025-09-27 14:40:49   
1  beta_stack_model_cash   0.38819717862003145   2025-10-05 13:43:34   
2  beta_stack_model_cash   0.27462729854256773   2025-10-03 14:02:40   
3  beta_stack_model_cash    0.7925616629605761   2025-09-26 22:01:48   
4  beta_stack_model_cash    0.6812381103531799   2025-09-29 09:20:58   

  disbursementdate Application_month Data_selection  deffpd10  \
0       2025-10-03           2025-09           Test         0   
1       2025-10-05           2025-10           Test         0   
2       2025-10-03           2025-10           Test         1   
3       2025-09-27           2025-09           Test         1   
4       2025-09-29           2025-09           Test         0   

   flg_mature_fpd0 new_loan_type modelVersionId trenchCategory  \
0                1         Quick             v1       Trench 2   
1                1         Quick             v1       Trench 2   
2                1         Quick             v1       Trench 3   
3                1         Quick             v1       Trench 3   
4                1         Quick             v1       Trench 2   

  loan_product_type  flg_mature_fpd10  
0    not applicable              <NA>  
1    not applicable              <NA>  
2    not applicable              <NA>  
3    not applicable              <NA>  
4    not applicable              <NA>

In [499]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable        4147
Train           Quick          v1              not applicable       38091
Name: digitalLoanAccountId, dtype: int64

In [500]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_cash_stack_score', 
    'deffpd10', 
    'FPD10',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))
C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\2123458924.py:16: RuntimeWarning: invalid value encountered in scalar divide
  gini = 1 - 2 * np.sum(cumsum_labels) / (n * np.sum(sorted_labels))


In [501]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_cash', product='CASH')

In [502]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=05b01c3f-f791-44a4-aed1-d70bba21a13a>

In [503]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=20bc8856-3c3f-45f7-88ef-1a9ba5b176f5>

### FPD30

### Test

In [504]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
and modelVersionId = 'v1'
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction AS Beta_cash_stack_score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (111, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3427045  399798f3-47e7-4cf6-8c2b-11b4a0afba4e    60834270450018   
1    1886292  08ce90dd-2e33-485b-88f3-b684c6bc63ae    60818862920033   
2    3713545  3d4efb65-52d5-4ff2-8740-8f499b6491c7    60837135450011   
3    3479077  628bb8f9-78bd-4a36-bd17-80d4f85852d9    60834790770019   
4    2642293  c81869ae-c522-4839-91a8-b8e7285e3c0f    60826422930033   

        modelDisplayName Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash    0.2944272257925552   2025-09-27 14:40:49   
1  beta_stack_model_cash    0.5436870222954989   2025-10-01 19:08:33   
2  beta_stack_model_cash    0.3864858913094533   2025-09-29 19:36:21   
3  beta_stack_model_cash    0.5279231050104731   2025-10-03 19:44:09   
4  beta_stack_model_cash    0.8619704556252671   2025-09-26 15:49:49   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-03           2025-09           Test         0   
1       2025-10-01           2025-10           Test         0   
2       2025-09-30           2025-09           Test         0   
3       2025-10-03           2025-10           Test         0   
4       2025-09-26           2025-09           Test         1   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 3   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 2   
4                 1         Quick             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [505]:
df1 = dfd.copy()

### Train

In [506]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_cash_stack_score,
    case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else modelDisplayName end as modelDisplayName,
    modelVersionId,
  trenchCategory
  from parsed
  )
,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffpd30,
  del.flg_mature_fpd30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fpd30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (38065, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2963570  3da434ca-81f6-43db-8f8a-bffa2f6ae3f2    60829635700011   
1     2987114  2b443475-c448-4eda-b206-ba1a2bcecea5    60829871140017   
2     2934979  f2aba3fb-56d9-4289-9fba-bd84644e5368    60829349790011   
3     2985765  7ea2e826-33c2-407b-8c5b-1f4e56ff6cc4    60829857650026   
4     2670636  267861d8-d7b9-4a27-a1cd-4dd2ba91695b    60826706360017   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.545035   2024-10-25 15:57:32   
1  beta_stack_model_cash               0.595169   2024-10-31 12:07:57   
2  beta_stack_model_cash               0.475053   2024-10-13 00:42:40   
3  beta_stack_model_cash               0.651783   2024-10-30 23:27:53   
4  beta_stack_model_cash               0.260578   2024-10-25 23:49:09   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2024-10-25           2024-10          Train         0   
1       2024-10-31           2024-10          Train         0   
2       2024-10-13           2024-10          Train         1   
3       2024-10-31           2024-10          Train         1   
4       2024-10-26           2024-10          Train         0   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 1   
1                 1         Quick             v1       Trench 1   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 1   
4                 1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [507]:
df2 = dfd.copy()

### Concat

In [508]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (38176, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0    3427045  399798f3-47e7-4cf6-8c2b-11b4a0afba4e    60834270450018   
1    1886292  08ce90dd-2e33-485b-88f3-b684c6bc63ae    60818862920033   
2    3713545  3d4efb65-52d5-4ff2-8740-8f499b6491c7    60837135450011   
3    3479077  628bb8f9-78bd-4a36-bd17-80d4f85852d9    60834790770019   
4    2642293  c81869ae-c522-4839-91a8-b8e7285e3c0f    60826422930033   

        modelDisplayName Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash    0.2944272257925552   2025-09-27 14:40:49   
1  beta_stack_model_cash    0.5436870222954989   2025-10-01 19:08:33   
2  beta_stack_model_cash    0.3864858913094533   2025-09-29 19:36:21   
3  beta_stack_model_cash    0.5279231050104731   2025-10-03 19:44:09   
4  beta_stack_model_cash    0.8619704556252671   2025-09-26 15:49:49   

  disbursementdate Application_month Data_selection  deffpd30  \
0       2025-10-03           2025-09           Test         0   
1       2025-10-01           2025-10           Test         0   
2       2025-09-30           2025-09           Test         0   
3       2025-10-03           2025-10           Test         0   
4       2025-09-26           2025-09           Test         1   

   flg_mature_fpd30 new_loan_type modelVersionId trenchCategory  \
0                 1         Quick             v1       Trench 2   
1                 1         Quick             v1       Trench 3   
2                 1         Quick             v1       Trench 1   
3                 1         Quick             v1       Trench 2   
4                 1         Quick             v1       Trench 3   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [509]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Test            Quick          v1              not applicable         111
Train           Quick          v1              not applicable       38065
Name: digitalLoanAccountId, dtype: int64

In [510]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_cash_stack_score', 
    'deffpd30', 
    'FPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [511]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_cash', product='CASH')

In [512]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=bacbfa07-a1f8-4b4b-9586-2d930168967b>

In [513]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=b93f1645-5c98-44e4-b682-fec78580de23>

### FSPD30

### Test

In [514]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
and modelVersionId = 'v1'
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction AS Beta_cash_stack_score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, Beta_cash_stack_score, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffspd30, flg_mature_fspd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [515]:
df1 = dfd.copy()

### Train

In [516]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_cash_stack_score,
    case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else modelDisplayName end as modelDisplayName,
    modelVersionId,
  trenchCategory
  from parsed
  )
,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffspd30,
  del.flg_mature_fspd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fspd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (35648, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2142046  52b312d4-ba99-4663-940b-23819858af58    60821420460014   
1     2513878  01d5f47c-260a-4abc-8a06-d388c44c3398    60825138780019   
2     2267444  4ebd86b0-2f1b-4261-853d-3d24447a6923    60822674440011   
3     2931608  c8668edd-f568-4ca2-a837-6cb49dc4ec21    60829316080015   
4     2960064  fada4367-e24e-4fbf-86e5-1c3f5b3161e1    60829600640016   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.537420   2024-10-25 20:14:06   
1  beta_stack_model_cash               0.821079   2024-10-07 15:06:51   
2  beta_stack_model_cash               0.177088   2024-10-22 19:57:26   
3  beta_stack_model_cash               0.704146   2024-10-11 19:34:52   
4  beta_stack_model_cash               0.301397   2024-10-21 10:16:10   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2024-10-25           2024-10          Train          1   
1       2024-10-09           2024-10          Train          1   
2       2024-10-23           2024-10          Train          1   
3       2024-10-13           2024-10          Train          1   
4       2024-10-21           2024-10          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1         Quick             v1       Trench 2   
1                   1         Quick             v1       Trench 2   
2                   1         Quick             v1       Trench 2   
3                   1         Quick             v1       Trench 1   
4                   1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [517]:
df2 = dfd.copy()

### Concat

In [518]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (35648, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2142046  52b312d4-ba99-4663-940b-23819858af58    60821420460014   
1     2513878  01d5f47c-260a-4abc-8a06-d388c44c3398    60825138780019   
2     2267444  4ebd86b0-2f1b-4261-853d-3d24447a6923    60822674440011   
3     2931608  c8668edd-f568-4ca2-a837-6cb49dc4ec21    60829316080015   
4     2960064  fada4367-e24e-4fbf-86e5-1c3f5b3161e1    60829600640016   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.537420   2024-10-25 20:14:06   
1  beta_stack_model_cash               0.821079   2024-10-07 15:06:51   
2  beta_stack_model_cash               0.177088   2024-10-22 19:57:26   
3  beta_stack_model_cash               0.704146   2024-10-11 19:34:52   
4  beta_stack_model_cash               0.301397   2024-10-21 10:16:10   

  disbursementdate Application_month Data_selection  deffspd30  \
0       2024-10-25           2024-10          Train          1   
1       2024-10-09           2024-10          Train          1   
2       2024-10-23           2024-10          Train          1   
3       2024-10-13           2024-10          Train          1   
4       2024-10-21           2024-10          Train          0   

   flg_mature_fspd_30 new_loan_type modelVersionId trenchCategory  \
0                   1         Quick             v1       Trench 2   
1                   1         Quick             v1       Trench 2   
2                   1         Quick             v1       Trench 2   
3                   1         Quick             v1       Trench 1   
4                   1         Quick             v1       Trench 1   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [519]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       35648
Name: digitalLoanAccountId, dtype: int64

In [520]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_cash_stack_score', 
    'deffspd30', 
    'FSPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [521]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_cash', product='CASH')

In [522]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=fe09ff14-dc14-42a2-abaf-4052d43ab294>

In [523]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=c11c55e9-a25b-426a-9403-4b37cef0c70a>

### FSTPD30

### Test

In [524]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
REPLACE(REPLACE(prediction, "'", '"'), "None", "null") AS prediction_clean
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details`
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
and modelVersionId = 'v1'
),
latest_request as (
select * from parsed
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelDisplayName ORDER BY start_time DESC ) = 1),

model_run as (
select customerId,digitalLoanAccountId,modelName, publish_time,
REPLACE(REPLACE(requestPayload, "'", '"'), "None", "null") AS requestPayload_clean
from `prj-prod-dataplatform.audit_balance.ml_request_details` 
WHERE modelName = 'Beta-Cash-Model-response'
QUALIFY ROW_NUMBER() OVER (PARTITION BY customerId, digitalLoanAccountId,modelName ORDER BY publish_time DESC ) = 1)
, 
  modelname as (
  select p.customerId,
  p.digitalLoanAccountId,
  start_time,
  prediction AS Beta_cash_stack_score,
  coalesce(p.trenchCategory, JSON_VALUE(m.requestPayload_clean, "$.predictions.trenchCategory")) AS trenchCategory,
  case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else p.modelDisplayName end as modelDisplayName,
  p.modelVersionId
  from latest_request p
  left join model_run m on m.digitalLoanAccountId = p.digitalLoanAccountId
  ),
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as 
  (select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Test' Data_selection,  
  del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId, trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
  from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
   left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select *  from base
  ;
"""
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()



The shape of the dataframe downloaded is:	 (0, 15)


Empty DataFrame
Columns: [customerId, digitalLoanAccountId, loanAccountNumber, modelDisplayName, Beta_cash_stack_score, appln_submit_datetime, disbursementdate, Application_month, Data_selection, deffstpd30, flg_mature_fstpd_30, new_loan_type, modelVersionId, trenchCategory, loan_product_type]
Index: []

In [525]:
df1 = dfd.copy()

### Train

In [526]:
sq = """
WITH parsed as (
select customerId, digitalLoanAccountId,modelDisplayName,modelVersionId,start_time,end_time,prediction,trenchCategory,
REPLACE(REPLACE(calcFeature, "'", '"'), "None", "null") AS calcFeatures,
FROM prj-prod-dataplatform.dap_ds_poweruser_playground.ml_training_model_run_details
where modelDisplayName in  ('Beta-Cash-Stack-Model', 'beta_stack_model_cash')
),
  modelname as (
  select customerId,
  digitalLoanAccountId,
  start_time,
  prediction Beta_cash_stack_score,
    case when modelDisplayName like 'Beta-Cash-Stack-Model' then 'beta_stack_model_cash' else modelDisplayName end as modelDisplayName,
    modelVersionId,
  trenchCategory
  from parsed
  )
,
  deliquency as
(select loanAccountNumber,
case when obs_min_inst_def0 >= 1 and min_inst_def0 = 1 then 1 else 0 end deffpd0,
case when obs_min_inst_def10 >=1 and min_inst_def10 =1 then 1 else 0 end deffpd10,
case when obs_min_inst_def30 >=1 and min_inst_def30 =1 then 1 else 0 end deffpd30,
case when obs_min_inst_def30 >=2 and min_inst_def30 in (1,2) then 1 else 0 end deffspd30,
case when obs_min_inst_def30 >=3 and min_inst_def30 in (1,2,3) then 1 else 0 end deffstpd30,
case when obs_min_inst_def0 >= 1 then 1 else 0 end flg_mature_fpd0,
case when obs_min_inst_def10 >=1 then 1 else 0 end flg_mature_fpd10,
case when obs_min_inst_def30 >=1 then 1 else 0 end flg_mature_fpd30,
case when obs_min_inst_def30 >=2 then 1 else 0 end flg_mature_fspd_30,
case when obs_min_inst_def30 >=3 then 1 else 0 end flg_mature_fstpd_30
from prj-prod-dataplatform.risk_credit_mis.loan_deliquency_data),
base as
(select r.customerId,
  r.digitalLoanAccountId,
  loanmaster.loanAccountNumber,
  r.modelDisplayName,
  r.Beta_cash_stack_score,
  coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime)) AS appln_submit_datetime,
  date(loanmaster.disbursementDateTime) disbursementdate,
  format_date('%Y-%m', coalesce(IF(loanmaster.new_loan_type = 'Flex-up', loanmaster.startApplyDateTime, loanmaster.termsAndConditionsSubmitDateTime),  cast(r.start_time as datetime))) as Application_month, 
  'Train' Data_selection,  
    del.deffstpd30,
  del.flg_mature_fstpd_30,
  loanmaster.new_loan_type,
  modelVersionId,
    trenchCategory,
    case when loanmaster.loantype='BNPL' and store_type =1 then 'Appliance'
    when loanmaster.loantype='BNPL' and store_type =2 then 'Mobile' 
    when loanmaster.loantype='BNPL' and store_type =3 then 'Mall' 
    when loanmaster.loantype='BNPL' and store_type not in (1,2,3) then store_tagging
    else 'not applicable' end as loan_product_type,
    from modelname r
  left join risk_credit_mis.loan_master_table loanmaster  ON loanmaster.digitalLoanAccountId = r.digitalLoanAccountId
  inner join deliquency del on del.loanAccountNumber = loanmaster.loanAccountNumber
  left join(SELECT DISTINCT mer_refferal_code, mer_name mer_name,store_type,store_tagging FROM `dl_loans_db_raw.tdbk_merchant_refferal_mtb`
  left join worktable_datachampions.TARGET_SPLIT P on P.STORE_NAME = mer_name
 qualify row_number() over(partition by mer_refferal_code order by  created_dt desc)=1) sil_category on loanmaster.purpleKey=sil_category.mer_refferal_code
  where loanmaster.flagDisbursement = 1
  and loanmaster.disbursementDateTime is not null
  and r.Beta_cash_stack_score is not null
  and del.flg_mature_fstpd_30 = 1
  )
  select * from base;
  """
dfd = client.query(sq).to_dataframe()
dfd = dfd.drop_duplicates(keep='first')
print(f"The shape of the dataframe downloaded is:\t {dfd.shape}")
dfd.head()

The shape of the dataframe downloaded is:	 (32499, 15)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2961024  c5953a65-53b6-4968-9300-9289f37645a1    60829610240012   
1     2689173  70c02608-2661-48ef-9d2c-032d8ae6294a    60826891730018   
2     2573609  a19dcfcf-3dd5-470c-8f60-93b15586d4cc    60825736090011   
3     2447359  2a6c5524-e8d5-4bb1-9cde-ef14daa7289d    60824473590024   
4     2492595  e0503248-96d4-4d35-8d6a-792a837cca49    60824925950011   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.404200   2024-10-21 14:32:02   
1  beta_stack_model_cash               0.910489   2024-10-29 17:47:08   
2  beta_stack_model_cash               0.415966   2024-10-03 19:06:26   
3  beta_stack_model_cash               0.473548   2024-10-06 18:30:35   
4  beta_stack_model_cash               0.447011   2024-10-19 12:42:54   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2024-10-21           2024-10          Train           1   
1       2024-10-29           2024-10          Train           1   
2       2024-10-03           2024-10          Train           1   
3       2024-10-06           2024-10          Train           1   
4       2024-10-19           2024-10          Train           1   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1         Quick             v1       Trench 1   
1                    1         Quick             v1       Trench 2   
2                    1         Quick             v1       Trench 2   
3                    1         Quick             v1       Trench 3   
4                    1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [527]:
df2 = dfd.copy()

### Concat

In [528]:
df_concat = pd.concat([df1, df2], ignore_index=True)
print(f"The shape of the concatenated dataframe is:\t {df_concat.shape}")
df_concat.head()

The shape of the concatenated dataframe is:	 (32499, 15)


C:\Users\Dwaipayan\AppData\Local\Temp\ipykernel_36596\3863462463.py:1: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_concat = pd.concat([df1, df2], ignore_index=True)


customerId                  digitalLoanAccountId loanAccountNumber  \
0     2961024  c5953a65-53b6-4968-9300-9289f37645a1    60829610240012   
1     2689173  70c02608-2661-48ef-9d2c-032d8ae6294a    60826891730018   
2     2573609  a19dcfcf-3dd5-470c-8f60-93b15586d4cc    60825736090011   
3     2447359  2a6c5524-e8d5-4bb1-9cde-ef14daa7289d    60824473590024   
4     2492595  e0503248-96d4-4d35-8d6a-792a837cca49    60824925950011   

        modelDisplayName  Beta_cash_stack_score appln_submit_datetime  \
0  beta_stack_model_cash               0.404200   2024-10-21 14:32:02   
1  beta_stack_model_cash               0.910489   2024-10-29 17:47:08   
2  beta_stack_model_cash               0.415966   2024-10-03 19:06:26   
3  beta_stack_model_cash               0.473548   2024-10-06 18:30:35   
4  beta_stack_model_cash               0.447011   2024-10-19 12:42:54   

  disbursementdate Application_month Data_selection  deffstpd30  \
0       2024-10-21           2024-10          Train           1   
1       2024-10-29           2024-10          Train           1   
2       2024-10-03           2024-10          Train           1   
3       2024-10-06           2024-10          Train           1   
4       2024-10-19           2024-10          Train           1   

   flg_mature_fstpd_30 new_loan_type modelVersionId trenchCategory  \
0                    1         Quick             v1       Trench 1   
1                    1         Quick             v1       Trench 2   
2                    1         Quick             v1       Trench 2   
3                    1         Quick             v1       Trench 3   
4                    1         Quick             v1       Trench 2   

  loan_product_type  
0    not applicable  
1    not applicable  
2    not applicable  
3    not applicable  
4    not applicable

In [529]:
df_concat.groupby(['Data_selection','new_loan_type', 'modelVersionId', 'loan_product_type'])['digitalLoanAccountId'].nunique()

Data_selection  new_loan_type  modelVersionId  loan_product_type
Train           Quick          v1              not applicable       32499
Name: digitalLoanAccountId, dtype: int64

In [530]:
fact_table, dimension_table = calculate_periodic_gini_prod_ver_trench_dimfact(
    df_concat, 
    'Beta_cash_stack_score', 
    'deffstpd30', 
    'FSTPD30',
    model_version_column='modelVersionId',
    trench_column='trenchCategory',
    loan_type_column='new_loan_type',
    loan_product_type_column='loan_product_type',
    account_id_column='digitalLoanAccountId'
)

In [531]:
fact_table, dimension_table = update_tables(fact_table, dimension_table, model_name='beta_stack_model_cash', product='CASH')
print(f"The shape of the fact table is:\t {fact_table.shape}")
print(f"The shape of the dimension table is:\t {dimension_table.shape}")

The shape of the fact table is:	 (1848, 15)
The shape of the dimension table is:	 (32, 10)


In [532]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.fact_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(fact_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=c484680b-0a78-4ba1-9213-7a9b011c1a44>

In [533]:
# Upload to BigQuery
table_id = "prj-prod-dataplatform.dap_ds_poweruser_playground.dimension_table"
job_config = bigquery.LoadJobConfig(
    write_disposition="WRITE_APPEND",  # or "WRITE_APPEND"
)
job = client.load_table_from_dataframe(dimension_table, table_id, job_config=job_config)
job.result()  # Wait for the job to complete

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\_pandas_helpers.py:483: FutureWarning: Loading pandas DataFrame into BigQuery will require pandas-gbq package version 0.26.1 or greater in the future. Tried to import pandas-gbq and got: No module named 'pandas_gbq'
  warnings.warn(


LoadJob<project=prj-prod-dataplatform, location=asia-southeast1, id=a6de5177-e9cf-4ec9-88b1-dc9245a21dfc>

# End